In [1]:
# CNT Five-Pillar Proof — All Simultaneous Mega Cell (v0.3, CNT_Lab-wired)
# Author: Telos x Oracle

import os, re, glob, math, json
import numpy as np, pandas as pd
from pathlib import Path
from typing import Tuple, Optional, Dict, List
from scipy.signal import welch, hilbert
from sklearn.metrics import roc_auc_score, precision_recall_curve, auc
from sklearn.linear_model import LogisticRegression
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline

# -------- Optional dependency for permutation entropy --------
try:
    import antropy as ant  # pip install antropy
except Exception:
    ant = None

# =============================
# 0) IO & Global Settings
# =============================
ROOT = Path(r"C:\Users\caleb\CNT_Lab").resolve()
OUT  = ROOT / "artifacts" / "cnt_five_pillars"
OUT.mkdir(parents=True, exist_ok=True)

# Known files from your recent logs (adjust as needed)
KNOWN = dict(
    eeg   = ROOT / r"artifacts\tables\migrated__cnt-eeg-labeled-all__68a51fca.csv",
    cooling = ROOT / r"notebooks\archive\cnt_cooling_log_20251015-123830_labeled.csv",
    wiki  = ROOT / r"artifacts\tables\wiki_views_labeled.csv",
    ising_glyph      = ROOT / r"data\sim\ising_glyph.csv",
    ising_random     = ROOT / r"data\sim\ising_random.csv",
    kuramoto_glyph   = ROOT / r"data\sim\kuramoto_glyph.csv",
    kuramoto_random  = ROOT / r"data\sim\kuramoto_random.csv",
    saddlenode_glyph = ROOT / r"data\sim\saddlenode_glyph.csv",
    saddlenode_random= ROOT / r"data\sim\saddlenode_random.csv",
)

# If a known path is missing, try to auto-discover a best candidate
def discover_file(patterns: List[str]) -> Optional[Path]:
    for pat in patterns:
        hits = list(ROOT.glob(pat))
        if hits:
            # pick most recent by modified time
            hits.sort(key=lambda p: p.stat().st_mtime, reverse=True)
            return hits[0]
    return None

def ensure_path(key: str, fallback_patterns: List[str]) -> Optional[Path]:
    p = KNOWN.get(key, None)
    if p and p.exists():
        return p
    cand = discover_file(fallback_patterns)
    return cand

DATASETS: Dict[str, Optional[Path]] = {
    "ising_glyph":     ensure_path("ising_glyph",     [r"data\sim\ising_glyph*.csv"]),
    "ising_random":    ensure_path("ising_random",    [r"data\sim\ising_random*.csv"]),
    "kuramoto_glyph":  ensure_path("kuramoto_glyph",  [r"data\sim\kuramoto_glyph*.csv"]),
    "kuramoto_random": ensure_path("kuramoto_random", [r"data\sim\kuramoto_random*.csv"]),
    "saddlenode_glyph":ensure_path("saddlenode_glyph",[r"data\sim\saddlenode_glyph*.csv"]),
    "saddlenode_random":ensure_path("saddlenode_random",[r"data\sim\saddlenode_random*.csv"]),
    "eeg":             ensure_path("eeg",   [r"artifacts\tables\migrated__cnt-eeg-labeled-all__*.csv",
                                             r"artifacts\tables\*eeg*labeled*.csv", r"artifacts\tables\*EEG*.csv"]),
    "cooling":         ensure_path("cooling",[r"notebooks\archive\cnt_*cooling*_labeled*.csv",
                                             r"notebooks\archive\*cooling*_labeled*.csv",
                                             r"artifacts\*\*cooling*.csv"]),
    "wiki":            ensure_path("wiki",  [r"artifacts\tables\*wiki*views*labeled*.csv",
                                             r"artifacts\tables\*wiki*.csv"]),
}

# Sampling rates (used only for spectral entropy). Tune if you know them.
FS_MAP = {
    "eeg": 256.0,      # common EEG fs
    "cooling": 100.0,  # nominal
    "wiki": 1.0,       # daily/step series; spectral entropy remains defined
    "ising_glyph": 100.0,
    "ising_random": 100.0,
    "kuramoto_glyph": 100.0,
    "kuramoto_random": 100.0,
    "saddlenode_glyph": 100.0,
    "saddlenode_random": 100.0,
}

LABEL_COL = "collapse_label"   # 0/1; optional
WIN  = 512                     # window length (samples)
STEP = 64                      # hop size
ALPHA = 1.25                   # RFI penalty weight
RISK_THRESHOLD = 0.60          # Oracle policy threshold
BUDGET_FRAC    = 0.10          # fraction of windows allowed to intervene

# =============================
# 1) Utility: windowing and helpers
# =============================
def rolling_windows(X: np.ndarray, win=WIN, step=STEP):
    T = X.shape[0]
    for start in range(0, max(T - win + 1, 0), step):
        yield start, X[start:start+win]

def safe_log(x, eps=1e-12):
    return np.log(np.clip(x, eps, None))

# =============================
# 2) Entropy & Coherence
# =============================
def spectral_entropy_sig(y, fs: float):
    f, Pxx = welch(y, fs=fs, nperseg=min(256, len(y)))
    P = Pxx / np.sum(Pxx) if np.sum(Pxx) > 0 else np.ones_like(Pxx)/len(Pxx)
    return -np.sum(P * safe_log(P)) / safe_log(len(P))

def permutation_entropy_sig(y, order=3, delay=1):
    if ant is not None:
        try:
            return ant.perm_entropy(y, order=order, delay=delay, normalize=True)
        except Exception:
            pass
    # Fallback: normalized histogram entropy
    hist, _ = np.histogram(y, bins=32, density=True)
    P = hist/np.sum(hist) if np.sum(hist)>0 else np.ones(32)/32
    return -np.sum(P*safe_log(P))/safe_log(len(P))

def entropy_matrix(Xw: np.ndarray, fs: float):
    se = np.mean([spectral_entropy_sig(Xw[:,i], fs=fs) for i in range(Xw.shape[1])])
    pe = np.mean([permutation_entropy_sig(Xw[:,i])         for i in range(Xw.shape[1])])
    return dict(H_spec=se, H_perm=pe, H=(se+pe)/2)

def plv_matrix(Xw: np.ndarray):
    # Phase locking value across channels
    Z = hilbert(Xw, axis=0)
    phases = np.angle(Z)
    n = phases.shape[1]
    vals = []
    for i in range(n):
        for j in range(i+1, n):
            dphi = phases[:,i] - phases[:,j]
            vals.append(np.abs(np.mean(np.exp(1j*dphi))))
    return dict(C_plv=np.mean(vals) if vals else np.nan)

def nmi_matrix(Xw: np.ndarray, bins=16):
    n = Xw.shape[1]
    vals = []
    for i in range(n):
        xi = Xw[:,i]
        hist_i, _ = np.histogram(xi, bins=bins); Pi = hist_i/np.sum(hist_i) if np.sum(hist_i)>0 else np.ones(bins)/bins
        Hi = -np.sum(Pi*safe_log(Pi))
        for j in range(i+1, n):
            xj = Xw[:,j]
            hist_j, _ = np.histogram(xj, bins=bins); Pj = hist_j/np.sum(hist_j) if np.sum(hist_j)>0 else np.ones(bins)/bins
            Hj = -np.sum(Pj*safe_log(Pj))
            H2, _, _ = np.histogram2d(xi, xj, bins=bins)
            Pij = H2/np.sum(H2) if np.sum(H2)>0 else np.ones((bins,bins))/(bins*bins)
            Hij = -np.sum(Pij*safe_log(Pij))
            Iij = Hi + Hj - Hij
            denom = max(Hi, Hj)
            if denom > 0: vals.append(Iij/denom)
    return dict(C_nmi=np.mean(vals) if vals else np.nan)

def coherence_features(Xw: np.ndarray):
    d = {}; d.update(plv_matrix(Xw)); d.update(nmi_matrix(Xw))
    Cvals = [v for k,v in d.items() if k.startswith('C_') and np.isfinite(v)]
    d['C'] = float(np.nanmean(Cvals)) if Cvals else np.nan
    return d

# =============================
# 3) RFI, dH and derivatives
# =============================
def finite_diff(arr: np.ndarray):
    arr = np.asarray(arr, float)
    d = np.diff(arr)
    d = np.concatenate([[np.nan], d])
    return d

def rfi_series(C, dH, alpha=ALPHA):
    dHpos = np.maximum(0.0, np.asarray(dH))
    return np.asarray(C) * np.exp(-alpha * dHpos)

# =============================
# 4) Invariants & Curvature Proxy
# =============================
def graph_from_corr(Xw: np.ndarray, thresh=0.4):
    R = np.corrcoef(Xw.T)
    np.fill_diagonal(R, 0.0)
    edges = (np.abs(R) >= thresh).astype(int)
    return edges

def invariant_features(Xw: np.ndarray, thresh=0.4):
    A = graph_from_corr(Xw, thresh)
    V = A.shape[0]
    E = int(A.sum()//2)
    # Connected components (β0)
    unvisited = set(range(V))
    comps = 0
    while unvisited:
        stack = [unvisited.pop()]; comps += 1
        while stack:
            u = stack.pop()
            nbrs = list(np.where(A[u]>0)[0])
            for v in nbrs:
                if v in unvisited:
                    unvisited.remove(v); stack.append(v)
    beta0 = comps
    # Cyclomatic number ~ β1
    beta1 = E - V + comps
    return dict(I_beta0=beta0, I_beta1=beta1, I_cyclomatic=beta1)

def curvature_proxy(Xw: np.ndarray):
    Xc = Xw - Xw.mean(0, keepdims=True)
    Cov = np.cov(Xc.T)
    eps = 1e-6
    Cov = Cov + eps*np.eye(Cov.shape[0])
    sign, logdet = np.linalg.slogdet(Cov)
    neg_logdet = -logdet  # larger => more "negative curvature" proxy (instability)
    return dict(R_tilde=neg_logdet)

# =============================
# 5) Oracle: features, risk model, closed-loop
# =============================
def make_features_df(X: np.ndarray, fs: float, win=WIN, step=STEP, labels=None, ds_name=""):
    rows = []
    for t0, Xw in rolling_windows(X, win, step):
        ent = entropy_matrix(Xw, fs=fs)
        coh = coherence_features(Xw)
        invv = invariant_features(Xw)
        curv = curvature_proxy(Xw)
        row = dict(t0=t0, **ent, **coh, **invv, **curv)
        rows.append(row)
    df = pd.DataFrame(rows).sort_values("t0").reset_index(drop=True)
    df["dH"]  = finite_diff(df["H"].values)
    df["RFI"] = rfi_series(df["C"].values, df["dH"].values, ALPHA)
    if labels is not None and len(labels) >= int(df["t0"].iloc[-1] + win):
        center = (df["t0"] + win//2).astype(int)
        y = np.array(labels)[np.clip(center, 0, len(labels)-1)]
        df["y"] = y.astype(int)
    df["dataset"] = ds_name
    return df

def train_oracle(df: pd.DataFrame):
    use_cols = [c for c in ["RFI","dH","C","R_tilde","I_beta0","I_beta1","H"] if c in df]
    dtrain = df.dropna(subset=use_cols + (["y"] if "y" in df else []))
    if "y" not in dtrain or dtrain["y"].nunique()<2:
        return None, use_cols
    X = dtrain[use_cols].values
    y = dtrain["y"].values
    pipe = Pipeline([("scaler", StandardScaler()),
                     ("clf", LogisticRegression(max_iter=400))])
    pipe.fit(X, y)
    return pipe, use_cols

def closed_loop_policy(df: pd.DataFrame, model, use_cols,
                       risk_thr=RISK_THRESHOLD, budget_frac=BUDGET_FRAC):
    df = df.copy()
    if model is None or not use_cols:
        df["risk"] = np.nan; df["intervene"] = 0
        return df
    X = df[use_cols].values
    risk = model.predict_proba(X)[:,1]
    df["risk"] = risk
    # budget-constrained top-k above threshold
    kmax = int(budget_frac * len(df))
    idx = np.where(risk >= risk_thr)[0]
    sel = idx[np.argsort(risk[idx])[-kmax:]] if len(idx) > kmax else idx
    mask = np.zeros(len(df), dtype=int); mask[sel] = 1
    df["intervene"] = mask
    return df

# =============================
# 6) Evaluation
# =============================
def eval_metrics(df: pd.DataFrame, label_col="y"):
    out = {}
    if label_col in df.columns and df[label_col].nunique()>1 and df["risk"].notna().any():
        y = df[label_col].values
        r = df["risk"].values
        out["AUC_risk"] = float(roc_auc_score(y, r))
        P, R, T = precision_recall_curve(y, r)
        out["AUPRC_risk"] = float(auc(R, P))
        pol = df[df["intervene"]==1]
        if len(pol)>0:
            out["Precision_policy"] = float(((pol[label_col]==1).sum())/len(pol))
        out["Corr_RFI_y"] = float(pd.Series(df["RFI"]).corr(pd.Series(1-y)))
    # C-pillar: invariant vs metric drift
    if {"I_beta0","I_beta1","H","C"}.issubset(df.columns):
        dI = np.abs(np.gradient(df["I_beta0"].values)) + np.abs(np.gradient(df["I_beta1"].values))
        dM = np.abs(np.gradient(df["H"].values))      + np.abs(np.gradient(df["C"].values))
        out["Invariant_vs_Metric_Drift"] = float(np.nanmean(dI) / np.nanmean(dM))
    # G-pillar: geometry relation
    if {"R_tilde","RFI"}.issubset(df.columns):
        out["Corr_Rtilde_RFI"] = float(pd.Series(df["R_tilde"]).corr(pd.Series(df["RFI"])))
    return out

# =============================
# 7) Runner
# =============================
def load_wide(path: Path) -> Tuple[Optional[np.ndarray], Optional[np.ndarray]]:
    if not path or not path.exists():
        return None, None
    df = pd.read_csv(path)
    y = df[LABEL_COL].values.astype(int) if LABEL_COL in df.columns else None
    X = df.select_dtypes(include=[np.number]).drop(columns=[LABEL_COL], errors='ignore').values
    if X.ndim == 1: X = X[:,None]
    return X, y

def process_dataset(name: str, path: Optional[Path], fs_map: Dict[str,float]):
    if path is None:
        print(f"[skip] {name} (not found)")
        return None, None, None
    X, y = load_wide(path)
    if X is None:
        print(f"[skip] {name} (unloadable: {path})")
        return None, None, None
    fs = fs_map.get(name, 100.0)
    dff = make_features_df(X, fs=fs, labels=y, ds_name=name)
    model, use_cols = train_oracle(dff)
    dff_open = dff.copy(); dff_open["risk"] = np.nan; dff_open["intervene"] = 0
    dff_closed = closed_loop_policy(dff, model, use_cols)
    m_open  = eval_metrics(dff_open)
    m_close = eval_metrics(dff_closed)
    return dff_closed, m_open, m_close

# =============================
# 8) Execute across CNT_Lab
# =============================
all_metrics = []
all_frames  = []

print(f"[ROOT] {ROOT}")
for name, path in DATASETS.items():
    dff, m_open, m_close = process_dataset(name, path, FS_MAP)
    if dff is None:
        continue
    out_csv = OUT / f"features_{name}.csv"
    dff.to_csv(out_csv, index=False)
    row = dict(dataset=name,
               **{f"open::{k}":v for k,v in (m_open  or {}).items()},
               **{f"closed::{k}":v for k,v in (m_close or {}).items()},
               source=str(path))
    all_metrics.append(row)
    all_frames.append(dff.assign(run=name))

if all_metrics:
    tab = pd.DataFrame(all_metrics).sort_values("dataset")
    tab.to_csv(OUT/"verdict_table.csv", index=False)
    print("\n== Verdict Table ==")
    print(tab.fillna("").to_string(index=False))

    # Glyph vs Random pairings (expect glyph >= random)
    def pair_cmp(metric_key: str):
        rows = []
        for sys in ["ising","kuramoto","saddlenode"]:
            g = tab[tab["dataset"].eq(f"{sys}_glyph")][metric_key].values
            r = tab[tab["dataset"].eq(f"{sys}_random")][metric_key].values
            if len(g)==1 and len(r)==1:
                rows.append(dict(system=sys, metric=metric_key,
                                 glyph=float(g[0]), random=float(r[0]),
                                 diff=float(g[0])-float(r[0])))
        return pd.DataFrame(rows)

    for key in ["closed::AUC_risk","closed::Precision_policy","closed::Corr_RFI_y"]:
        if key in tab.columns:
            cmp = pair_cmp(key)
            if len(cmp):
                cmp.to_csv(OUT/f"pair_{key.replace('::','_')}.csv", index=False)
                print(f"\n== Pairing on {key} ==")
                print(cmp.to_string(index=False))

# C-pillar summary (invariant vs metric drift) across all datasets
if all_frames:
    big = pd.concat(all_frames, ignore_index=True)
    cstat = big.groupby("dataset")["Invariant_vs_Metric_Drift"].mean().reset_index()
    cstat.to_csv(OUT/"invariant_vs_metric_drift.csv", index=False)
    print("\n== Invariant vs Metric Drift (mean ratio; <1 is good) ==")
    print(cstat.to_string(index=False))

print(f"\nArtifacts written to: {OUT}")


[ROOT] C:\Users\caleb\CNT_Lab
[skip] ising_glyph (not found)
[skip] ising_random (not found)
[skip] kuramoto_glyph (not found)
[skip] kuramoto_random (not found)
[skip] saddlenode_glyph (not found)
[skip] saddlenode_random (not found)


KeyError: 't0'

In [2]:
# === HOTFIX v0.3.1: adaptive windows + empty-rows guard, then re-run ===

# 1) Override make_features_df with adaptive WIN/STEP and single-window fallback
def make_features_df(X: np.ndarray, fs: float, win=WIN, step=STEP, labels=None, ds_name=""):
    T = int(X.shape[0])
    # Adapt window/step if the series is short
    if T <= 0:
        print(f"[skip] {ds_name} is empty (T=0)")
        return pd.DataFrame()
    if T < win:
        local_win  = max(8, min(win, T))                 # never exceed T
        local_step = max(1, min(step, max(1, local_win//4)))
        print(f"[adapt] {ds_name}: T={T} < WIN={win} → using WIN={local_win}, STEP={local_step}")
    else:
        local_win, local_step = win, step

    rows = []
    for t0, Xw in rolling_windows(X, local_win, local_step):
        ent  = entropy_matrix(Xw, fs=fs)
        coh  = coherence_features(Xw)
        invv = invariant_features(Xw)
        curv = curvature_proxy(Xw)
        rows.append(dict(t0=t0, **ent, **coh, **invv, **curv))

    # If still no rows (e.g., extremely short series), compute one full-window row
    if not rows:
        ent  = entropy_matrix(X, fs=fs)
        coh  = coherence_features(X)
        invv = invariant_features(X)
        curv = curvature_proxy(X)
        rows = [dict(t0=0, **ent, **coh, **invv, **curv)]
        print(f"[fallback] {ds_name}: single full-window features (T={T})")

    df = pd.DataFrame(rows).sort_values("t0").reset_index(drop=True)
    df["dH"]  = finite_diff(df["H"].values)
    # If coherence couldn't be estimated (NaNs for single-channel), set C to 0 for RFI
    C_clean = np.nan_to_num(df["C"].values, nan=0.0, posinf=0.0, neginf=0.0)
    df["RFI"] = rfi_series(C_clean, df["dH"].values, ALPHA)

    # Attach labels if available & long enough; otherwise skip
    if labels is not None and len(labels) >= int(df["t0"].iloc[-1] + local_win):
        centers = (df["t0"] + local_win//2).astype(int)
        y = np.array(labels)[np.clip(centers, 0, len(labels)-1)]
        df["y"] = y.astype(int)

    df["dataset"] = ds_name
    df.attrs["WIN_used"]  = local_win
    df.attrs["STEP_used"] = local_step
    return df

# 2) Re-run execution across whatever datasets are present
all_metrics = []
all_frames  = []

print(f"[ROOT] {ROOT}")
for name, path in DATASETS.items():
    dff, m_open, m_close = process_dataset(name, path, FS_MAP)
    if dff is None or dff.empty:
        continue
    out_csv = OUT / f"features_{name}.csv"
    dff.to_csv(out_csv, index=False)
    row = dict(dataset=name,
               **{f"open::{k}":v for k,v in (m_open  or {}).items()},
               **{f"closed::{k}":v for k,v in (m_close or {}).items()},
               source=str(path))
    all_metrics.append(row)
    all_frames.append(dff.assign(run=name))

if all_metrics:
    tab = pd.DataFrame(all_metrics).sort_values("dataset")
    tab.to_csv(OUT/"verdict_table.csv", index=False)
    print("\n== Verdict Table ==")
    print(tab.fillna("").to_string(index=False))

    def pair_cmp(metric_key: str):
        rows = []
        for sys in ["ising","kuramoto","saddlenode"]:
            if metric_key in tab.columns:
                g = tab[tab["dataset"].eq(f"{sys}_glyph")][metric_key].values
                r = tab[tab["dataset"].eq(f"{sys}_random")][metric_key].values
                if len(g)==1 and len(r)==1:
                    rows.append(dict(system=sys, metric=metric_key,
                                     glyph=float(g[0]), random=float(r[0]),
                                     diff=float(g[0])-float(r[0])))
        return pd.DataFrame(rows)

    for key in ["closed::AUC_risk","closed::Precision_policy","closed::Corr_RFI_y"]:
        cmp = pair_cmp(key)
        if len(cmp):
            cmp.to_csv(OUT/f"pair_{key.replace('::','_')}.csv", index=False)
            print(f"\n== Pairing on {key} ==\n", cmp.to_string(index=False))

if all_frames:
    big = pd.concat(all_frames, ignore_index=True)
    cstat = big.groupby("dataset")["Invariant_vs_Metric_Drift"].mean().reset_index()
    cstat.to_csv(OUT/"invariant_vs_metric_drift.csv", index=False)
    print("\n== Invariant vs Metric Drift (mean ratio; <1 is good) ==")
    print(cstat.to_string(index=False))

print(f"\nArtifacts written to: {OUT}")


[ROOT] C:\Users\caleb\CNT_Lab
[skip] ising_glyph (not found)
[skip] ising_random (not found)
[skip] kuramoto_glyph (not found)
[skip] kuramoto_random (not found)
[skip] saddlenode_glyph (not found)
[skip] saddlenode_random (not found)
[adapt] eeg: T=488 < WIN=512 → using WIN=488, STEP=64


C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3065: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3066: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]


ValueError: Shape of array too small to calculate a numerical gradient, at least (edge_order + 1) elements are required.

In [3]:
# CNT Five-Pillar Proof — Mega Cell (v0.4 "Scrubber Edition")
# Scans entire CNT_Lab, scores every time-series it finds, and writes verdicts.
# Author: Telos x Oracle

import os, re, math, json, warnings
from pathlib import Path
from typing import Tuple, Optional, Dict, List

import numpy as np
import pandas as pd

from scipy.signal import welch, hilbert
from sklearn.metrics import roc_auc_score, precision_recall_curve, auc
from sklearn.linear_model import LogisticRegression
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline

warnings.filterwarnings("ignore", category=FutureWarning)

# Optional: permutation entropy (pip install antropy)
try:
    import antropy as ant
except Exception:
    ant = None

# =============================
# 0) Config — edit if needed
# =============================
ROOT = Path(r"C:\Users\caleb\CNT_Lab").resolve()
SEARCH_DIRS = [ROOT, ROOT / "notebooks" / "archive"]  # recursive
FILE_PATTERNS = ["**/*.csv", "**/*.parquet"]

OUT  = ROOT / "artifacts" / "cnt_five_pillars"
OUT.mkdir(parents=True, exist_ok=True)

# Windowing / policy
WIN_DEFAULT  = 512
STEP_DEFAULT = 64
ALPHA        = 1.25         # RFI penalty weight
RISK_THRESHOLD = 0.60       # Oracle policy threshold
BUDGET_FRAC    = 0.10       # fraction of windows allowed to intervene

# Limits / guards
CHANNEL_MAX   = 32          # max numeric channels to use per file
MIN_T         = 64          # minimal rows to attempt windowing
FILE_MAX_ROWS = 2_000_000   # skip ultra-huge files (guard)
CSV_READ_KW   = dict(low_memory=False)  # tweak if needed

# Label candidates (binary; we map truthy to 1)
LABEL_CANDIDATES = [
    "collapse_label","label","y","event","is_event","collapse","is_collapse","target"
]

# FS inference defaults
FS_DEFAULT = 100.0  # used if we can't infer from time column
TIME_COL_CANDIDATES = ["time","timestamp","datetime","date","ts"]

# =============================
# 1) File discovery
# =============================
def discover_files(dirs: List[Path], patterns: List[str]) -> List[Path]:
    hits = []
    for d in dirs:
        if not d.exists():
            continue
        for pat in patterns:
            hits.extend(d.glob(pat))
    # unique and sort by path
    uniq = sorted(list({p.resolve() for p in hits}))
    return uniq

# =============================
# 2) FS inference
# =============================
def infer_fs(df: pd.DataFrame) -> float:
    # Try to infer FS from a timestamp-like column
    # 1) exact datetime cols
    for c in df.columns:
        if np.issubdtype(df[c].dtype, np.datetime64):
            s = df[c].dropna()
            if len(s) >= 3:
                dt = s.sort_values().diff().dt.total_seconds().dropna()
                if len(dt) and dt.median() > 0:
                    return float(1.0 / dt.median())
    # 2) parse likely time columns
    for name in TIME_COL_CANDIDATES:
        cols = [c for c in df.columns if c.lower() == name]
        for c in cols:
            s = df[c].dropna()
            # try parse as datetime
            try:
                dt = pd.to_datetime(s, errors="raise")
                dsec = dt.sort_values().diff().dt.total_seconds().dropna()
                if len(dsec) and dsec.median() > 0:
                    return float(1.0 / dsec.median())
            except Exception:
                pass
            # try numeric time with (approx) seconds
            if pd.api.types.is_numeric_dtype(s):
                dnum = s.sort_values().diff().dropna()
                med = float(dnum.median()) if len(dnum) else 0.0
                if med > 0:
                    return float(1.0 / med)
    return FS_DEFAULT

# =============================
# 3) Label extraction (binary)
# =============================
def extract_labels(df: pd.DataFrame) -> Tuple[Optional[np.ndarray], Optional[str]]:
    for c in df.columns:
        if c.lower() in LABEL_CANDIDATES:
            y = df[c]
            # map truthy to 1, else 0
            if y.dtype == bool:
                yb = y.astype(int).values
            elif pd.api.types.is_numeric_dtype(y):
                # assume already 0/1 or threshold at >0
                yb = (y.astype(float).values > 0).astype(int)
            else:
                # text labels
                yb = y.astype(str).str.strip().str.lower().isin(
                    {"1","true","yes","y","t","event","collapse"}
                ).astype(int).values
            return yb, c
    return None, None

# =============================
# 4) Core metrics and helpers
# =============================
def safe_log(x, eps=1e-12):
    return np.log(np.clip(x, eps, None))

def spectral_entropy_sig(y, fs: float):
    from scipy.signal import welch
    f, Pxx = welch(y, fs=fs, nperseg=min(256, len(y)))
    P = Pxx / np.sum(Pxx) if np.sum(Pxx) > 0 else np.ones_like(Pxx)/len(Pxx)
    return -np.sum(P * safe_log(P)) / safe_log(len(P))

def permutation_entropy_sig(y, order=3, delay=1):
    if ant is not None:
        try:
            return ant.perm_entropy(y, order=order, delay=delay, normalize=True)
        except Exception:
            pass
    hist, _ = np.histogram(y, bins=32, density=True)
    P = hist/np.sum(hist) if np.sum(hist)>0 else np.ones(32)/32
    return -np.sum(P*safe_log(P))/safe_log(len(P))

def entropy_matrix(Xw: np.ndarray, fs: float):
    se = np.mean([spectral_entropy_sig(Xw[:,i], fs=fs) for i in range(Xw.shape[1])])
    pe = np.mean([permutation_entropy_sig(Xw[:,i])       for i in range(Xw.shape[1])])
    return dict(H_spec=se, H_perm=pe, H=(se+pe)/2)

def plv_matrix(Xw: np.ndarray):
    Z = hilbert(Xw, axis=0)
    ph = np.angle(Z)
    n  = ph.shape[1]
    vals=[]
    for i in range(n):
        for j in range(i+1,n):
            dphi = ph[:,i]-ph[:,j]
            vals.append(np.abs(np.mean(np.exp(1j*dphi))))
    return dict(C_plv=np.mean(vals) if vals else np.nan)

def nmi_matrix(Xw: np.ndarray, bins=16):
    n  = Xw.shape[1]
    vals=[]
    for i in range(n):
        xi = Xw[:,i]
        hi,_ = np.histogram(xi,bins=bins); Pi=hi/np.sum(hi) if np.sum(hi)>0 else np.ones(bins)/bins
        Hi = -np.sum(Pi*safe_log(Pi))
        for j in range(i+1,n):
            xj = Xw[:,j]
            hj,_ = np.histogram(xj,bins=bins); Pj=hj/np.sum(hj) if np.sum(hj)>0 else np.ones(bins)/bins
            Hj = -np.sum(Pj*safe_log(Pj))
            H2,_,_ = np.histogram2d(xi,xj,bins=bins)
            Pij = H2/np.sum(H2) if np.sum(H2)>0 else np.ones((bins,bins))/(bins*bins)
            Hij = -np.sum(Pij*safe_log(Pij))
            Iij = Hi + Hj - Hij
            denom = max(Hi, Hj)
            if denom>0: vals.append(Iij/denom)
    return dict(C_nmi=np.mean(vals) if vals else np.nan)

def coherence_features(Xw: np.ndarray):
    d = {}; d.update(plv_matrix(Xw)); d.update(nmi_matrix(Xw))
    Cvals = [v for k,v in d.items() if k.startswith("C_") and np.isfinite(v)]
    d["C"] = float(np.nanmean(Cvals)) if Cvals else 0.0
    return d

def finite_diff(arr: np.ndarray):
    arr = np.asarray(arr, float)
    d = np.diff(arr)
    return np.concatenate([[np.nan], d])

def rfi_series(C, dH, alpha=ALPHA):
    C = np.nan_to_num(C, nan=0.0, posinf=0.0, neginf=0.0)
    dHpos = np.maximum(0.0, np.asarray(dH))
    return np.asarray(C) * np.exp(-alpha * dHpos)

def graph_from_corr(Xw: np.ndarray, thresh=0.4):
    R = np.corrcoef(Xw.T)
    np.fill_diagonal(R, 0.0)
    edges = (np.abs(R) >= thresh).astype(int)
    return edges

def invariant_features(Xw: np.ndarray, thresh=0.4):
    A = graph_from_corr(Xw, thresh)
    V = A.shape[0]
    E = int(A.sum()//2)
    # components (β0)
    un = set(range(V)); comps=0
    while un:
        stack=[un.pop()]; comps+=1
        while stack:
            u=stack.pop()
            nbr=list(np.where(A[u]>0)[0])
            for v in nbr:
                if v in un: un.remove(v); stack.append(v)
    beta0 = comps
    beta1 = E - V + comps   # cyclomatic number ~ β1
    return dict(I_beta0=beta0, I_beta1=beta1, I_cyclomatic=beta1)

def curvature_proxy(Xw: np.ndarray):
    Xc  = Xw - Xw.mean(0, keepdims=True)
    Cov = np.cov(Xc.T)
    Cov = Cov + 1e-6*np.eye(Cov.shape[0])
    sign, logdet = np.linalg.slogdet(Cov)
    return dict(R_tilde = -logdet)

# =============================
# 5) Windowed features + Oracle
# =============================
def rolling_windows(X: np.ndarray, win, step):
    T = X.shape[0]
    for start in range(0, max(T - win + 1, 0), step):
        yield start, X[start:start+win]

def make_features_df(X: np.ndarray, fs: float, ds_name:str,
                     win:int=WIN_DEFAULT, step:int=STEP_DEFAULT,
                     labels:Optional[np.ndarray]=None) -> pd.DataFrame:
    T = int(X.shape[0])
    if T <= 0:
        print(f"[skip] {ds_name} empty (T=0)")
        return pd.DataFrame()

    # adaptive window for short series
    if T < win:
        win  = max(8, min(win, T))
        step = max(1, min(step, max(1, win//4)))
        print(f"[adapt] {ds_name}: T={T} < WIN -> using WIN={win}, STEP={step}")

    rows=[]
    for t0, Xw in rolling_windows(X, win, step):
        ent  = entropy_matrix(Xw, fs=fs)
        coh  = coherence_features(Xw)
        invv = invariant_features(Xw)
        curv = curvature_proxy(Xw)
        rows.append(dict(t0=t0, **ent, **coh, **invv, **curv))

    if not rows:
        # single full-window fallback
        ent  = entropy_matrix(X, fs=fs)
        coh  = coherence_features(X)
        invv = invariant_features(X)
        curv = curvature_proxy(X)
        rows = [dict(t0=0, **ent, **coh, **invv, **curv)]
        print(f"[fallback] {ds_name}: single full-window features (T={T})")

    df = pd.DataFrame(rows).sort_values("t0").reset_index(drop=True)
    df["dH"]  = finite_diff(df["H"].values)
    df["RFI"] = rfi_series(df["C"].values, df["dH"].values, ALPHA)

    # align labels to window centers if available
    if labels is not None and len(labels) >= int(df["t0"].iloc[-1] + win):
        centers = (df["t0"] + win//2).astype(int)
        y = np.array(labels)[np.clip(centers, 0, len(labels)-1)]
        df["y"] = y.astype(int)

    df["dataset"] = ds_name
    df.attrs["WIN_used"]  = win
    df.attrs["STEP_used"] = step
    return df

def train_oracle(df: pd.DataFrame):
    use_cols = [c for c in ["RFI","dH","C","R_tilde","I_beta0","I_beta1","H"] if c in df]
    dtrain = df.dropna(subset=use_cols + (["y"] if "y" in df else []))
    if "y" not in dtrain or dtrain["y"].nunique() < 2:
        return None, use_cols
    X = dtrain[use_cols].values
    y = dtrain["y"].values
    pipe = Pipeline([
        ("scaler", StandardScaler()),
        ("clf", LogisticRegression(max_iter=400))
    ])
    pipe.fit(X, y)
    return pipe, use_cols

def closed_loop_policy(df: pd.DataFrame, model, use_cols,
                       risk_thr=RISK_THRESHOLD, budget_frac=BUDGET_FRAC):
    df = df.copy()
    if model is None or not use_cols:
        df["risk"] = np.nan; df["intervene"]=0
        return df
    X = df[use_cols].values
    risk = model.predict_proba(X)[:,1]
    df["risk"] = risk
    kmax = int(budget_frac * len(df))
    idx  = np.where(risk >= risk_thr)[0]
    sel  = idx[np.argsort(risk[idx])[-kmax:]] if len(idx) > kmax else idx
    mask = np.zeros(len(df), dtype=int); mask[sel] = 1
    df["intervene"] = mask
    return df

def eval_metrics(df: pd.DataFrame, label_col="y"):
    out={}
    if label_col in df.columns and df[label_col].nunique()>1 and df["risk"].notna().any():
        y = df[label_col].values
        r = df["risk"].values
        out["AUC_risk"]   = float(roc_auc_score(y, r))
        P,R,T             = precision_recall_curve(y, r)
        out["AUPRC_risk"] = float(auc(R, P))
        pol = df[df["intervene"]==1]
        if len(pol)>0:
            out["Precision_policy"] = float(((pol[label_col]==1).sum())/len(pol))
        out["Corr_RFI_y"] = float(pd.Series(df["RFI"]).corr(pd.Series(1-y)))
    if {"I_beta0","I_beta1","H","C"}.issubset(df.columns):
        dI = np.abs(np.gradient(df["I_beta0"].values)) + np.abs(np.gradient(df["I_beta1"].values))
        dM = np.abs(np.gradient(df["H"].values))      + np.abs(np.gradient(df["C"].values))
        out["Invariant_vs_Metric_Drift"] = float(np.nanmean(dI)/np.nanmean(dM))
    if {"R_tilde","RFI"}.issubset(df.columns):
        out["Corr_Rtilde_RFI"] = float(pd.Series(df["R_tilde"]).corr(pd.Series(df["RFI"])))
    return out

# =============================
# 6) Dataset loader
# =============================
def load_dataset(path: Path) -> Tuple[Optional[np.ndarray], Optional[np.ndarray], pd.DataFrame]:
    if not path.exists():
        return None, None, pd.DataFrame()
    if path.suffix.lower()==".csv":
        df = pd.read_csv(path, **CSV_READ_KW)
    elif path.suffix.lower()==".parquet":
        df = pd.read_parquet(path)
    else:
        return None, None, pd.DataFrame()

    if len(df) > FILE_MAX_ROWS:
        print(f"[skip huge] {path} rows={len(df)} > FILE_MAX_ROWS={FILE_MAX_ROWS}")
        return None, None, pd.DataFrame()

    # Try label extraction before selecting numeric
    y, ycol = extract_labels(df)

    # Keep numeric columns (drop label from X if present)
    Xdf = df.select_dtypes(include=[np.number]).copy()
    if y is not None and ycol in Xdf.columns:
        Xdf = Xdf.drop(columns=[ycol])

    # If too many numeric channels, take first CHANNEL_MAX
    if Xdf.shape[1] > CHANNEL_MAX:
        Xdf = Xdf.iloc[:, :CHANNEL_MAX]

    if Xdf.shape[1] == 0:
        # try to coerce a single non-numeric numeric-like column
        print(f"[skip] {path} has no numeric sensor columns after filtering")
        return None, None, df

    X = Xdf.values
    if X.ndim == 1:
        X = X[:, None]
    return X, y, df

# =============================
# 7) Main — scan & score
# =============================
def slugify_path(p: Path) -> str:
    rel = str(p.relative_to(ROOT)).replace("\\","/")
    # safe slug: letters, numbers, dash, underscore
    s = re.sub(r"[^A-Za-z0-9_\-./]", "_", rel)
    s = s.replace("/", "__")
    return s

all_files = discover_files(SEARCH_DIRS, FILE_PATTERNS)
print(f"[ROOT] {ROOT}")
print(f"[scan] Found {len(all_files)} candidate files")

all_metrics = []
all_frames  = []

for i, path in enumerate(all_files, 1):
    try:
        X, y, raw = load_dataset(path)
        if X is None:
            continue

        ds_slug = slugify_path(path)
        # FS inference (from datetime/time col or default)
        fs = infer_fs(raw)

        # Make features (adaptive windowing inside)
        dff = make_features_df(X, fs=fs, ds_name=ds_slug, labels=y)

        if dff is None or dff.empty:
            print(f"[skip] {ds_slug} produced no features")
            continue

        # Train oracle (if labels allow), then closed-loop
        model, use_cols = train_oracle(dff)
        dff_open   = dff.copy(); dff_open["risk"]=np.nan; dff_open["intervene"]=0
        dff_closed = closed_loop_policy(dff, model, use_cols)

        # Metrics
        m_open  = eval_metrics(dff_open)
        m_close = eval_metrics(dff_closed)

        # Write features per dataset
        out_csv = OUT / f"features__{ds_slug}.csv"
        out_csv.parent.mkdir(parents=True, exist_ok=True)
        dff_closed.to_csv(out_csv, index=False)

        row = dict(dataset=ds_slug, source=str(path),
                   fs=fs, win_used=int(dff.attrs.get("WIN_used", WIN_DEFAULT)),
                   step_used=int(dff.attrs.get("STEP_used", STEP_DEFAULT)),
                   **{f"open::{k}":v for k,v in (m_open  or {}).items()},
                   **{f"closed::{k}":v for k,v in (m_close or {}).items()})
        all_metrics.append(row)
        all_frames.append(dff_closed.assign(run=ds_slug))

        print(f"[{i}/{len(all_files)}] ✓ {ds_slug}  ->  {out_csv.name}")

    except Exception as e:
        print(f"[{i}/{len(all_files)}] ! Error on {path}: {e}")

# Summary tables
if all_metrics:
    tab = pd.DataFrame(all_metrics).sort_values("dataset")
    tab.to_csv(OUT/"verdict_table.csv", index=False)
    print("\n== Verdict Table (saved) ==")
    print(tab.fillna("").to_string(index=False))

    # Optional glyph vs random pairing if such files exist in scan
    def pair_cmp(metric_key: str):
        rows=[]
        # Find pairs by suffix markers in slug
        systems = {}
        for ds in tab["dataset"]:
            if ds.endswith("__data__sim__ising_glyph.csv"):
                systems.setdefault("ising", {})["glyph"] = ds
            if ds.endswith("__data__sim__ising_random.csv"):
                systems.setdefault("ising", {})["random"] = ds
            if ds.endswith("__data__sim__kuramoto_glyph.csv"):
                systems.setdefault("kuramoto", {})["glyph"] = ds
            if ds.endswith("__data__sim__kuramoto_random.csv"):
                systems.setdefault("kuramoto", {})["random"] = ds
            if ds.endswith("__data__sim__saddlenode_glyph.csv"):
                systems.setdefault("saddlenode", {})["glyph"] = ds
            if ds.endswith("__data__sim__saddlenode_random.csv"):
                systems.setdefault("saddlenode", {})["random"] = ds
        for sys, d in systems.items():
            if "glyph" in d and "random" in d:
                g = tab[tab["dataset"].eq(d["glyph"])][f"closed::{metric_key}"].values
                r = tab[tab["dataset"].eq(d["random"])][f"closed::{metric_key}"].values
                if len(g)==1 and len(r)==1:
                    rows.append(dict(system=sys, metric=metric_key,
                                     glyph=float(g[0]), random=float(r[0]),
                                     diff=float(g[0])-float(r[0])))
        return pd.DataFrame(rows)

    for key in ["AUC_risk","Precision_policy","Corr_RFI_y"]:
        cmp = pair_cmp(key)
        if len(cmp):
            cmp.to_csv(OUT/f"pair_closed__{key}.csv", index=False)
            print(f"\n== Pairing on closed::{key} ==")
            print(cmp.to_string(index=False))

if all_frames:
    big = pd.concat(all_frames, ignore_index=True)
    cstat = big.groupby("dataset")["Invariant_vs_Metric_Drift"].mean().reset_index()
    cstat.to_csv(OUT/"invariant_vs_metric_drift.csv", index=False)
    print("\n== Invariant vs Metric Drift (mean ratio; <1 is good) ==")
    print(cstat.to_string(index=False))

print(f"\nArtifacts written to: {OUT}")


[ROOT] C:\Users\caleb\CNT_Lab
[scan] Found 2949 candidate files
[skip] C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\astropy\coordinates\tests\accuracy\data\fk4_no_e_fk4.csv has no numeric sensor columns after filtering
[skip] C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\astropy\coordinates\tests\accuracy\data\fk4_no_e_fk5.csv has no numeric sensor columns after filtering
[skip] C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\astropy\coordinates\tests\accuracy\data\galactic_fk4.csv has no numeric sensor columns after filtering
[skip] C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\astropy\coordinates\tests\accuracy\data\icrs_fk5.csv has no numeric sensor columns after filtering
[adapt] .venv__Lib__site-packages__astropy__io__ascii__tests__data__simple_csv.csv: T=2 < WIN -> using WIN=8, STEP=2
[fallback] .venv__Lib__site-packages__astropy__io__ascii__tests__data__simple_csv.csv: single full-window features (T=2)
[5/2949] ! Error on C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\astropy

C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3065: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3066: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]
C:\Users\caleb\AppData\Local\Temp\ipykernel_27992\3182257274.py:137: RuntimeWarning: invalid value encountered in scalar divide
  return -np.sum(P * safe_log(P)) / safe_log(len(P))
C:\Users\caleb\AppData\Local\Temp\ipykernel_27992\3182257274.py:137: RuntimeWarning: invalid value encountered in scalar divide
  return -np.sum(P * safe_log(P)) / safe_log(len(P))


[adapt] .venv__Lib__site-packages__astroquery__xmatch__tests__data__posList_duplicates.csv: T=6 < WIN -> using WIN=8, STEP=2
[fallback] .venv__Lib__site-packages__astroquery__xmatch__tests__data__posList_duplicates.csv: single full-window features (T=6)
[14/2949] ! Error on C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\astroquery\xmatch\tests\data\posList_duplicates.csv: Shape of array too small to calculate a numerical gradient, at least (edge_order + 1) elements are required.
[adapt] .venv__Lib__site-packages__astroquery__xmatch__tests__data__query_res.csv: T=11 < WIN -> using WIN=11, STEP=2
[15/2949] ! Error on C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\astroquery\xmatch\tests\data\query_res.csv: autodetected range of [nan, nan] is not finite
[skip] C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\astroquery\xmatch\tests\data\tables.csv has no numeric sensor columns after filtering
[skip] C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\matplotlib\mpl-data\sample_data\data_x_x2_x3.

C:\Users\caleb\AppData\Local\Temp\ipykernel_27992\3182257274.py:92: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  dt = pd.to_datetime(s, errors="raise")


[20/2949] ! Error on C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\mne\datasets\sleep_physionet\age_records.csv: Shape of array too small to calculate a numerical gradient, at least (edge_order + 1) elements are required.
[adapt] .venv__Lib__site-packages__mne__datasets__sleep_physionet__temazepam_records.csv: T=44 < WIN -> using WIN=44, STEP=11
[21/2949] ! Error on C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\mne\datasets\sleep_physionet\temazepam_records.csv: Shape of array too small to calculate a numerical gradient, at least (edge_order + 1) elements are required.
[adapt] .venv__Lib__site-packages__mne__io__artemis123__resources__Artemis123_ChannelMap.csv: T=145 < WIN -> using WIN=145, STEP=36
[22/2949] ! Error on C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\mne\io\artemis123\resources\Artemis123_ChannelMap.csv: autodetected range of [nan, nan] is not finite
[adapt] .venv__Lib__site-packages__mne__io__artemis123__resources__Artemis123_mneLoc.csv: T=143 < WIN -> using WIN=143, 

...

[adapt] omega_hunt__omega_hunt_v0_2_20251019-015707__omega_fused_20251019-123257__omega_v0_5_checker_guard_20251022-001428__evolve_history.csv: T=12 < WIN -> using WIN=12, STEP=3
[2938/2949] ! Error on C:\Users\caleb\CNT_Lab\omega_hunt\omega_hunt_v0_2_20251019-015707\omega_fused_20251019-123257\omega_v0_5_checker_guard_20251022-001428\evolve_history.csv: Shape of array too small to calculate a numerical gradient, at least (edge_order + 1) elements are required.
[adapt] omega_hunt__omega_hunt_v0_2_20251019-015707__omega_fused_20251019-123257__omega_v0_5_checker_guard_20251022-001428__quick_verify_checker_guard.csv: T=16 < WIN -> using WIN=16, STEP=4
[2939/2949] ! Error on C:\Users\caleb\CNT_Lab\omega_hunt\omega_hunt_v0_2_20251019-015707\omega_fused_20251019-123257\omega_v0_5_checker_guard_20251022-001428\quick_verify_checker_guard.csv: Shape of array too small to calculate a numerical gradient, at least (edge_order + 1) elements are required.
[adapt] omega_hunt__omega_hunt_v0_2_20251019

C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3065: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3066: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3065: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3066: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]


[adapt] omega_hunt__omega_hunt_v0_2_20251019-015707__omega_leaderboard.csv: T=296 < WIN -> using WIN=296, STEP=64
[2949/2949] ! Error on C:\Users\caleb\CNT_Lab\omega_hunt\omega_hunt_v0_2_20251019-015707\omega_leaderboard.csv: Shape of array too small to calculate a numerical gradient, at least (edge_order + 1) elements are required.

== Verdict Table (saved) ==
                                                                                               dataset                                                                                                                 source         fs  win_used  step_used  open::Invariant_vs_Metric_Drift open::Corr_Rtilde_RFI  closed::Invariant_vs_Metric_Drift closed::Corr_Rtilde_RFI
                                       .venv__Lib__site-packages__nitime__data__event_related_fmri.csv                                      C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\nitime\data\event_related_fmri.csv 100.000000       512         64               

C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3065: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3066: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]


KeyError: 'Column not found: Invariant_vs_Metric_Drift'

In [4]:
# === HOTFIX v0.4.3 "Clean Pass" — robust stats, skip .venv, safe gradients, NaN impute ===
import os, numpy as np, pandas as pd
from pathlib import Path

try:
    from sklearn.impute import SimpleImputer
    from sklearn.pipeline import Pipeline
    from sklearn.preprocessing import StandardScaler
    from sklearn.linear_model import LogisticRegression
except Exception:
    pass  # already imported earlier

# --- 0) Guards & defaults (reuse ROOT/OUT/SEARCH_DIRS/FILE_PATTERNS if already defined) ---
ROOT = Path(globals().get("ROOT", r"C:\Users\caleb\CNT_Lab")).resolve()
OUT  = Path(globals().get("OUT", ROOT / "artifacts" / "cnt_five_pillars")).resolve()
SEARCH_DIRS = globals().get("SEARCH_DIRS", [ROOT, ROOT / "notebooks" / "archive"])
FILE_PATTERNS = globals().get("FILE_PATTERNS", ["**/*.csv", "**/*.parquet"])
OUT.mkdir(parents=True, exist_ok=True)

# --- 1) Skip filters to avoid scanning package test data ---
SKIP_SUBSTRINGS = [
    f"{os.sep}.venv{os.sep}", "site-packages", f"{os.sep}tests{os.sep}",
    "mpl-data", f"{os.sep}sample_data{os.sep}", f"{os.sep}datasets{os.sep}",
]
NAME_DISALLOW = [
    "validation-set", "testset", "sample_data", "penguins", "iris", "sunspots",
    "breast_cancer", "wine_data", "anes", "statsmodels", "sklearn", "astroquery",
    "nitime", "pyarrow", "mne", "tornado", "pingouin"
]
def should_skip_path(p: Path) -> bool:
    s = str(p).lower().replace("/", os.sep)
    if any(tok in s for tok in SKIP_SUBSTRINGS): return True
    base = p.name.lower()
    if any(tok in base for tok in NAME_DISALLOW): return True
    return False

def discover_files_clean(dirs, patterns):
    hits=[]
    for d in dirs:
        if not Path(d).exists(): continue
        for pat in patterns:
            hits.extend(q for q in Path(d).glob(pat) if not should_skip_path(q))
    return sorted(set(p.resolve() for p in hits))

# --- 2) Safer primitives overriding earlier defs ---
def safe_log(x, eps=1e-12):
    return np.log(np.clip(x, eps, None))

def safe_gradient(arr: np.ndarray):
    arr = np.asarray(arr, float)
    if arr.size < 2:
        return np.zeros_like(arr, dtype=float)
    try:
        return np.gradient(arr)
    except Exception:
        d = np.diff(arr, prepend=arr[0])
        return d

def bins_for_array(x, max_bins=16):
    x = np.asarray(x)
    n = int(x.size)
    if n < 8: return 2
    xnf = x[np.isfinite(x)]
    if xnf.size < 2: return None
    ux = np.unique(xnf)
    if ux.size < 2: return None
    return int(max(2, min(max_bins, int(np.sqrt(n)), ux.size)))

def nmi_matrix(Xw: np.ndarray):
    n = Xw.shape[1]
    vals=[]
    for i in range(n):
        xi = Xw[:,i]
        bi = bins_for_array(xi)
        if bi is None: continue
        try:
            hi,_= np.histogram(xi, bins=bi); Pi = hi/hi.sum() if hi.sum()>0 else np.ones(bi)/bi
            Hi = -np.sum(Pi*safe_log(Pi))
        except Exception:
            continue
        for j in range(i+1, n):
            xj = Xw[:,j]
            bj = bins_for_array(xj)
            b  = bi if bj is None else min(bi, bj)
            if b is None: continue
            try:
                hj,_= np.histogram(xj, bins=b); Pj = hj/hj.sum() if hj.sum()>0 else np.ones(b)/b
                Hj = -np.sum(Pj*safe_log(Pj))
                H2,_,_ = np.histogram2d(xi, xj, bins=b)
                Pij = H2/H2.sum() if H2.sum()>0 else np.ones((b,b))/(b*b)
                Hij = -np.sum(Pij*safe_log(Pij))
                Iij = Hi + Hj - Hij
                denom = max(Hi, Hj)
                if denom>0 and np.isfinite(Iij): vals.append(Iij/denom)
            except Exception:
                continue
    return {"C_nmi": float(np.nanmean(vals)) if vals else np.nan}

from scipy.signal import hilbert
def plv_matrix(Xw: np.ndarray):
    # Require some minimal resolution for phases; else return NaN
    if Xw.shape[0] < 16 or Xw.shape[1] < 2:
        return {"C_plv": np.nan}
    try:
        Z = hilbert(Xw, axis=0)
        ph = np.angle(Z)
        n  = ph.shape[1]
        vals=[]
        for i in range(n):
            for j in range(i+1, n):
                dphi = ph[:,i]-ph[:,j]
                vals.append(np.abs(np.mean(np.exp(1j*dphi))))
        return {"C_plv": float(np.nanmean(vals)) if vals else np.nan}
    except Exception:
        return {"C_plv": np.nan}

def coherence_features(Xw: np.ndarray):
    d = {}; d.update(plv_matrix(Xw)); d.update(nmi_matrix(Xw))
    Cvals = [v for k,v in d.items() if k.startswith("C_") and np.isfinite(v)]
    d["C"] = float(np.nanmean(Cvals)) if Cvals else 0.0
    return d

def curvature_proxy(Xw: np.ndarray):
    # Cheap/robust negative logdet(Cov) proxy; guard tiny/degenerate shapes
    if Xw.shape[1] < 2 or Xw.shape[0] < 3:
        return {"R_tilde": 0.0}
    Xc  = Xw - Xw.mean(0, keepdims=True)
    Cov = np.cov(Xc.T)
    if not np.isfinite(Cov).all():
        return {"R_tilde": 0.0}
    Cov = Cov + 1e-6*np.eye(Cov.shape[0])
    try:
        sign, logdet = np.linalg.slogdet(Cov)
        return {"R_tilde": float(-logdet) if np.isfinite(logdet) else 0.0}
    except Exception:
        return {"R_tilde": 0.0}

# Override make_features_df to use safe_gradient & robust coherence/curvature
def make_features_df(X: np.ndarray, fs: float, ds_name:str,
                     win:int=globals().get("WIN_DEFAULT", globals().get("WIN", 512)),
                     step:int=globals().get("STEP_DEFAULT", globals().get("STEP", 64)),
                     labels=None) -> pd.DataFrame:
    T = int(X.shape[0])
    if T <= 0:
        print(f"[skip] {ds_name} empty")
        return pd.DataFrame()

    if T < win:
        win  = max(8, min(win, T))
        step = max(1, min(step, max(1, win//4)))
        print(f"[adapt] {ds_name}: T={T} -> WIN={win}, STEP={step}")

    rows=[]
    for start in range(0, max(T - win + 1, 0), step):
        Xw = X[start:start+win]
        ent = entropy_matrix(Xw, fs=fs)  # from your earlier cell
        coh = coherence_features(Xw)
        invv= invariant_features(Xw)
        curv= curvature_proxy(Xw)
        rows.append(dict(t0=start, **ent, **coh, **invv, **curv))

    if not rows:
        Xw = X
        rows = [dict(t0=0, **entropy_matrix(Xw, fs=fs),
                          **coherence_features(Xw),
                          **invariant_features(Xw),
                          **curvature_proxy(Xw))]
        print(f"[fallback] {ds_name}: single full-window features (T={T})")

    df = pd.DataFrame(rows).sort_values("t0").reset_index(drop=True)
    # Use safe gradient for dH; and safe RFI construction
    df["dH"]  = safe_gradient(df["H"].values)
    C_clean   = np.nan_to_num(df["C"].values, nan=0.0, posinf=0.0, neginf=0.0)
    df["RFI"] = rfi_series(C_clean, df["dH"].values, ALPHA)  # rfi_series from earlier cell

    # Label align (only if long enough)
    if labels is not None and len(labels) >= int(df["t0"].iloc[-1] + win):
        centers = (df["t0"] + win//2).astype(int)
        y = np.array(labels)[np.clip(centers, 0, len(labels)-1)]
        df["y"] = y.astype(int)

    df["dataset"] = ds_name
    df.attrs["WIN_used"]  = win
    df.attrs["STEP_used"] = step
    return df

# Override Oracle trainer with NaN imputer
def train_oracle(df: pd.DataFrame):
    use_cols = [c for c in ["RFI","dH","C","R_tilde","I_beta0","I_beta1","H"] if c in df]
    dtrain = df.dropna(subset=use_cols + (["y"] if "y" in df else []))
    if "y" not in dtrain or dtrain["y"].nunique() < 2:
        return None, use_cols
    X = dtrain[use_cols].values
    y = dtrain["y"].values
    pipe = Pipeline([
        ("imputer", SimpleImputer(strategy="median")),
        ("scaler",  StandardScaler()),
        ("clf",     LogisticRegression(max_iter=400))
    ])
    pipe.fit(X, y)
    return pipe, use_cols

# Safer eval (no gradient crashes; only compute drifts if columns exist)
def eval_metrics(df: pd.DataFrame, label_col="y"):
    out={}
    if label_col in df.columns and df[label_col].nunique()>1 and df["risk"].notna().any():
        from sklearn.metrics import roc_auc_score, precision_recall_curve, auc
        y = df[label_col].values
        r = df["risk"].values
        try:
            out["AUC_risk"]   = float(roc_auc_score(y, r))
            P,R,T             = precision_recall_curve(y, r)
            out["AUPRC_risk"] = float(auc(R, P))
        except Exception:
            pass
        pol = df[df["intervene"]==1]
        if len(pol)>0:
            out["Precision_policy"] = float(((pol[label_col]==1).sum())/len(pol))
        try:
            out["Corr_RFI_y"] = float(pd.Series(df["RFI"]).corr(pd.Series(1-y)))
        except Exception:
            pass
    if {"I_beta0","I_beta1","H","C"}.issubset(df.columns):
        dI = np.abs(safe_gradient(df["I_beta0"].values)) + np.abs(safe_gradient(df["I_beta1"].values))
        dM = np.abs(safe_gradient(df["H"].values))       + np.abs(safe_gradient(df["C"].values))
        if np.nanmean(dM) > 0:
            out["Invariant_vs_Metric_Drift"] = float(np.nanmean(dI)/np.nanmean(dM))
    if {"R_tilde","RFI"}.issubset(df.columns):
        try:
            out["Corr_Rtilde_RFI"] = float(pd.Series(df["R_tilde"]).corr(pd.Series(df["RFI"])))
        except Exception:
            pass
    return out

# --- 3) Re-scan with clean discover + re-run, writing a new verdict table ---
all_files = discover_files_clean(SEARCH_DIRS, FILE_PATTERNS)
print(f"[ROOT] {ROOT}")
print(f"[scan-clean] {len(all_files)} candidates after skip filters")

all_metrics = []
all_frames  = []

def slugify_path(p: Path) -> str:
    rel = str(p.relative_to(ROOT)).replace("\\","/"); import re
    s = re.sub(r"[^A-Za-z0-9_\-./]", "_", rel)
    return s.replace("/", "__")

def load_dataset(path: Path):
    if not path.exists(): return None, None, pd.DataFrame()
    if path.suffix.lower()==".csv":
        df = pd.read_csv(path, low_memory=False)
    elif path.suffix.lower()==".parquet":
        df = pd.read_parquet(path)
    else:
        return None, None, pd.DataFrame()
    y = None
    for cand in ["collapse_label","label","y","event","is_event","collapse","is_collapse","target"]:
        if cand in df.columns:
            col = df[cand]
            if col.dtype==bool: y = col.astype(int).values
            elif pd.api.types.is_numeric_dtype(col): y = (col.astype(float).fillna(0).values>0).astype(int)
            else: y = col.astype(str).str.strip().str.lower().isin({"1","true","yes","y","event","collapse"}).astype(int).values
            break
    Xdf = df.select_dtypes(include=[np.number]).copy()
    if y is not None and "y" in Xdf.columns: Xdf = Xdf.drop(columns=["y"])
    if Xdf.shape[1]==0: return None, None, df
    if Xdf.shape[1]>32: Xdf = Xdf.iloc[:, :32]
    X = Xdf.values
    if X.ndim==1: X = X[:,None]
    return X, y, df

def infer_fs(df: pd.DataFrame, default=100.0):
    # try datetime diffs, then numeric time column; else default
    for c in df.columns:
        if np.issubdtype(df[c].dtype, np.datetime64):
            dt = df[c].dropna().sort_values().diff().dt.total_seconds().dropna()
            if len(dt) and np.isfinite(dt.median()) and dt.median()>0:
                return float(1.0/dt.median())
    for name in ["time","timestamp","datetime","date","ts"]:
        cols = [c for c in df.columns if c.lower()==name]
        for c in cols:
            s = df[c].dropna()
            try:
                dsec = pd.to_datetime(s, errors="raise").sort_values().diff().dt.total_seconds().dropna()
                if len(dsec) and dsec.median()>0: return float(1.0/dsec.median())
            except Exception:
                pass
            if pd.api.types.is_numeric_dtype(s):
                dnum = s.sort_values().diff().dropna()
                if len(dnum) and float(dnum.median())>0: return float(1.0/float(dnum.median()))
    return float(default)

from math import isnan
saved = 0
for i, path in enumerate(all_files, 1):
    try:
        X, y, raw = load_dataset(path)
        if X is None: continue
        ds_slug = slugify_path(path)
        fs = infer_fs(raw)
        dff = make_features_df(X, fs=fs, ds_name=ds_slug, labels=y)
        if dff is None or dff.empty: continue
        model, use_cols = train_oracle(dff)
        dff_open   = dff.copy(); dff_open["risk"]=np.nan; dff_open["intervene"]=0
        dff_closed = closed_loop_policy(dff, model, use_cols)  # uses your earlier function
        m_open  = eval_metrics(dff_open)
        m_close = eval_metrics(dff_closed)
        (OUT / f"features__{ds_slug}.csv").parent.mkdir(parents=True, exist_ok=True)
        dff_closed.to_csv(OUT / f"features__{ds_slug}.csv", index=False)
        saved += 1
        all_metrics.append(dict(dataset=ds_slug, source=str(path),
                                fs=fs,
                                win_used=int(dff.attrs.get("WIN_used", 0)),
                                step_used=int(dff.attrs.get("STEP_used", 0)),
                                **{f"open::{k}":v for k,v in (m_open  or {}).items()},
                                **{f"closed::{k}":v for k,v in (m_close or {}).items()}))
        all_frames.append(dff_closed.assign(run=ds_slug))
        if i % 50 == 0:
            print(f"[{i}/{len(all_files)}] … processed, {saved} saved")
    except Exception as e:
        # Keep quiet unless you'd like verbose errors; comment next line to silence
        print(f"[{i}/{len(all_files)}] ! {path}: {e}")

# --- 4) Summaries ---
if all_metrics:
    tab = pd.DataFrame(all_metrics).sort_values("dataset")
    tab.to_csv(OUT/"verdict_table.csv", index=False)
    print("\n== Verdict Table (head) ==")
    print(tab.head(20).fillna("").to_string(index=False))
else:
    print("\n[warn] No metrics were aggregated (features may still be saved).")

if all_frames:
    big = pd.concat(all_frames, ignore_index=True)
    if "Invariant_vs_Metric_Drift" in big.columns:
        cstat = big.groupby("dataset")["Invariant_vs_Metric_Drift"].mean().reset_index()
        cstat.to_csv(OUT/"invariant_vs_metric_drift.csv", index=False)
        print("\n== Invariant vs Metric Drift (mean ratio; <1 is good) ==")
        print(cstat.head(20).to_string(index=False))

print(f"\nArtifacts written to: {OUT}")


[ROOT] C:\Users\caleb\CNT_Lab
[scan-clean] 2721 candidates after skip filters
[adapt] artifacts__cnt_five_pillars__features__artifacts__pli_humans_100plus__tests_functional__tables__subject_metrics_allconds.csv.csv: T=3 -> WIN=8, STEP=2
[fallback] artifacts__cnt_five_pillars__features__artifacts__pli_humans_100plus__tests_functional__tables__subject_metrics_allconds.csv.csv: single full-window features (T=3)
[adapt] artifacts__cnt_five_pillars__features__artifacts__tables__genome3d__atlas__edges_v0a__20251008-211232.parquet.csv: T=4 -> WIN=8, STEP=2
[fallback] artifacts__cnt_five_pillars__features__artifacts__tables__genome3d__atlas__edges_v0a__20251008-211232.parquet.csv: single full-window features (T=4)
[adapt] artifacts__cnt_five_pillars__features__artifacts__tables__genome3d__atlas__edges_v0a__20251008-211922.parquet.csv: T=4 -> WIN=8, STEP=2
[fallback] artifacts__cnt_five_pillars__features__artifacts__tables__genome3d__atlas__edges_v0a__20251008-211922.parquet.csv: single full-wi

C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3065: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3066: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3057: RuntimeWarning: Degrees of freedom <= 0 for slice
  c = cov(x, y, rowvar, dtype=dtype)
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:2914: RuntimeWarning: divide by zero encountered in divide
  c *= np.true_divide(1, fact)
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:2914: RuntimeWarning: invalid value encountered in multiply
  c *= np.true_divide(1, fact)
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3065: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
C:\

[adapt] artifacts__cnt_five_pillars__features__artifacts__tables__genome3d__atlas__edges_v1h__20251008-215623.parquet.csv: T=11 -> WIN=11, STEP=2
[adapt] artifacts__cnt_five_pillars__features__artifacts__tables__genome3d__atlas__edges_v1s__20251008-222324.parquet.csv: T=11 -> WIN=11, STEP=2
[adapt] artifacts__cnt_five_pillars__features__artifacts__tables__genome3d__atlas__edges_v1s__20251008-222534.parquet.csv: T=11 -> WIN=11, STEP=2


C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3065: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3066: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3057: RuntimeWarning: Degrees of freedom <= 0 for slice
  c = cov(x, y, rowvar, dtype=dtype)
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:2914: RuntimeWarning: divide by zero encountered in divide
  c *= np.true_divide(1, fact)
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:2914: RuntimeWarning: invalid value encountered in multiply
  c *= np.true_divide(1, fact)
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3065: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
C:\

[adapt] artifacts__cnt_five_pillars__features__artifacts__tables__migrated__enrichment__cc99918a.csv.csv: T=88 -> WIN=88, STEP=22
[adapt] artifacts__cnt_five_pillars__features__artifacts__tables__migrated__epochs-with-predictions__d98a82f2.csv.csv: T=4 -> WIN=8, STEP=2
[fallback] artifacts__cnt_five_pillars__features__artifacts__tables__migrated__epochs-with-predictions__d98a82f2.csv.csv: single full-window features (T=4)
[adapt] artifacts__cnt_five_pillars__features__artifacts__tables__migrated__features__62fc8d4b.csv.csv: T=4 -> WIN=8, STEP=2
[fallback] artifacts__cnt_five_pillars__features__artifacts__tables__migrated__features__62fc8d4b.csv.csv: single full-window features (T=4)
[adapt] artifacts__cnt_five_pillars__features__artifacts__tables__migrated__features__a022e273.csv.csv: T=4 -> WIN=8, STEP=2


...

[adapt] omega_hunt__omega_hunt_v0_2_20251019-015707__omega_fused_20251019-123257__omega_v0_4_20251020-223420__atlas__metrics_v0_4.csv: T=1 -> WIN=8, STEP=2
[fallback] omega_hunt__omega_hunt_v0_2_20251019-015707__omega_fused_20251019-123257__omega_v0_4_20251020-223420__atlas__metrics_v0_4.csv: single full-window features (T=1)
[adapt] omega_hunt__omega_hunt_v0_2_20251019-015707__omega_fused_20251019-123257__omega_v0_4_20251020-223420__evolve_history.csv: T=60 -> WIN=60, STEP=15
[adapt] omega_hunt__omega_hunt_v0_2_20251019-015707__omega_fused_20251019-123257__omega_v0_4_20251020-223420__truth_audit_20251021-005753__deep_basin.csv: T=225 -> WIN=225, STEP=56
[adapt] omega_hunt__omega_hunt_v0_2_20251019-015707__omega_fused_20251019-123257__omega_v0_4_20251020-223420__truth_audit_20251021-005753__threshold_margin.csv: T=7 -> WIN=8, STEP=2
[fallback] omega_hunt__omega_hunt_v0_2_20251019-015707__omega_fused_20251019-123257__omega_v0_4_20251020-223420__truth_audit_20251021-005753__threshold_mar

C:\Users\caleb\AppData\Local\Temp\ipykernel_27992\3182257274.py:137: RuntimeWarning: invalid value encountered in scalar divide
  return -np.sum(P * safe_log(P)) / safe_log(len(P))
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3057: RuntimeWarning: Degrees of freedom <= 0 for slice
  c = cov(x, y, rowvar, dtype=dtype)
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:2914: RuntimeWarning: divide by zero encountered in divide
  c *= np.true_divide(1, fact)
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:2914: RuntimeWarning: invalid value encountered in multiply
  c *= np.true_divide(1, fact)
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3057: RuntimeWarning: Degrees of freedom <= 0 for slice
  c = cov(x, y, rowvar, dtype=dtype)
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:2914: RuntimeWarning: divide by zero encountered in 

[adapt] omega_hunt__omega_hunt_v0_2_20251019-015707__omega_fused_20251019-123257__omega_v0_5_lite_20251021-233500__quick_verify_paired_checker.csv: T=16 -> WIN=16, STEP=4
[adapt] omega_hunt__omega_hunt_v0_2_20251019-015707__omega_fused_20251019-123257__omega_v0_5_lite_20251021-233500__quick_verify_parity_aware.csv: T=16 -> WIN=16, STEP=4
[adapt] omega_hunt__omega_hunt_v0_2_20251019-015707__omega_fused_20251019-123257__omega_v0_5_lite_20251021-233500__quick_verify_results.csv: T=16 -> WIN=16, STEP=4
[adapt] omega_hunt__omega_hunt_v0_2_20251019-015707__omega_fused_20251019-123257__omega_v0_6_hysteresis_20251022-001941__evolve_history.csv: T=12 -> WIN=12, STEP=3
[adapt] omega_hunt__omega_hunt_v0_2_20251019-015707__omega_fused_20251019-123257__omega_v0_6_hysteresis_20251022-001941__quick_verify_hysteresis.csv: T=24 -> WIN=24, STEP=6
[adapt] omega_hunt__omega_hunt_v0_2_20251019-015707__omega_fused_20251019-123257__omega_v0_7_fused_20251022-004408__evolve_history.csv: T=12 -> WIN=12, STEP=3


C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3057: RuntimeWarning: Degrees of freedom <= 0 for slice
  c = cov(x, y, rowvar, dtype=dtype)
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:2914: RuntimeWarning: divide by zero encountered in divide
  c *= np.true_divide(1, fact)
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:2914: RuntimeWarning: invalid value encountered in multiply
  c *= np.true_divide(1, fact)
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:3057: RuntimeWarning: Degrees of freedom <= 0 for slice
  c = cov(x, y, rowvar, dtype=dtype)
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:2914: RuntimeWarning: divide by zero encountered in divide
  c *= np.true_divide(1, fact)
C:\Users\caleb\CNT_Lab\.venv\Lib\site-packages\numpy\lib\_function_base_impl.py:2914: RuntimeWarning: invalid value encountered in multiply
  c


== Verdict Table (head) ==
                                                                                                                         dataset                                                                                                                                                source    fs  win_used  step_used open::Corr_Rtilde_RFI closed::Corr_Rtilde_RFI open::Invariant_vs_Metric_Drift closed::Invariant_vs_Metric_Drift closed::AUC_risk closed::AUPRC_risk closed::Precision_policy closed::Corr_RFI_y
                                                                                   artifacts__CNT_PLI_EC_EO_paired_bootstrap.csv                                                                                   C:\Users\caleb\CNT_Lab\artifacts\CNT_PLI_EC_EO_paired_bootstrap.csv 100.0        15          3                                                                                                                                                                         

In [5]:
# === CNT Lab Scoreboard v1 — bound drift ratio, skip self-outputs, rank datasets ===
import numpy as np, pandas as pd
from pathlib import Path

ROOT = Path(r"C:\Users\caleb\CNT_Lab").resolve()
OUT  = ROOT / "artifacts" / "cnt_five_pillars"
OUT.mkdir(parents=True, exist_ok=True)

# --- 1) Ensure the scanner won't reprocess our own feature files next runs ---
try:
    SKIP_SUBSTRINGS  # from hotfix cell
    NAME_DISALLOW
    SKIP_SUBSTRINGS += [f"{Path('artifacts/cnt_five_pillars').as_posix()}/features__".replace("/", "\\")]
    NAME_DISALLOW   += ["features__"]
except NameError:
    pass  # fine if hotfix cell isn't in memory; this only matters on re-scans

# --- 2) Collect all features we’ve already produced ---
feat_files = sorted((p for p in OUT.glob("features__*.csv") if p.is_file()), key=lambda p: p.name)
if not feat_files:
    print("[warn] No features__*.csv found in", OUT)

def safe_grad(v):
    v = np.asarray(v, float)
    if v.size < 2: return np.zeros_like(v)
    try:
        return np.gradient(v)
    except Exception:
        d = np.diff(v, prepend=v[0])
        return d

def bound_drift_ratio(df):
    eps = 1e-6
    if {"I_beta0","I_beta1","H","C"}.issubset(df.columns):
        dI = np.abs(safe_grad(df["I_beta0"].values)) + np.abs(safe_grad(df["I_beta1"].values))
        dM = np.abs(safe_grad(df["H"].values))       + np.abs(safe_grad(df["C"].values))
        num = float(np.nanmean(dI))
        den = float(max(np.nanmean(dM), eps))
        raw = num/den
        return float(min(raw, 10.0)), float(num), float(den)
    return np.nan, np.nan, np.nan

rows = []
for f in feat_files:
    try:
        df = pd.read_csv(f, low_memory=False)
        n  = len(df)
        if n == 0: continue

        C_mean  = float(np.nanmean(df.get("C", np.nan)))
        H_mean  = float(np.nanmean(df.get("H", np.nan)))
        RFI_mu  = float(np.nanmean(df.get("RFI", np.nan)))
        RFI_p95 = float(np.nanpercentile(df.get("RFI", np.array([np.nan])), 95))
        dH_abs  = float(np.nanmean(np.abs(df.get("dH", np.nan))))
        policy  = float(np.nanmean(df.get("intervene", 0))) if "intervene" in df.columns else np.nan
        risk_mu = float(np.nanmean(df.get("risk", np.nan))) if "risk" in df.columns else np.nan
        risk_nan= float(np.mean(~np.isfinite(df.get("risk", np.array([np.nan]))))) if "risk" in df.columns else np.nan

        ratio_bounded, dI_bar, dM_bar = bound_drift_ratio(df)
        static = (np.isfinite(dM_bar) and dM_bar < 1e-5) and (np.isfinite(C_mean) and C_mean < 1e-3)

        rows.append(dict(
            dataset=f.stem.replace("features__", ""),
            file=str(f),
            n_windows=n,
            C_mean=C_mean,
            H_mean=H_mean,
            dH_abs=dH_abs,
            RFI_mean=RFI_mu,
            RFI_p95=RFI_p95,
            drift_ratio_bounded=ratio_bounded,  # capped at 10.0
            drift_motion=dM_bar,
            inv_motion=dI_bar,
            static=int(static),
            policy_rate=policy,
            risk_mean=risk_mu,
            risk_nan_rate=risk_nan
        ))
    except Exception as e:
        print(f"[skip] {f.name}: {e}")

score = pd.DataFrame(rows)
if len(score):
    # sensible ordering: strong resonance peaks, not static, bounded ratio not crazy
    score["ok_ratio"] = score["drift_ratio_bounded"].fillna(10.0) < 5.0
    score["rank_key"] = score["RFI_p95"].fillna(0) * (1.0 - 0.8*score["static"]) * (1.0 - 0.3*(~score["ok_ratio"]))
    top = score.sort_values(["rank_key","RFI_p95","RFI_mean"], ascending=False)

    score_path = OUT / "lab_score.csv"
    top_path   = OUT / "top_signals.csv"
    static_path= OUT / "static_files.csv"

    score.to_csv(score_path, index=False)
    top[top["static"]==0].head(200).to_csv(top_path, index=False)
    score[score["static"]==1].to_csv(static_path, index=False)

    print("== CNT_Lab Scoreboard (top 15, non-static) ==")
    cols = ["dataset","n_windows","RFI_p95","RFI_mean","C_mean","dH_abs","drift_ratio_bounded","policy_rate"]
    print(top[top["static"]==0][cols].head(15).to_string(index=False))
    print("\nSaved:")
    print(" -", score_path)
    print(" -", top_path)
    print(" -", static_path)
else:
    print("[warn] No rows scored; check that features__*.csv exist in", OUT)


C:\Users\caleb\AppData\Local\Temp\ipykernel_27992\1798477133.py:56: RuntimeWarning: Mean of empty slice
  risk_mu = float(np.nanmean(df.get("risk", np.nan))) if "risk" in df.columns else np.nan
C:\Users\caleb\AppData\Local\Temp\ipykernel_27992\1798477133.py:56: RuntimeWarning: Mean of empty slice
  risk_mu = float(np.nanmean(df.get("risk", np.nan))) if "risk" in df.columns else np.nan
C:\Users\caleb\AppData\Local\Temp\ipykernel_27992\1798477133.py:56: RuntimeWarning: Mean of empty slice
  risk_mu = float(np.nanmean(df.get("risk", np.nan))) if "risk" in df.columns else np.nan
C:\Users\caleb\AppData\Local\Temp\ipykernel_27992\1798477133.py:56: RuntimeWarning: Mean of empty slice
  risk_mu = float(np.nanmean(df.get("risk", np.nan))) if "risk" in df.columns else np.nan
C:\Users\caleb\AppData\Local\Temp\ipykernel_27992\1798477133.py:56: RuntimeWarning: Mean of empty slice
  risk_mu = float(np.nanmean(df.get("risk", np.nan))) if "risk" in df.columns else np.nan
C:\Users\caleb\AppData\Local\T

== CNT_Lab Scoreboard (top 15, non-static) ==
                                                                                      dataset  n_windows  RFI_p95  RFI_mean  C_mean  dH_abs  drift_ratio_bounded  policy_rate
                                           artifacts__tables__migrated__cm-eoec__d840b959.csv          1      1.0       1.0     1.0     0.0                  0.0          0.0
                                      artifacts__tables__migrated__cm-task-rest__92049ff5.csv          1      1.0       1.0     1.0     0.0                  0.0          0.0
                               artifacts__tables__migrated__cnt-eeg-erd-summary__5f7da9e8.csv          1      1.0       1.0     1.0     0.0                  0.0          0.0
                                   artifacts__tables__migrated__composition-old__a6a11e92.csv          1      1.0       1.0     1.0     0.0                  0.0          0.0
                                artifacts__tables__migrated__condition-accuracy__bcb

C:\Users\caleb\AppData\Local\Temp\ipykernel_27992\1798477133.py:56: RuntimeWarning: Mean of empty slice
  risk_mu = float(np.nanmean(df.get("risk", np.nan))) if "risk" in df.columns else np.nan
C:\Users\caleb\AppData\Local\Temp\ipykernel_27992\1798477133.py:56: RuntimeWarning: Mean of empty slice
  risk_mu = float(np.nanmean(df.get("risk", np.nan))) if "risk" in df.columns else np.nan
C:\Users\caleb\AppData\Local\Temp\ipykernel_27992\1798477133.py:56: RuntimeWarning: Mean of empty slice
  risk_mu = float(np.nanmean(df.get("risk", np.nan))) if "risk" in df.columns else np.nan
C:\Users\caleb\AppData\Local\Temp\ipykernel_27992\1798477133.py:56: RuntimeWarning: Mean of empty slice
  risk_mu = float(np.nanmean(df.get("risk", np.nan))) if "risk" in df.columns else np.nan
C:\Users\caleb\AppData\Local\Temp\ipykernel_27992\1798477133.py:56: RuntimeWarning: Mean of empty slice
  risk_mu = float(np.nanmean(df.get("risk", np.nan))) if "risk" in df.columns else np.nan
C:\Users\caleb\AppData\Local\T

In [6]:
# === CNT Lab Scoreboard v1.1 — quality filters + quiet risk stats ===
import numpy as np, pandas as pd
from pathlib import Path

OUT = Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars")

score_path = OUT / "lab_score.csv"
score = pd.read_csv(score_path) if score_path.exists() else pd.DataFrame()

def _finite_mean(a):
    a = np.asarray(a, float)
    m = np.isfinite(a)
    return float(np.mean(a[m])) if m.any() else np.nan

if score.empty:
    print("[warn] lab_score.csv is empty; run the feature pass first.")
else:
    # Quality gates
    MIN_WINDOWS = 12
    MOTION_MIN  = 1e-4          # minimal metric motion
    VAR_MIN     = 1e-6          # minimal variance to avoid flat series
    BAD_TOKENS  = {"summary","overview","omni-summary","gra_summary",
                   "cm-eoec","cm-task-rest","condition-accuracy",
                   "composition-old","dwell-by-id"}

    score["bad_name"] = score["dataset"].str.lower().apply(lambda s: any(t in s for t in BAD_TOKENS))

    # Recompute a few robustness bits if missing
    for col in ["risk_mean","risk_nan_rate"]:
        if col not in score.columns:
            score[col] = np.nan

    # Build dynamic filters
    ok = (
        (score["n_windows"] >= MIN_WINDOWS) &
        (score["drift_motion"].fillna(0.0) >= MOTION_MIN) &
        (score["RFI_mean"].fillna(0.0).between(0.0, 1.0)) &
        (score["RFI_p95"].fillna(0.0) <= 1.0 + 1e-9) &
        (~score["bad_name"])
    )

    filtered = score.loc[ok].copy()

    # A richer rank key: high RFI peaks + moderate motion + non-crazy ratio
    ratio = filtered["drift_ratio_bounded"].fillna(10.0)
    motion = np.clip(filtered["drift_motion"].fillna(0.0), 0, 1e3)
    dyn    = 1.0 / (1.0 + np.exp(-(np.log10(motion + 1e-6)+3.0)))   # squashed motion score
    penalty= (ratio > 5.0).astype(float)*0.4 + (ratio > 8.0).astype(float)*0.4
    filtered["rank_key"] = filtered["RFI_p95"].fillna(0)* (0.5 + 0.5*dyn) * (1.0 - penalty)

    cols = ["dataset","n_windows","RFI_p95","RFI_mean","C_mean","dH_abs","drift_motion","drift_ratio_bounded","policy_rate"]
    top = filtered.sort_values(["rank_key","RFI_p95","RFI_mean"], ascending=False)

    top_csv = OUT / "top_signals_filtered.csv"
    top[cols].head(50).to_csv(top_csv, index=False)

    print("== CNT_Lab Scoreboard (filtered top, up to 50) ==")
    print(top[cols].head(15).to_string(index=False))
    print("\nSaved:", top_csv)


== CNT_Lab Scoreboard (filtered top, up to 50) ==
                                                                               dataset  n_windows  RFI_p95  RFI_mean   C_mean   dH_abs  drift_motion  drift_ratio_bounded  policy_rate
                 artifacts__tables__genome3d__atlas__genes_v1__20251008-214043.parquet        661 0.939549  0.787247 0.792935 0.011407      0.031603             1.244647     0.045386
                artifacts__tables__genome3d__atlas__nodes_v0a__20251008-211232.parquet         96 0.888097  0.548545 0.561690 0.036146      0.118717             1.140666     0.093750
                artifacts__tables__genome3d__atlas__nodes_v0a__20251008-211922.parquet         96 0.888097  0.548545 0.561690 0.036146      0.118717             1.140666     0.093750
        artifacts__tables__genome3d__atlas__nodes_v1h_realhic__20251009-020445.parquet        661 0.917329  0.843031 0.848716 0.011348      0.030412             0.895404     0.024206
                artifacts__tables__

In [7]:
# === CNT Pillar Micro-Scores v0.3 ===
import numpy as np, pandas as pd
from pathlib import Path

OUT = Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars")
score_path = OUT / "lab_score.csv"
assert score_path.exists(), "Run the feature pass / scoreboard first."

score = pd.read_csv(score_path)

# 1) Strict filters: no virtualenv test data, no trivial 'summary' aggregates
def bad_file(s):
    s = str(s).lower()
    return any(tok in s for tok in [r"\.venv\\", "/.venv/", "gra_summary", "omni-summary", "overview", "summary.csv"])

score = score[~score["file"].apply(bad_file)].copy()
score = score.drop_duplicates(subset=["file"])

# 2) Take the strongest 30 by our prior key (fallback to RFI if missing)
if "rank_key" in score.columns:
    top = score.sort_values(["rank_key","RFI_p95","RFI_mean"], ascending=False).head(30).copy()
else:
    top = score.sort_values(["RFI_p95","RFI_mean"], ascending=False).head(30).copy()

def finite_mean(a):
    a = np.asarray(a, float)
    m = np.isfinite(a)
    return float(np.mean(a[m])) if m.any() else np.nan

def micro_scores(file_path, policy_rate):
    df = pd.read_csv(file_path, low_memory=False)

    # Pull what we can
    rfi = df["RFI"].to_numpy() if "RFI" in df.columns else np.full(1, np.nan)
    dH  = df["dH" ].to_numpy() if "dH"  in df.columns else np.full_like(rfi, np.nan)
    C   = df["C"  ].to_numpy() if "C"   in df.columns else np.full_like(rfi, np.nan)
    H   = df["H"  ].to_numpy() if "H"   in df.columns else np.full_like(rfi, np.nan)
    I0  = df["I_beta0"].to_numpy() if "I_beta0" in df.columns else np.full_like(rfi, np.nan)
    I1  = df["I_beta1"].to_numpy() if "I_beta1" in df.columns else np.full_like(rfi, np.nan)

    # E — “resonance when entropy falls”
    e_score = np.nanmean((rfi > 0.85) & (np.nan_to_num(dH) <= 0))

    # I — free-energy (lower better), z-scored to a [0,1]-ish sigmoid
    medC = np.nanmedian(C)
    lam  = (np.nanmedian(H) / medC) if (np.isfinite(medC) and medC > 0) else 1.0
    F    = H - lam * C
    Fz   = (F - np.nanmedian(F)) / (np.nanstd(F) + 1e-9)
    i_score = 1.0 / (1.0 + np.exp(np.nanmean(Fz)))  # lower F -> higher score

    # C — invariants drift slower than metrics
    def safe_grad(v):
        v = np.asarray(v, float)
        return np.gradient(v) if v.size >= 2 else np.zeros_like(v)
    inv_motion  = finite_mean(np.abs(safe_grad(I0))) + finite_mean(np.abs(safe_grad(I1)))
    metr_motion = finite_mean(np.abs(safe_grad(C)))  + finite_mean(np.abs(safe_grad(H)))
    c_score = (1 - np.clip(inv_motion / (metr_motion + 1e-6), 0, 1)) if np.isfinite(inv_motion) and np.isfinite(metr_motion) else np.nan

    # G — curvature proxy from local covariance (less negative curvature => higher score)
    Xcols = [v for v in [C, H, dH, rfi] if np.isfinite(v).any()]
    g_score = np.nan
    if len(Xcols) >= 3 and len(Xcols[0]) > 10:
        X = np.vstack(Xcols).T
        Cov = np.cov(np.nan_to_num(X, nan=0.0).T)
        sign, logdet = np.linalg.slogdet(Cov)
        neg_curv = max(0.0, -logdet)
        g_score  = 1.0 / (1.0 + neg_curv)

    # O — budget-sane policy (sweet spot ≈ 5%)
    pr = float(policy_rate) if np.isfinite(policy_rate) else np.nan
    o_score = np.exp(-((pr - 0.05)**2) / (2*0.05**2)) if np.isfinite(pr) else np.nan

    return dict(E=e_score, I=i_score, C=c_score, G=g_score, O=o_score)

rows = []
for _, r in top.iterrows():
    try:
        ms = micro_scores(r["file"], r.get("policy_rate", np.nan))
        rows.append(dict(dataset=r["dataset"], file=r["file"], **ms))
    except Exception as e:
        print("[skip micro]", r["file"], e)

pillars = pd.DataFrame(rows)
pillars["Composite"] = pillars[["E","I","C","G","O"]].mean(axis=1, skipna=True)
pillar_csv = OUT / "pillar_scores.csv"
pillars.sort_values("Composite", ascending=False).to_csv(pillar_csv, index=False)

print("== Pillar micro-scores (top 12) ==")
print(pillars.sort_values("Composite", ascending=False).head(12).to_string(index=False))
print("\nSaved:", pillar_csv)


== Pillar micro-scores (top 12) ==
                                                                            dataset                                                                                                                                                file   E   I   C   G        O  Composite
                                 artifacts__tables__migrated__cm-eoec__d840b959.csv                                  C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\features__artifacts__tables__migrated__cm-eoec__d840b959.csv.csv 1.0 0.5 1.0 NaN 0.606531   0.776633
                            artifacts__tables__migrated__cm-task-rest__92049ff5.csv                             C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\features__artifacts__tables__migrated__cm-task-rest__92049ff5.csv.csv 1.0 0.5 1.0 NaN 0.606531   0.776633
                     artifacts__tables__migrated__cnt-eeg-erd-summary__5f7da9e8.csv                      C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\featur

In [8]:
# === CNT Pillar Micro-Scores v0.31 (STRICT) ===
import numpy as np, pandas as pd
from pathlib import Path

ROOT = Path(r"C:\Users\caleb\CNT_Lab")
OUT  = ROOT / "artifacts" / "cnt_five_pillars"
lab   = OUT / "lab_score.csv"
tops  = OUT / "top_signals_filtered.csv"

assert lab.exists() and tops.exists(), "Missing lab_score.csv or top_signals_filtered.csv"

score = pd.read_csv(lab)
topf  = pd.read_csv(tops)

# strict filters
BAD_TOKENS = {"summary","overview","omni-summary","gra_summary",
              "cm-eoec","cm-task-rest","condition-accuracy",
              "composition-old","dwell-by-id",".venv\\"}

def bad_name(s):
    s = str(s).lower()
    return any(t in s for t in BAD_TOKENS)

ok = (
    (score["n_windows"] >= 64) &
    (score["drift_motion"].fillna(0) >= 1e-4) &
    (~score["dataset"].apply(bad_name)) &
    (~score["file"].str.lower().str.contains(r"\\\.venv\\|/\.venv/"))
)

strict = score.loc[ok].copy()

# keep only candidates that appeared in filtered top list
strict = strict[strict["dataset"].isin(set(topf["dataset"]))].drop_duplicates("file")

def safe_grad(v):
    v = np.asarray(v, float)
    return np.gradient(v) if v.size >= 2 else np.zeros_like(v)

def finite_mean(a):
    a = np.asarray(a, float)
    m = np.isfinite(a)
    return float(np.mean(a[m])) if m.any() else np.nan

def micro_scores(file_path, policy_rate):
    df = pd.read_csv(file_path, low_memory=False)
    N  = len(df)

    rfi = df["RFI"].to_numpy() if "RFI" in df.columns else np.full(1, np.nan)
    dH  = df["dH" ].to_numpy() if "dH"  in df.columns else np.full_like(rfi, np.nan)
    C   = df["C"  ].to_numpy() if "C"   in df.columns else np.full_like(rfi, np.nan)
    H   = df["H"  ].to_numpy() if "H"   in df.columns else np.full_like(rfi, np.nan)
    I0  = df["I_beta0"].to_numpy() if "I_beta0" in df.columns else np.full_like(rfi, np.nan)
    I1  = df["I_beta1"].to_numpy() if "I_beta1" in df.columns else np.full_like(rfi, np.nan)

    # E — “resonance when entropy non-increasing”
    E = np.nanmean((rfi > 0.85) & (np.nan_to_num(dH) <= 0))

    # I — free-energy: lower H - λC is better
    lam  = (np.nanmedian(H) / max(np.nanmedian(C), 1e-9)) if np.isfinite(np.nanmedian(C)) else 1.0
    F    = H - lam*C
    Fz   = (F - np.nanmedian(F)) / (np.nanstd(F) + 1e-9)
    I    = 1.0 / (1.0 + np.exp(np.nanmean(Fz)))  # ~1 if free-energy below typical

    # C — invariants drift slower than metrics
    inv_motion  = finite_mean(np.abs(safe_grad(I0))) + finite_mean(np.abs(safe_grad(I1)))
    metr_motion = finite_mean(np.abs(safe_grad(C)))  + finite_mean(np.abs(safe_grad(H)))
    Cscore = (1 - np.clip(inv_motion / (metr_motion + 1e-6), 0, 1)) if np.isfinite(inv_motion) and np.isfinite(metr_motion) else np.nan

    # G — curvature proxy needs depth
    G = np.nan
    if N >= 64 and np.isfinite(C).sum()>10 and np.isfinite(H).sum()>10:
        X = np.vstack([np.nan_to_num(C, nan=0.0),
                       np.nan_to_num(H, nan=0.0),
                       np.nan_to_num(dH, nan=0.0),
                       np.nan_to_num(rfi, nan=0.0)]).T
        Cov = np.cov(X.T)
        sign, logdet = np.linalg.slogdet(Cov)
        neg_curv = max(0.0, -logdet)  # larger = worse curvature
        G = 1.0 / (1.0 + neg_curv)

    # O — budget-sane policy (sweet spot ≈ 5%)
    pr = float(policy_rate) if np.isfinite(policy_rate) else np.nan
    O = np.exp(-((pr - 0.05)**2) / (2*0.05**2)) if np.isfinite(pr) else np.nan

    return dict(E=E, I=I, C=Cscore, G=G, O=O, n=N)

rows=[]
for _, r in strict.iterrows():
    try:
        ms = micro_scores(r["file"], r.get("policy_rate", np.nan))
        rows.append(dict(dataset=r["dataset"], file=r["file"], **ms))
    except Exception as e:
        print("[skip micro]", r["file"], e)

pillars = pd.DataFrame(rows)
# Weighted composite (favor E/I/C; include G, gentle weight on O)
w = dict(E=0.3, I=0.25, C=0.2, G=0.15, O=0.1)
def wmean(row):
    num, den = 0.0, 0.0
    for k, wk in w.items():
        if np.isfinite(row.get(k, np.nan)):
            num += wk*row[k]; den += wk
    return num/den if den>0 else np.nan

pillars["Composite"] = pillars.apply(wmean, axis=1)
pillars = pillars.sort_values("Composite", ascending=False)

out_csv = OUT / "pillar_scores_strict.csv"
pillars.to_csv(out_csv, index=False)

# Convenience export for the Field Law Sheet
sheet_cols = ["dataset","E","I","C","G","O","Composite"]
(pillars[sheet_cols].head(12)
         .to_csv(OUT/"results_for_sheet.csv", index=False))

print("== Pillar micro-scores (STRICT top 12) ==")
print(pillars[sheet_cols].head(12).to_string(index=False))
print("\nSaved:\n -", out_csv, "\n -", OUT/"results_for_sheet.csv")


== Pillar micro-scores (STRICT top 12) ==
                                                                           dataset        E        I        C        G        O  Composite
.venv__Lib__site-packages__statsmodels__discrete__tests__results__yhat_poisson.csv 0.227273 0.500682 1.000000 0.034426 0.606531   0.459169
              artifacts__tables__migrated__cnt-genomic-resonance-map__df629623.csv 0.004294 0.542254 1.000000 0.026214 0.606531   0.401437
                              artifacts__tables__migrated__sim-theta__fc536f2f.csv 0.000000 0.529244 1.000000 0.016974 0.606531   0.395510
  .venv__Lib__site-packages__statsmodels__genmod__tests__results__inv_gaussian.csv 0.000000 0.503146 1.000000 0.021954 0.606531   0.389733
                              artifacts__tables__migrated__sim-alpha__f44f6f05.csv 0.000000 0.500948 1.000000 0.017312 0.606531   0.388487
    artifacts__tables__genome3d__atlas__nodes_v1h_realhic__20251009-020445.parquet 0.416036 0.419484 0.104625 0.033268 0.875

In [9]:
# === CNT Strict Filter v1.2 — real vs synth, nuke underscored .venv ===
import re, numpy as np, pandas as pd
from pathlib import Path

ROOT = Path(r"C:\Users\caleb\CNT_Lab")
OUT  = ROOT / "artifacts" / "cnt_five_pillars"
lab  = OUT / "lab_score.csv"
tops = OUT / "top_signals_filtered.csv"

score = pd.read_csv(lab)
topf  = pd.read_csv(tops)

VENV_PAT = re.compile(r"(?:^|[_/\\\.-])venv(?:$|[_/\\\.-])|site[-_]?packages|statsmodels|genmod|tests|results", re.IGNORECASE)
JUNK_PAT = re.compile(r"summary|overview|omni-summary|gra_summary|dwell-by-id", re.IGNORECASE)
SYN_PAT  = re.compile(r"\b(sim|synthetic|ising|kuramoto|saddlenode)\b", re.IGNORECASE)

def is_junk_row(row):
    return bool(
        VENP := VENP if (VENP:=False) else False or
        VENP or VENP
    )

def bad_name(s): return bool(JUNK_PAT.search(str(s)))
def has_venv(s): return bool(VENV_PAT.search(str(s)))
def is_synth(s): return bool(SYN_PAT.search(str(s)))

# depth / motion thresholds
MIN_WINDOWS = 64
MOTION_MIN  = 1e-4

# strict pool drawn from the filtered top list
pool = score.merge(topf[["dataset"]].drop_duplicates(), on="dataset", how="inner")
pool["is_bad"]   = pool["dataset"].apply(bad_name) | pool["file"].apply(has_venv)
pool["is_synth"] = pool["dataset"].apply(is_synth)

strict = pool[
    (~pool["is_bad"]) &
    (pool["n_windows"] >= MIN_WINDOWS) &
    (pool["drift_motion"].fillna(0) >= MOTION_MIN)
].drop_duplicates("file")

real  = strict[~strict["is_synth"]].copy()
synth = strict[ strict["is_synth"]].copy()

print(f"[kept] real={len(real)}  synth={len(synth)}  (from {len(pool)})")
real.to_csv(OUT/"strict_candidates_real.csv", index=False)
synth.to_csv(OUT/"strict_candidates_synth.csv", index=False)
print("Saved real/synth candidate lists.")


[kept] real=22  synth=0  (from 50)
Saved real/synth candidate lists.


In [10]:
# === Pillar Scores v1.2 — robust invariants fallback + real/synth tables ===
import numpy as np, pandas as pd
from pathlib import Path

OUT = Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars")

real = pd.read_csv(OUT/"strict_candidates_real.csv")
synth= pd.read_csv(OUT/"strict_candidates_synth.csv")

def ema(x, alpha=0.02):
    x = np.asarray(x, float)
    y = np.empty_like(x); m = np.isfinite(x); 
    if not m.any(): return np.full_like(x, np.nan)
    y[:] = np.nan; last = x[m][0]
    for i,xi in enumerate(x):
        if np.isfinite(xi): last = alpha*xi + (1-alpha)*last
        y[i]=last
    return y

def micro_scores(file_path, policy_rate):
    df = pd.read_csv(file_path, low_memory=False)
    N  = len(df)

    rfi = df.get("RFI", pd.Series([np.nan]*N)).to_numpy()
    dH  = df.get("dH",  pd.Series([np.nan]*N)).to_numpy()
    C   = df.get("C",   pd.Series([np.nan]*N)).to_numpy()
    H   = df.get("H",   pd.Series([np.nan]*N)).to_numpy()

    # Invariants: use provided; else slow EMA proxies (very low-frequency)
    I0  = (df["I_beta0"].to_numpy() if "I_beta0" in df.columns else ema(C, alpha=0.01))
    I1  = (df["I_beta1"].to_numpy() if "I_beta1" in df.columns else ema(H, alpha=0.01))

    # E — resonance with non-increasing entropy
    E = np.nanmean((rfi > 0.85) & (np.nan_to_num(dH) <= 0))

    # I — free-energy H - λC (lower is better)
    Cmed = np.nanmedian(C); lam = (np.nanmedian(H)/max(Cmed,1e-9)) if np.isfinite(Cmed) else 1.0
    F  = H - lam*C
    Fz = (F - np.nanmedian(F)) / (np.nanstd(F)+1e-9)
    I  = 1.0 / (1.0 + np.exp(np.nanmean(Fz)))

    # C — invariants drift slower than metrics (ratio; smaller is better)
    def motion(v): 
        v = np.asarray(v, float)
        if v.size<2: return np.nan
        g = np.gradient(v)
        g = g[np.isfinite(g)]
        return float(np.mean(np.abs(g))) if g.size else np.nan

    inv_m  = np.nansum([motion(I0), motion(I1)])
    metr_m = np.nansum([motion(C),  motion(H)])
    Cscore = np.nan
    if np.isfinite(inv_m) and np.isfinite(metr_m) and metr_m>0:
        Cscore = 1 - np.clip(inv_m / (metr_m + 1e-9), 0, 1)  # 1 = invariants much steadier

    # G — curvature proxy via logdet(Cov)
    G = np.nan
    if N >= 64:
        X = np.vstack([np.nan_to_num(C,0), np.nan_to_num(H,0),
                       np.nan_to_num(dH,0), np.nan_to_num(rfi,0)]).T
        Cov = np.cov(X.T)
        sign, logdet = np.linalg.slogdet(Cov)
        G = 1.0 / (1.0 + max(0.0, -logdet))

    # O — policy budget sweet spot ~5%
    pr = float(policy_rate) if np.isfinite(policy_rate) else np.nan
    O  = np.exp(-((pr - 0.05)**2)/(2*0.05**2)) if np.isfinite(pr) else np.nan

    return dict(E=E, I=I, C=Cscore, G=G, O=O, n=N)

def rescore(df):
    rows=[]
    for _,r in df.iterrows():
        try:
            ms = micro_scores(r["file"], r.get("policy_rate", np.nan))
            rows.append(dict(dataset=r["dataset"], file=r["file"], **ms))
        except Exception as e:
            print("[skip]", r["file"], e)
    pill = pd.DataFrame(rows)
    w = dict(E=0.3, I=0.25, C=0.2, G=0.15, O=0.1)
    def wmean(row):
        num=den=0.0
        for k, wk in w.items():
            if np.isfinite(row.get(k, np.nan)):
                num += wk*row[k]; den += wk
        return num/den if den else np.nan
    pill["Composite"] = pill.apply(wmean, axis=1)
    return pill.sort_values("Composite", ascending=False)

real_p  = rescore(real)
synth_p = rescore(synth)

real_p.to_csv(OUT/"pillar_scores_real.csv", index=False)
synth_p.to_csv(OUT/"pillar_scores_synth.csv", index=False)

print("== REAL top 10 ==")
print(real_p[["dataset","E","I","C","G","O","Composite"]].head(10).to_string(index=False))
print("\n== SYNTH top 5 ==")
print(synth_p[["dataset","E","I","C","G","O","Composite"]].head(5).to_string(index=False))
print("\nSaved:\n -", OUT/"pillar_scores_real.csv", "\n -", OUT/"pillar_scores_synth.csv")


== REAL top 10 ==
                                                                       dataset        E        I        C        G        O  Composite
          artifacts__tables__migrated__cnt-genomic-resonance-map__df629623.csv 0.004294 0.542254 1.000000 0.026214 0.606531   0.401437
                          artifacts__tables__migrated__sim-theta__fc536f2f.csv 0.000000 0.529244 1.000000 0.016974 0.606531   0.395510
                          artifacts__tables__migrated__sim-alpha__f44f6f05.csv 0.000000 0.500948 1.000000 0.017312 0.606531   0.388487
artifacts__tables__genome3d__atlas__nodes_v1h_realhic__20251009-020445.parquet 0.416036 0.419484 0.104596 0.033268 0.875405   0.343132
        artifacts__tables__genome3d__atlas__nodes_v1h__20251008-215623.parquet 0.411498 0.413112 0.054040 0.033139 0.661432   0.308649
         artifacts__tables__genome3d__atlas__genes_v1__20251008-214043.parquet 0.340393 0.394727 0.000000 0.037155 0.995751   0.305948
                       artifacts__tab

KeyError: "['dataset', 'E', 'I', 'C', 'G', 'O'] not in index"

In [11]:
# CNT Five-Pillar — Single Mega Cell (rescore + robust fallbacks)
# Telos | CNT_Lab
import re, warnings, numpy as np, pandas as pd
from pathlib import Path

# -----------------------------
# 0) Paths & I/O setup
# -----------------------------
ROOT = Path(r"C:\Users\caleb\CNT_Lab")
OUT  = ROOT / "artifacts" / "cnt_five_pillars"
OUT.mkdir(parents=True, exist_ok=True)

warnings.filterwarnings("ignore", category=RuntimeWarning)

def exists(p: Path) -> bool:
    try: return p.exists()
    except Exception: return False

# Prefer the strict lists you just wrote; fall back gracefully if missing
STRICT_REAL  = OUT / "strict_candidates_real.csv"
STRICT_SYNTH = OUT / "strict_candidates_synth.csv"
LAB_SCORE    = OUT / "lab_score.csv"
TOP_FILTERED = OUT / "top_signals_filtered.csv"
PILLAR_SHEET = OUT / "pillar_scores.csv"  # earlier wide pillar dump (if present)

# -----------------------------
# 1) Light utilities
# -----------------------------
def ema(x, alpha=0.02):
    x = np.asarray(x, float)
    if x.size == 0: return x
    y = np.empty_like(x); y[:] = np.nan
    # seed with first finite obs if any
    m = np.isfinite(x)
    if not m.any(): return y
    last = x[m][0]
    for i, xi in enumerate(x):
        if np.isfinite(xi):
            last = alpha*xi + (1-alpha)*last
        y[i] = last
    return y

def motion(v):
    v = np.asarray(v, float)
    if v.size < 2: return np.nan
    g = np.gradient(v)
    g = g[np.isfinite(g)]
    return float(np.mean(np.abs(g))) if g.size else np.nan

def safe_read_csv(path: Path) -> pd.DataFrame:
    try:
        return pd.read_csv(path, low_memory=False)
    except Exception as e:
        # last-ditch: try python engine
        return pd.read_csv(path, low_memory=False, engine="python")

# -----------------------------
# 2) Micro-scores with robust fallbacks
#     E, I, C, G, O + n
# -----------------------------
def micro_scores(file_path, policy_rate):
    df = safe_read_csv(Path(file_path))
    N  = len(df)

    # pull columns or stand in with NaNs
    rfi = df["RFI"].to_numpy() if "RFI" in df.columns else np.full(N, np.nan)
    dH  = df["dH" ].to_numpy() if "dH"  in df.columns else np.full(N, np.nan)
    C   = df["C"  ].to_numpy() if "C"   in df.columns else np.full(N, np.nan)
    H   = df["H"  ].to_numpy() if "H"   in df.columns else np.full(N, np.nan)

    # Invariants: provided or ultra-slow EMA proxies (placeholder)
    I0  = (df["I_beta0"].to_numpy() if "I_beta0" in df.columns else ema(C, alpha=0.01))
    I1  = (df["I_beta1"].to_numpy() if "I_beta1" in df.columns else ema(H, alpha=0.01))

    # E — resonance with non-increasing entropy
    E = np.nan
    if np.isfinite(rfi).any() and np.isfinite(dH).any():
        E = float(np.nanmean((rfi > 0.85) & (np.nan_to_num(dH) <= 0)))

    # I — glyphic free-energy H - λC (lower is better)
    Cmed = np.nanmedian(C)
    lam  = (np.nanmedian(H)/max(Cmed,1e-9)) if np.isfinite(Cmed) else 1.0
    F    = H - lam*C
    Fz   = (F - np.nanmedian(F)) / (np.nanstd(F)+1e-9) if np.isfinite(F).any() else np.full_like(F, np.nan)
    I    = 1.0 / (1.0 + np.exp(np.nanmean(Fz))) if np.isfinite(Fz).any() else np.nan

    # C — invariants drift slower than metrics (ratio; smaller is better)
    inv_m  = np.nansum([motion(I0), motion(I1)])
    metr_m = np.nansum([motion(C),  motion(H)])
    Cscore = np.nan
    eps    = 1e-4  # motion floor
    if np.isfinite(inv_m) and np.isfinite(metr_m):
        if metr_m < eps and inv_m < eps:
            Cscore = np.nan  # nothing moves: don't award a free 1.0
        elif metr_m >= eps:
            Cscore = 1 - np.clip(inv_m / (metr_m + 1e-9), 0, 1)

    # G — curvature proxy via logdet(Cov) of [C,H,dH,RFI]
    G = np.nan
    if N >= 64:
        X = np.vstack([
            np.nan_to_num(C,  0.0),
            np.nan_to_num(H,  0.0),
            np.nan_to_num(dH, 0.0),
            np.nan_to_num(rfi,0.0)
        ]).T
        try:
            Cov = np.cov(X.T)
            sign, logdet = np.linalg.slogdet(Cov)
            G = 1.0 / (1.0 + max(0.0, -logdet))
        except Exception:
            G = np.nan

    # O — policy budget sweet spot ~5%
    pr = float(policy_rate) if pd.notna(policy_rate) else np.nan
    O  = float(np.exp(-((pr - 0.05)**2)/(2*0.05**2))) if np.isfinite(pr) else np.nan

    return dict(E=E, I=I, C=Cscore, G=G, O=O, n=N)

# -----------------------------
# 3) Candidate loading & rescoring
# -----------------------------
SYN_PAT = re.compile(
    r"(?:^|[^A-Za-z0-9])(?:(?:sim(?:[-_]|$))|ising|kuramoto|saddle[-_]?node|synthetic)",
    re.IGNORECASE
)

def is_synth_name(s: str) -> bool:
    s = str(s)
    return bool(SYN_PAT.search(s))

def attach_policy_rate(df: pd.DataFrame) -> pd.DataFrame:
    # try to merge a policy rate from lab_score.csv if present
    if exists(LAB_SCORE):
        try:
            lab = pd.read_csv(LAB_SCORE)
            cols = [c for c in lab.columns if c.lower() == "policy_rate"]
            if "dataset" in lab.columns and cols:
                df = df.merge(lab[["dataset", cols[0]]].rename(columns={cols[0]:"policy_rate"}),
                              on="dataset", how="left")
        except Exception:
            pass
    if "policy_rate" not in df.columns:
        df["policy_rate"] = np.nan
    return df

def load_candidates():
    real = synth = None
    if exists(STRICT_REAL):
        real = pd.read_csv(STRICT_REAL)
    if exists(STRICT_SYNTH):
        synth = pd.read_csv(STRICT_SYNTH)
    # Fallbacks
    if real is None or ("file" not in real.columns):
        # try pillar sheet
        if exists(PILLAR_SHEET):
            tmp = pd.read_csv(PILLAR_SHEET)
            pick = ["dataset","file","policy_rate"]
            real = tmp[pick].drop_duplicates() if all(c in tmp.columns for c in pick) else tmp.rename(columns=lambda c: c.strip())
        elif exists(TOP_FILTERED):
            tmp = pd.read_csv(TOP_FILTERED)
            # require at least dataset, try to infer file path column name
            cand = tmp.copy()
            file_col = next((c for c in cand.columns if c.lower() in ("file","path","source","fullpath")), None)
            if file_col is None:
                cand["file"] = cand["dataset"].apply(lambda d: "")
                file_col = "file"
            real = cand[["dataset", file_col]].rename(columns={file_col:"file"})
        else:
            real = pd.DataFrame(columns=["dataset","file"])
    if synth is None or ("file" not in synth.columns):
        synth = pd.DataFrame(columns=["dataset","file"])
    # Standardize
    for df in (real, synth):
        if "dataset" not in df.columns: df["dataset"] = ""
        if "file" not in df.columns:    df["file"]    = ""
    real = attach_policy_rate(real)
    synth= attach_policy_rate(synth)
    # If synth empty, try name-based split from 'real'
    if synth.empty and not real.empty:
        m = real["dataset"].astype(str).apply(is_synth_name) | real["file"].astype(str).apply(is_synth_name)
        synth = real[m].copy()
        real  = real[~m].copy()
    return real.drop_duplicates(subset=["file"]), synth.drop_duplicates(subset=["file"])

def rescore(df: pd.DataFrame) -> pd.DataFrame:
    rows=[]
    for _, r in df.iterrows():
        fpath = r.get("file","")
        if not fpath or not exists(Path(fpath)):
            # skip non-existent files silently
            continue
        try:
            ms = micro_scores(fpath, r.get("policy_rate", np.nan))
            rows.append(dict(dataset=r["dataset"], file=fpath, policy_rate=r.get("policy_rate", np.nan), **ms))
        except Exception as e:
            print("[skip]", fpath, e)
    pill = pd.DataFrame(rows)
    if pill.empty: return pill
    # Weighted composite (tolerant to NaNs)
    w = dict(E=0.30, I=0.25, C=0.20, G=0.15, O=0.10)
    def wmean(row):
        num=den=0.0
        for k, wk in w.items():
            v = row.get(k, np.nan)
            if pd.notna(v):
                num += wk*float(v); den += wk
        return num/den if den else np.nan
    pill["Composite"] = pill.apply(wmean, axis=1)
    cols = ["dataset","E","I","C","G","O","Composite","n","policy_rate","file"]
    return pill.reindex(columns=cols).sort_values("Composite", ascending=False, na_position="last")

# -----------------------------
# 4) Run + save
# -----------------------------
real_in, synth_in = load_candidates()

real_p  = rescore(real_in)
synth_p = rescore(synth_in)

real_p.to_csv(OUT/"pillar_scores_real.csv",  index=False)
synth_p.to_csv(OUT/"pillar_scores_synth.csv", index=False)

# Friendly prints without KeyErrors
def print_table(df: pd.DataFrame, k=10, title=""):
    print(title)
    if df.empty:
        print("(none)")
        return
    keep = [c for c in ["dataset","E","I","C","G","O","Composite"] if c in df.columns]
    print(df[keep].head(k).to_string(index=False))

print("== REAL top 10 ==")
print_table(real_p, 10)

print("\n== SYNTH top 5 ==")
print_table(synth_p, 5)

# Optional: a compact sheet for dashboards
sheet_cols = ["dataset","Composite","E","I","C","G","O","n","policy_rate","file"]
sheet = pd.concat([real_p.assign(kind="real"), synth_p.assign(kind="synth")], axis=0, ignore_index=True)
sheet = sheet.reindex(columns=(["kind"]+sheet_cols))
sheet.to_csv(OUT/"pillar_scores_sheet.csv", index=False)

print("\nSaved:")
print(" -", OUT/"pillar_scores_real.csv")
print(" -", OUT/"pillar_scores_synth.csv")
print(" -", OUT/"pillar_scores_sheet.csv")


== REAL top 10 ==

                                                                       dataset        E        I        C        G   O  Composite
          artifacts__tables__migrated__cnt-genomic-resonance-map__df629623.csv 0.004294 0.542254 1.000000 0.026214 NaN   0.378649
artifacts__tables__genome3d__atlas__nodes_v1h_realhic__20251009-020445.parquet 0.416036 0.419484 0.104596 0.033268 NaN   0.283990
        artifacts__tables__genome3d__atlas__nodes_v1h__20251008-215623.parquet 0.411498 0.413112 0.054040 0.033139 NaN   0.269451
                       artifacts__tables__migrated__gdf-snapshot__d8dc9743.csv 0.511111 0.318376 0.000000 0.035062 NaN   0.264652
         artifacts__tables__genome3d__atlas__genes_v1__20251008-214043.parquet 0.340393 0.394727 0.000000 0.037155 NaN   0.229303
        artifacts__tables__genome3d__atlas__nodes_v0a__20251008-211232.parquet 0.083333 0.583529 0.000000 0.038379 NaN   0.196266
        artifacts__tables__genome3d__atlas__nodes_v0a__20251008-211922.

In [12]:
# === CNT Five-Pillars: Score Repair + Strict Picks (v2, single cell) ===
# - Fills missing O (policy pillar) with open-loop fallback (pr_fallback=0.0 -> O=exp(-0.5))
# - Recomputes Composite with weights: E=.30, I=.25, C=.20, G=.15, O=.10
# - Adds pillar driver breakdown (weighted contributions)
# - Saves v2 sheets + strict pick lists

import numpy as np, pandas as pd
from pathlib import Path

ROOT = Path(r"C:\Users\caleb\CNT_Lab")
OUT  = ROOT / "artifacts" / "cnt_five_pillars"
OUT.mkdir(parents=True, exist_ok=True)

# inputs produced in your last run
REAL_IN   = OUT / "pillar_scores_real.csv"
SYNTH_IN  = OUT / "pillar_scores_synth.csv"
LAB_SCORE = OUT / "lab_score.csv"  # optional source of policy_rate by dataset

# config
W = dict(E=0.30, I=0.25, C=0.20, G=0.15, O=0.10)
PR_FALLBACK = 0.00  # open-loop budget if unknown => O = exp(-((0-0.05)^2)/(2*0.05^2)) ~ 0.606531
O_from_pr = lambda pr: float(np.exp(-((float(pr) - 0.05)**2)/(2*0.05**2)))

def load_scores(path: Path) -> pd.DataFrame:
    if not path.exists(): return pd.DataFrame()
    df = pd.read_csv(path)
    # normalize column names
    df.columns = [c.strip() for c in df.columns]
    return df

def merge_policy_rate(df: pd.DataFrame) -> pd.DataFrame:
    if df.empty: return df.assign(policy_rate=np.nan)
    if LAB_SCORE.exists():
        try:
            lab = pd.read_csv(LAB_SCORE)
            # try to find the policy rate column name robustly
            pr_col = next((c for c in lab.columns if c.lower() == "policy_rate"), None)
            if pr_col and "dataset" in lab.columns:
                df = df.merge(lab[["dataset", pr_col]].rename(columns={pr_col:"policy_rate"}),
                              on="dataset", how="left")
            else:
                if "policy_rate" not in df.columns:
                    df["policy_rate"] = np.nan
        except Exception:
            if "policy_rate" not in df.columns:
                df["policy_rate"] = np.nan
    else:
        if "policy_rate" not in df.columns:
            df["policy_rate"] = np.nan
    return df

def fix_O_and_composite(df: pd.DataFrame) -> pd.DataFrame:
    if df.empty: return df
    # compute/repair O
    if "O" not in df.columns: df["O"] = np.nan
    # prefer existing policy_rate → O; else fill fallback
    pr = df.get("policy_rate", pd.Series([np.nan]*len(df)))
    Ocalc = pr.apply(lambda x: O_from_pr(x) if pd.notna(x) else O_from_pr(PR_FALLBACK))
    # if a row already had O but NaN, fill it; otherwise respect existing finite O
    df["O"] = np.where(np.isfinite(df["O"]), df["O"], Ocalc)

    # recompute Composite with current pillars, ignoring missing terms
    def wmean(row):
        num = den = 0.0
        for k, wk in W.items():
            v = row.get(k, np.nan)
            if pd.notna(v):
                num += wk * float(v); den += wk
        return num/den if den else np.nan
    df["Composite"] = df.apply(wmean, axis=1)

    # pillar driver contributions (how much each pillar adds to Composite)
    for k, wk in W.items():
        df[f"contrib_{k}"] = wk * df.get(k, np.nan)
    # main driver label
    contrib_cols = [f"contrib_{k}" for k in W]
    df["driver"] = df[contrib_cols].idxmax(axis=1).str.replace("contrib_","",regex=False)

    return df

def strict_picks(df: pd.DataFrame, kind="real", top_k=10, q=0.90) -> pd.DataFrame:
    if df.empty: return df
    df = df.sort_values("Composite", ascending=False)
    # quantile gate + ensure at least top_k rows
    thresh = df["Composite"].quantile(q) if df["Composite"].notna().any() else -np.inf
    gate = df[df["Composite"] >= thresh]
    out = (gate if len(gate) >= top_k else df.head(top_k)).copy()
    out.insert(0, "kind", kind)
    return out

# load
real  = load_scores(REAL_IN)
synth = load_scores(SYNTH_IN)

# attach policy_rate if available and repair O + Composite
real  = fix_O_and_composite(merge_policy_rate(real)).assign(kind="real")
synth = fix_O_and_composite(merge_policy_rate(synth)).assign(kind="synth")

# save v2 sheets
REAL_V2  = OUT / "pillar_scores_real_v2.csv"
SYNTH_V2 = OUT / "pillar_scores_synth_v2.csv"
SHEET_V2 = OUT / "pillar_scores_sheet_v2.csv"

real.to_csv(REAL_V2, index=False)
synth.to_csv(SYNTH_V2, index=False)
pd.concat([real, synth], ignore_index=True).to_csv(SHEET_V2, index=False)

# strict picks and export
real_pick  = strict_picks(real,  "real",  top_k=10, q=0.90)
synth_pick = strict_picks(synth, "synth", top_k=5,  q=0.90)

REAL_PICK = OUT / "strict_picks_real_v2.csv"
SYN_PICK  = OUT / "strict_picks_synth_v2.csv"
pd.concat([real_pick, synth_pick], ignore_index=True).to_csv(OUT/"strict_picks_all_v2.csv", index=False)
real_pick.to_csv(REAL_PICK, index=False)
synth_pick.to_csv(SYN_PICK, index=False)

# pretty print
def ptab(df, k=10, title=""):
    if df.empty:
        print(title, "\n(none)\n"); return
    keep = [c for c in ["dataset","E","I","C","G","O","Composite","driver"] if c in df.columns]
    print(title)
    print(df.sort_values("Composite", ascending=False)[keep].head(k).to_string(index=False), "\n")

ptab(real,  10, "== REAL top 10 (repaired) ==")
ptab(synth,  5, "== SYNTH top 5 (repaired) ==")

print("Saved:")
print(" -", REAL_V2)
print(" -", SYNTH_V2)
print(" -", SHEET_V2)
print(" -", REAL_PICK)
print(" -", SYN_PICK)
print(" -", OUT / "strict_picks_all_v2.csv")


ValueError: cannot insert kind, already exists

In [13]:
# === CNT Five-Pillars — v2.1 Hotfix (O fill + 'kind' reinsert guard) ===
import numpy as np, pandas as pd
from pathlib import Path

ROOT = Path(r"C:\Users\caleb\CNT_Lab")
OUT  = ROOT / "artifacts" / "cnt_five_pillars"
OUT.mkdir(parents=True, exist_ok=True)

REAL_IN   = OUT / "pillar_scores_real.csv"
SYNTH_IN  = OUT / "pillar_scores_synth.csv"
LAB_SCORE = OUT / "lab_score.csv"   # optional policy_rate per dataset

# Weights and policy mapping
W = dict(E=0.30, I=0.25, C=0.20, G=0.15, O=0.10)
PR_FALLBACK = 0.00  # open-loop baseline -> O ≈ exp(-0.5)
def O_from_pr(pr): 
    pr = float(pr)
    return float(np.exp(-((pr - 0.05)**2)/(2*0.05**2)))

def load_df(path: Path) -> pd.DataFrame:
    if not path.exists(): 
        return pd.DataFrame()
    df = pd.read_csv(path, low_memory=False)
    df.columns = [c.strip() for c in df.columns]
    return df

def attach_policy_rate(df: pd.DataFrame) -> pd.DataFrame:
    if df.empty: 
        return df.assign(policy_rate=np.nan)
    if "policy_rate" not in df.columns:
        df["policy_rate"] = np.nan
    if LAB_SCORE.exists():
        try:
            lab = pd.read_csv(LAB_SCORE)
            lab.columns = [c.strip() for c in lab.columns]
            pr_col = next((c for c in lab.columns if c.lower()=="policy_rate"), None)
            if pr_col and "dataset" in lab.columns:
                df = df.merge(lab[["dataset", pr_col]].rename(columns={pr_col:"policy_rate"}),
                              on="dataset", how="left", suffixes=("","_lab"))
                # prefer lab policy_rate if present
                df["policy_rate"] = df["policy_rate_lab"].combine_first(df["policy_rate"])
                df.drop(columns=[c for c in df.columns if c.endswith("_lab")], inplace=True)
        except Exception as e:
            print("[warn] lab_score merge skipped:", e)
    return df

def coerce_numeric(df: pd.DataFrame, cols) -> None:
    for c in cols:
        if c in df.columns:
            df[c] = pd.to_numeric(df[c], errors="coerce")

def repair_scores(df: pd.DataFrame) -> pd.DataFrame:
    if df.empty: return df
    # ensure numeric pillars
    coerce_numeric(df, ["E","I","C","G","O","Composite","policy_rate"])
    # compute O from policy_rate when missing; fallback to open-loop otherwise
    pr_series = df["policy_rate"]
    Ocalc = pr_series.apply(lambda x: O_from_pr(x) if pd.notna(x) else O_from_pr(PR_FALLBACK))
    if "O" not in df.columns:
        df["O"] = Ocalc
    else:
        # if O is NaN or non-finite, replace with Ocalc
        O_num = pd.to_numeric(df["O"], errors="coerce")
        df["O"] = np.where(np.isfinite(O_num), O_num, Ocalc)

    # recompute Composite with weights, ignoring missing pieces
    def wmean(row):
        num = den = 0.0
        for k,wk in W.items():
            v = row.get(k, np.nan)
            if pd.notna(v):
                num += wk*float(v); den += wk
        return num/den if den else np.nan
    df["Composite"] = df.apply(wmean, axis=1)

    # contributions + driver
    for k,wk in W.items():
        df[f"contrib_{k}"] = wk * df.get(k, np.nan)
    contrib_cols = [f"contrib_{k}" for k in W]
    df["driver"] = df[contrib_cols].idxmax(axis=1).str.replace("contrib_","",regex=False)
    return df

def strict_picks(df: pd.DataFrame, kind: str, top_k=10, q=0.90) -> pd.DataFrame:
    if df.empty: return df
    df = df.sort_values("Composite", ascending=False)
    thresh = df["Composite"].quantile(q) if df["Composite"].notna().any() else -np.inf
    gate = df[df["Composite"] >= thresh]
    out = (gate if len(gate) >= top_k else df.head(top_k)).copy()
    # don’t re-insert 'kind' if present
    if "kind" in out.columns:
        out["kind"] = kind
        cols = ["kind"] + [c for c in out.columns if c!="kind"]
        out = out[cols]
    else:
        out.insert(0, "kind", kind)
    return out

def print_top(df, k, title):
    if df.empty:
        print(title, "\n(none)\n"); return
    keep = [c for c in ["dataset","E","I","C","G","O","Composite","driver"] if c in df.columns]
    print(title)
    print(df.sort_values("Composite", ascending=False)[keep].head(k).to_string(index=False), "\n")

# load → merge policy → repair
real  = repair_scores(attach_policy_rate(load_df(REAL_IN)))
synth = repair_scores(attach_policy_rate(load_df(SYNTH_IN)))

# tag kind for downstream (don’t duplicate later)
if not real.empty:  real["kind"]  = "real"
if not synth.empty: synth["kind"] = "synth"

# save v2 (overwrite)
REAL_V2  = OUT / "pillar_scores_real_v2.csv"
SYNTH_V2 = OUT / "pillar_scores_synth_v2.csv"
SHEET_V2 = OUT / "pillar_scores_sheet_v2.csv"
real.to_csv(REAL_V2, index=False)
synth.to_csv(SYNTH_V2, index=False)
pd.concat([real, synth], ignore_index=True).to_csv(SHEET_V2, index=False)

# strict picks (robust)
real_pick  = strict_picks(real,  "real",  top_k=10, q=0.90)
synth_pick = strict_picks(synth, "synth", top_k=5,  q=0.90)
REAL_PICK = OUT / "strict_picks_real_v2.csv"
SYN_PICK  = OUT / "strict_picks_synth_v2.csv"
pd.concat([real_pick, synth_pick], ignore_index=True).to_csv(OUT/"strict_picks_all_v2.csv", index=False)
real_pick.to_csv(REAL_PICK, index=False)
synth_pick.to_csv(SYN_PICK, index=False)

# display
print_top(real,  10, "== REAL top 10 (repaired) ==")
print_top(synth,  5, "== SYNTH top 5 (repaired) ==")

print("Saved:")
for p in [REAL_V2, SYNTH_V2, SHEET_V2, REAL_PICK, SYN_PICK, OUT/"strict_picks_all_v2.csv"]:
    print(" -", p)


== REAL top 10 (repaired) ==
                                                                       dataset        E        I        C        G        O  Composite driver
          artifacts__tables__migrated__cnt-genomic-resonance-map__df629623.csv 0.004294 0.542254 1.000000 0.026214 0.606531   0.401437      C
artifacts__tables__genome3d__atlas__nodes_v1h_realhic__20251009-020445.parquet 0.416036 0.419484 0.104596 0.033268 0.875405   0.343132      E
        artifacts__tables__genome3d__atlas__nodes_v1h__20251008-215623.parquet 0.411498 0.413112 0.054040 0.033139 0.661432   0.308649      E
         artifacts__tables__genome3d__atlas__genes_v1__20251008-214043.parquet 0.340393 0.394727 0.000000 0.037155 0.995751   0.305948      E
                       artifacts__tables__migrated__gdf-snapshot__d8dc9743.csv 0.511111 0.318376 0.000000 0.035062 0.606531   0.298840      E
        artifacts__tables__genome3d__atlas__nodes_v0c__20251008-213724.parquet 0.083333 0.570617 0.000000 0.038817 0.90

In [14]:
# === CNT Five Pillars — Master Stitch & Priority Planner (v3) ===
# Builds a single workbook + refreshed CSVs from the repaired v2 outputs.
# Safe if some sources are missing; prints what it could assemble.

import numpy as np, pandas as pd
from pathlib import Path

ROOT = Path(r"C:\Users\caleb\CNT_Lab")
OUT  = ROOT / "artifacts" / "cnt_five_pillars"
OUT.mkdir(parents=True, exist_ok=True)

# Inputs from prior steps (your v2 saves)
REAL_V2   = OUT / "pillar_scores_real_v2.csv"
SYNTH_V2  = OUT / "pillar_scores_synth_v2.csv"
SHEET_V2  = OUT / "pillar_scores_sheet_v2.csv"
PICKS_ALL = OUT / "strict_picks_all_v2.csv"
TOP_SIGS  = OUT / "top_signals_filtered.csv"  # from scoreboard phase (if present)

# Outputs (this cell writes/overwrites)
MASTER_XLSX = OUT / "CNT_Master_Sheet_v3.xlsx"
MASTER_CSV  = OUT / "CNT_Master_Sheet_v3.csv"
PRIORITY_CSV= OUT / "priority_shortlist_v3.csv"
SUMMARY_TXT = OUT / "priority_summary_v3.txt"

# ---------------- helpers ----------------
def load_df(path):
    if not path.exists():
        print(f"[warn] missing: {path.name}")
        return pd.DataFrame()
    df = pd.read_csv(path, low_memory=False)
    df.columns = [c.strip() for c in df.columns]
    return df

def coerce_cols(df, cols):
    for c in cols:
        if c in df.columns:
            df[c] = pd.to_numeric(df[c], errors="coerce")
    return df

def ensure_kind(df, default_kind):
    if df.empty: return df
    if "kind" not in df.columns:
        df.insert(0, "kind", default_kind)
    else:
        df["kind"] = df["kind"].fillna(default_kind)
    return df

def pillar_badges(df):
    # simple, sharp thresholds for quick scanning; tune if desired
    cuts = dict(E=0.40, I=0.55, C=0.50, G=0.030, O=0.80)
    for k,thr in cuts.items():
        if k in df.columns:
            df[f"badge_{k}"] = np.where(pd.to_numeric(df[k], errors="coerce")>=thr, f"{k}★", "")
    if set(["badge_E","badge_I","badge_C","badge_G","badge_O"]).issubset(df.columns):
        df["badges"] = df[["badge_E","badge_I","badge_C","badge_G","badge_O"]].agg(lambda r: " ".join([x for x in r if x]), axis=1)
    return df

def soft_rank(s):
    s = pd.to_numeric(s, errors="coerce")
    # Higher Composite better, higher RFI_p95 better -> descending ranks
    return s.rank(method="average", ascending=False)

# ---------------- load & prepare ----------------
real   = ensure_kind(load_df(REAL_V2),  "real")
synth  = ensure_kind(load_df(SYNTH_V2), "synth")
sheet  = load_df(SHEET_V2)
picks  = load_df(PICKS_ALL)
tops   = load_df(TOP_SIGS)

# Coerce pillars
pillar_cols = ["E","I","C","G","O","Composite","policy_rate"]
for df in (real, synth, sheet, picks):
    coerce_cols(df, pillar_cols)

# Minimal unify
master = pd.concat([real, synth], ignore_index=True)
if master.empty and not sheet.empty:
    master = sheet.copy()

# Add badges and driver if missing
if not master.empty:
    if "driver" not in master.columns:
        # reconstruct simple driver by largest weighted contribution (same weights as earlier)
        W = dict(E=0.30, I=0.25, C=0.20, G=0.15, O=0.10)
        for k,w in W.items():
            if k in master.columns:
                master[f"contrib_{k}"] = w * pd.to_numeric(master[k], errors="coerce")
        ccols = [c for c in master.columns if c.startswith("contrib_")]
        if ccols:
            master["driver"] = master[ccols].idxmax(axis=1).str.replace("contrib_","", regex=False)
    pillar_badges(master)

# Merge top_signals (RFI, drift) for priority
if not master.empty and not tops.empty:
    # standardize join key
    tops.columns = [c.strip() for c in tops.columns]
    key = "dataset" if "dataset" in master.columns else None
    if key and key in tops.columns:
        # keep only the useful scoreboard metrics
        keep_tops = [c for c in tops.columns if c in
                     ["dataset","RFI_p95","RFI_mean","C_mean","dH_abs","drift_motion","drift_ratio_bounded","policy_rate"]]
        tops_slim = tops[keep_tops].copy()
        master = master.merge(tops_slim, on="dataset", how="left", suffixes=("","_tops"))
        # If policy_rate missing in master, use tops copy
        if "policy_rate" in master.columns and "policy_rate_tops" in master.columns:
            master["policy_rate"] = master["policy_rate"].combine_first(master["policy_rate_tops"])
            master.drop(columns=["policy_rate_tops"], inplace=True)

# Priority score: blend Composite & RFI_p95 (if available), slight boost for real data
if not master.empty:
    if "Composite" in master.columns:
        master["rank_comp"] = soft_rank(master["Composite"])
    if "RFI_p95" in master.columns:
        master["rank_rfi"]  = soft_rank(master["RFI_p95"])
    # Combine ranks (lower is better)
    if {"rank_comp","rank_rfi"}.issubset(master.columns):
        base = (master["rank_comp"] + master["rank_rfi"]) / 2.0
    else:
        base = master.get("rank_comp", pd.Series(np.nan, index=master.index))
    # penalty/bonus terms
    bonus_real  = np.where(master.get("kind","real").values=="real", -0.25, 0.0)  # nudge real up
    penalty_low = np.where(pd.to_numeric(master.get("C", np.nan), errors="coerce")<0.05,  +0.25, 0.0) # penalize if invariants dominate solely
    master["priority_score"] = base + bonus_real + penalty_low
    master["priority_rank"]  = master["priority_score"].rank(method="average", ascending=True)

# Save master CSV
if not master.empty:
    # Order columns nicely
    front = [c for c in ["dataset","kind","Composite","priority_rank","priority_score",
                         "E","I","C","G","O","driver","badges","policy_rate",
                         "RFI_p95","RFI_mean","C_mean","dH_abs","drift_motion","drift_ratio_bounded"] if c in master.columns]
    rest  = [c for c in master.columns if c not in front]
    master_sorted = master[front + rest].sort_values(["kind","priority_rank","Composite"], ascending=[True, True, False])
    master_sorted.to_csv(MASTER_CSV, index=False)

# Strict picks view (if present)
if not picks.empty:
    picks_sorted = picks.sort_values(["kind","Composite"], ascending=[True, False])
else:
    picks_sorted = pd.DataFrame()

# Priority shortlist (top 20 real + top 10 synth)
prio_real  = master[(master.get("kind")=="real")].sort_values("priority_rank").head(20).copy() if "priority_rank" in master.columns else pd.DataFrame()
prio_synth = master[(master.get("kind")=="synth")].sort_values("priority_rank").head(10).copy() if "priority_rank" in master.columns else pd.DataFrame()
prio_all   = pd.concat([prio_real, prio_synth], ignore_index=True)
if not prio_all.empty:
    prio_keep = [c for c in ["dataset","kind","priority_rank","Composite","badges","driver","E","I","C","G","O","RFI_p95","drift_ratio_bounded"] if c in prio_all.columns]
    prio_all[prio_keep].to_csv(PRIORITY_CSV, index=False)

# Write workbook (best-effort)
written_sheets = []
try:
    with pd.ExcelWriter(MASTER_XLSX, engine="openpyxl") as xw:
        if not master.empty:
            master_sorted.to_excel(xw, index=False, sheet_name="master")
            written_sheets.append("master")
        if not picks_sorted.empty:
            picks_sorted.to_excel(xw, index=False, sheet_name="strict_picks")
            written_sheets.append("strict_picks")
        ts = load_df(TOP_SIGS)
        if not ts.empty:
            ts.to_excel(xw, index=False, sheet_name="top_signals")
            written_sheets.append("top_signals")
        if Path(SHEET_V2).exists():
            load_df(SHEET_V2).to_excel(xw, index=False, sheet_name="pillar_sheet_v2")
            written_sheets.append("pillar_sheet_v2")
except Exception as e:
    print("[warn] Excel export skipped:", e)

# Console summary
def head_or_note(df, k, title):
    print(title)
    if df.empty:
        print("(none)\n")
    else:
        print(df.head(k).to_string(index=False), "\n")

print("== CNT Master Build v3 ==")
head_or_note(master.sort_values("priority_rank").loc[:, ["dataset","kind","priority_rank","Composite","badges","driver"]]
             if "priority_rank" in master.columns else master.loc[:, ["dataset","kind","Composite","badges","driver"]],
             12, "Top-priority (all kinds)")

head_or_note(prio_real.loc[:, ["dataset","priority_rank","Composite","badges","driver"]] if not prio_real.empty else pd.DataFrame(),
             12, "Top-priority REAL")

head_or_note(prio_synth.loc[:, ["dataset","priority_rank","Composite","badges","driver"]] if not prio_synth.empty else pd.DataFrame(),
             8, "Top-priority SYNTH")

# Save a tiny text digest
with open(SUMMARY_TXT, "w", encoding="utf-8") as f:
    f.write("CNT Master Build v3 — priority digest\n")
    if not prio_real.empty:
        f.write("\nREAL (top 12):\n")
        f.write(prio_real[["dataset","priority_rank","Composite","badges","driver"]].head(12).to_string(index=False))
    if not prio_synth.empty:
        f.write("\n\nSYNTH (top 8):\n")
        f.write(prio_synth[["dataset","priority_rank","Composite","badges","driver"]].head(8).to_string(index=False))
    f.write("\n")
print("Saved:")
for p in [MASTER_CSV, PRIORITY_CSV, MASTER_XLSX, SUMMARY_TXT]:
    print(" -", p)


== CNT Master Build v3 ==
Top-priority (all kinds)
                                                                       dataset  kind  priority_rank  Composite   badges driver
artifacts__tables__genome3d__atlas__nodes_v1h_realhic__20251009-020445.parquet  real            1.0   0.343132 E★ G★ O★      E
                       artifacts__tables__migrated__gdf-snapshot__d8dc9743.csv  real            2.5   0.298840    E★ G★      E
         artifacts__tables__genome3d__atlas__genes_v1__20251008-214043.parquet  real            2.5   0.305948    G★ O★      E
        artifacts__tables__genome3d__atlas__nodes_v1h__20251008-215623.parquet  real            4.0   0.308649    E★ G★      E
        artifacts__tables__genome3d__atlas__nodes_v0a__20251008-211922.parquet  real            6.0   0.244833    I★ G★      I
        artifacts__tables__genome3d__atlas__nodes_v0a__20251008-211232.parquet  real            6.0   0.244833    I★ G★      I
        artifacts__tables__genome3d__atlas__nodes_v0c__20251

In [15]:
# === CNT Five Pillars — Evidence Packets + Lawbook (v3) =====================
# Consumes Master v3 outputs; generates per-dataset pillar checks and a consolidated lawbook.

import numpy as np, pandas as pd, re, os
from pathlib import Path

# --- IO ---------------------------------------------------------------------
ROOT = Path(r"C:\Users\caleb\CNT_Lab")
OUT  = ROOT / "artifacts" / "cnt_five_pillars"
OUT.mkdir(parents=True, exist_ok=True)

MASTER_CSV   = OUT / "CNT_Master_Sheet_v3.csv"
PRIO_CSV     = OUT / "priority_shortlist_v3.csv"  # optional accelerator
TOPSIG_CSV   = OUT / "top_signals_filtered.csv"   # optional metadata
PACKETS_DIR  = OUT / "packets_v3"; PACKETS_DIR.mkdir(exist_ok=True)
LAWBOOK_CSV  = OUT / "lawbook_v3.csv"
README_TXT   = OUT / "lawbook_v3_README.txt"

# --- utility ----------------------------------------------------------------
def load_df(p):
    if not Path(p).exists(): 
        print(f"[warn] missing: {p}")
        return pd.DataFrame()
    df = pd.read_csv(p, low_memory=False)
    df.columns = [c.strip() for c in df.columns]
    return df

def num(x):
    return pd.to_numeric(x, errors="coerce")

def ema(x, alpha=0.01):
    x = np.asarray(num(x), float)
    y = np.empty_like(x); y[:] = np.nan
    m = np.isfinite(x)
    if not m.any(): return y
    last = x[m][0]
    for i,xi in enumerate(x):
        if np.isfinite(xi): last = alpha*xi + (1-alpha)*last
        y[i]=last
    return y

def motion(v):
    v = np.asarray(num(v), float)
    if v.size < 2: return np.nan
    g = np.gradient(v)
    g = g[np.isfinite(g)]
    return float(np.mean(np.abs(g))) if g.size else np.nan

def find_feature_file(dataset, fallback_dir=OUT):
    """
    Prefer explicit 'features__*.csv' saved earlier. If master includes 'file', use it.
    Otherwise try to reconstruct from sanitized dataset stem by scanning OUT.
    """
    # Quick exact candidates
    stem = re.sub(r"[\\/]+", "__", str(dataset))
    exact = list(fallback_dir.glob(f"features__{stem}.csv"))
    if exact: return exact[0]
    # Fuzzy search
    picks = list(fallback_dir.glob(f"features__*{Path(dataset).name}*.csv"))
    if picks: return picks[0]
    # As a last resort, allow using dataset itself if it is a CSV of features
    p = Path(dataset)
    if p.exists() and p.suffix.lower()==".csv":
        return p
    return None

def curvature_proxy(C, H, dH, RFI):
    # build small feature matrix; guard tiny N
    C = np.nan_to_num(num(C), 0.0)
    H = np.nan_to_num(num(H), 0.0)
    dH= np.nan_to_num(num(dH),0.0)
    R = np.nan_to_num(num(RFI),0.0)
    X = np.vstack([C,H,dH,R]).T
    if X.shape[0] < 64: return np.nan, np.nan
    Cov = np.cov(X.T)
    sign, logdet = np.linalg.slogdet(Cov)
    # Map to [0,1] where larger ~ less negative curvature (safer)
    G = 1.0 / (1.0 + max(0.0, -logdet))
    return logdet, G

def rfi_series(C, dH, alpha=1.25):
    C = num(C).values if isinstance(C, pd.Series) else num(C)
    dH= num(dH).values if isinstance(dH,pd.Series) else num(dH)
    return C * np.exp(-alpha*np.maximum(0, np.nan_to_num(dH, 0.0)))

def gate_bool(val, thr, mode=">="):
    if not np.isfinite(val): return False
    return (val >= thr) if mode==">=" else (val <= thr)

# --- thresholds / weights (explicit) ----------------------------------------
W = dict(E=0.30, I=0.25, C=0.20, G=0.15, O=0.10)
THR = dict(
    E_rfi_p95 = 0.85,      # strong resonance
    I_score   = 0.55,      # low free-energy (sigmoid score)
    C_score   = 0.50,      # invariants steadier than metrics
    G_score   = 0.03,      # weakly positive curvature proxy
    O_star    = 0.80,      # policy sweet spot proximity
)
ALPHA = 1.25  # RFI penalty weight

# --- load master, shortlist, tops ------------------------------------------
master = load_df(MASTER_CSV)
prio   = load_df(PRIO_CSV)
tops   = load_df(TOPSIG_CSV)

if prio.empty and not master.empty and "priority_rank" in master.columns:
    # build a default shortlist (top 20 real, top 10 synth)
    prio_real  = master[master.get("kind")=="real"].sort_values("priority_rank").head(20)
    prio_synth = master[master.get("kind")=="synth"].sort_values("priority_rank").head(10)
    prio = pd.concat([prio_real, prio_synth], ignore_index=True)

if master.empty:
    raise SystemExit("No master sheet found; run CNT Master Build v3 first.")

# --- iterate priority items -------------------------------------------------
rows = []
for i, r in prio.iterrows():
    ds   = r.get("dataset")
    kind = r.get("kind","real")
    fpth = r.get("file", np.nan)
    fp   = Path(fpth) if (isinstance(fpth,str) and Path(fpth).exists()) else find_feature_file(ds)

    if fp is None:
        print(f"[skip] no features found for {ds}")
        continue

    try:
        df = pd.read_csv(fp, low_memory=False)
    except Exception as e:
        print(f"[skip] unreadable features for {ds}: {e}")
        continue

    # Normalize expected columns
    # Feature sets produced earlier usually include these; fallback if missing.
    C  = df["C"]  if "C"  in df.columns else pd.Series(np.nan, index=df.index)
    H  = df["H"]  if "H"  in df.columns else pd.Series(np.nan, index=df.index)
    dH = df["dH"] if "dH" in df.columns else pd.Series(np.gradient(num(H))) if H.notna().any() else pd.Series(np.nan, index=df.index)

    # Invariants (beta0/beta1) or very-slow EMA proxies
    I0 = df["I_beta0"] if "I_beta0" in df.columns else pd.Series(ema(C), index=df.index)
    I1 = df["I_beta1"] if "I_beta1" in df.columns else pd.Series(ema(H), index=df.index)

    # RFI: prefer existing column; else recompute
    RFI = df["RFI"] if "RFI" in df.columns else pd.Series(rfi_series(C, dH, alpha=ALPHA), index=df.index)

    # --- E: resonance with non-increasing entropy
    rfi95 = float(np.nanquantile(num(RFI), 0.95)) if np.isfinite(num(RFI)).any() else np.nan
    e_pass= gate_bool(rfi95, THR["E_rfi_p95"], ">=")

    # --- I: free-energy score (sigmoid of normalized free-energy)
    Cmed = float(np.nanmedian(num(C))) if np.isfinite(num(C)).any() else np.nan
    lam  = (float(np.nanmedian(num(H))) / max(Cmed,1e-9)) if np.isfinite(Cmed) else 1.0
    F    = num(H) - lam*num(C)
    Fz   = (F - np.nanmedian(F)) / (np.nanstd(F)+1e-9) if np.isfinite(F).any() else np.nan
    I_sc = float(1.0 / (1.0 + np.exp(np.nanmean(Fz)))) if np.isfinite(np.nanmean(Fz)) else np.nan
    i_pass= gate_bool(I_sc, THR["I_score"], ">=")

    # --- C: invariants drift slower than metrics
    inv_m  = np.nansum([motion(I0), motion(I1)])
    metr_m = np.nansum([motion(C),  motion(H)])
    C_sc   = float(1 - np.clip(inv_m / (metr_m + 1e-9), 0, 1)) if np.isfinite(inv_m) and np.isfinite(metr_m) and metr_m>0 else np.nan
    c_pass = gate_bool(C_sc, THR["C_score"], ">=")

    # --- G: curvature proxy via logdet(Cov) -> map to [0,1]
    logdet, G_sc = curvature_proxy(C, H, dH, RFI)
    g_pass = gate_bool(G_sc, THR["G_score"], ">=")

    # --- O: operational budget sweet spot around 5% (re-use from master if present)
    prate = None
    if "policy_rate" in r.index and np.isfinite(r["policy_rate"]):
        prate = float(r["policy_rate"])
    elif "policy_rate" in df.columns:
        prate = float(num(df["policy_rate"]).mean())
    O_sc = float(np.exp(-((prate - 0.05)**2)/(2*0.05**2))) if prate is not None and np.isfinite(prate) else np.nan
    o_pass = gate_bool(O_sc, THR["O_star"], ">=")

    # Composite (recompute with explicit weights, ignoring NaNs)
    comp_num = comp_den = 0.0
    for k, v in dict(E=e_pass and (rfi95/1.0) or (rfi95 if np.isfinite(rfi95) else np.nan),
                     I=I_sc, C=C_sc, G=G_sc, O=O_sc).items():
        if np.isfinite(v):
            comp_num += W[k]*v; comp_den += W[k]
    comp = comp_num/comp_den if comp_den>0 else np.nan

    # badges & driver
    badges = " ".join([s for s,b in zip(["E★","I★","C★","G★","O★"], [e_pass,i_pass,c_pass,g_pass,o_pass]) if b])
    contribs = dict(E=(rfi95 if np.isfinite(rfi95) else -np.inf)*W["E"],
                    I=(I_sc  if np.isfinite(I_sc)  else -np.inf)*W["I"],
                    C=(C_sc  if np.isfinite(C_sc)  else -np.inf)*W["C"],
                    G=(G_sc  if np.isfinite(G_sc)  else -np.inf)*W["G"],
                    O=(O_sc  if np.isfinite(O_sc)  else -np.inf)*W["O"])
    driver = max(contribs, key=contribs.get)

    # packet save
    slug = re.sub(r"[^A-Za-z0-9_.-]+", "_", str(ds))[:180]
    pkt  = pd.DataFrame([dict(
        dataset=ds, kind=kind, file=str(fp),
        rfi_p95=rfi95, I_score=I_sc, C_score=C_sc, G_score=G_sc, O_score=O_sc,
        pass_E=e_pass, pass_I=i_pass, pass_C=c_pass, pass_G=g_pass, pass_O=o_pass,
        Composite=comp, badges=badges, driver=driver,
        inv_motion=inv_m, metric_motion=metr_m, logdet=logdet, policy_rate=prate
    )])
    pkt_path = PACKETS_DIR / f"packet__{slug}.csv"
    pkt.to_csv(pkt_path, index=False)

    rows.append(pkt.iloc[0].to_dict())

# --- consolidate lawbook ----------------------------------------------------
lawbook = pd.DataFrame(rows)
if not lawbook.empty:
    # priority merge for ranks if available
    prio_slim = prio[["dataset","kind","priority_rank"]] if set(["dataset","kind","priority_rank"]).issubset(prio.columns) else pd.DataFrame()
    if not prio_slim.empty:
        lawbook = lawbook.merge(prio_slim, on=["dataset","kind"], how="left")
    # order
    order = ["dataset","kind","priority_rank","Composite","badges","driver",
             "rfi_p95","I_score","C_score","G_score","O_score",
             "inv_motion","metric_motion","logdet","policy_rate","file"]
    order = [c for c in order if c in lawbook.columns]
    lawbook = lawbook[order].sort_values(["kind","priority_rank","Composite"], ascending=[True, True, False])
    lawbook.to_csv(LAWBOOK_CSV, index=False)

# --- README summary ---------------------------------------------------------
with open(README_TXT, "w", encoding="utf-8") as f:
    f.write("CNT Lawbook v3 — Evidence Packets & Next Actions\n")
    f.write("Folders:\n")
    f.write(f" - packets: {PACKETS_DIR}\n")
    f.write(f" - lawbook: {LAWBOOK_CSV}\n\n")

    if not lawbook.empty:
        f.write("Top 12 by priority:\n")
        cols = [c for c in ["dataset","kind","priority_rank","Composite","badges","driver"] if c in lawbook.columns]
        f.write(lawbook[cols].head(12).to_string(index=False))
        f.write("\n\nAction by driver:\n")
        f.write("* E-driver: fit alpha for RFI→lead-time; plot RFI vs dH; validate Precision@Θ.\n")
        f.write("* I-driver: verify free-energy gap glyph vs random; confirm C_score>0.5 in windows.\n")
        f.write("* C-driver: audit invariant/metric drift ratio; localize invariants (I_beta*) hotspots.\n")
        f.write("* G-driver: recompute curvature windows (N≥64); check logdet trends; relate to lead-time.\n")
        f.write("* O-driver: budget sweep around 5% policy; sensitivity of AUC/lead-time vs policy_rate.\n")

print("Saved:")
print(" -", LAWBOOK_CSV)
print(" -", PACKETS_DIR)
print(" -", README_TXT)


Saved:
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\lawbook_v3.csv
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\lawbook_v3_README.txt


In [16]:
# CNT Lawbook v3 → Evidence Packets (v3)
# - Builds packets for top-priority rows in lawbook_v3.csv
# - Pulls/merges micro-scores where available
# - Emits per-dataset packet folder with packet.md + next_actions.md
# - Writes packets_index.md and refreshed priority_shortlist
# - Safe against existing "kind" column, missing O-scores, etc.

import os, re, json, math, textwrap, shutil
from pathlib import Path
import pandas as pd
import numpy as np

# ----------------------------- Paths & Config --------------------------------
ROOT        = Path(r"C:\Users\caleb\CNT_Lab")
LAWBOOK     = ROOT / r"artifacts\cnt_five_pillars\lawbook_v3.csv"
OUT_DIR     = ROOT / r"artifacts\cnt_five_pillars"
PACKETS_DIR = OUT_DIR / "packets_v3"

# Optional score tables (if present they’ll be merged)
PILLAR_REAL  = OUT_DIR / "pillar_scores_real_v2.csv"
PILLAR_SYNTH = OUT_DIR / "pillar_scores_synth_v2.csv"

# Files produced
INDEX_MD    = PACKETS_DIR / "packets_index.md"
SHORTLIST   = OUT_DIR / "priority_shortlist_v3.csv"

# Driver action recipes (from Lawbook v3 note)
DRIVER_ACTIONS = {
    "E": [
        "Fit α for RFI→lead-time (maximize concordance).",
        "Plot RFI vs dH; verify RFI high when dH≤0.",
        "Validate Precision@Θ against baseline windows."
    ],
    "I": [
        "Verify glyphic free-energy gap: glyph vs random.",
        "Confirm C_score > 0.5 in ≥ q* windows by bootstrap.",
        "Replicate across ≥2 domains (EEG + one synthetic)."
    ],
    "C": [
        "Audit invariant/metric drift ratio (I/metrics).",
        "Localize invariant hotspots (I_beta* windows).",
        "Stress-test under transformation T (semantics preserved)."
    ],
    "G": [
        "Recompute curvature windows (N≥64); logdet trends.",
        "Model Θ_lead ~ R^- + RFI; expect β1 < 0 (less neg. curvature → longer lead).",
        "Relate curvature shifts to glyph constraints."
    ],
    "O": [
        "Budget sweep around 5% policy; tune risk threshold.",
        "Report AUC/lead-time vs policy_rate sensitivity.",
        "Closed-loop ablation vs open-loop with matched budget."
    ],
}

# ----------------------------- Utilities -------------------------------------
def ensure_dir(p: Path):
    p.mkdir(parents=True, exist_ok=True)
    return p

def slugify(s: str, maxlen=120):
    s = re.sub(r"[^\w\-]+", "_", s.strip())
    s = re.sub(r"__+", "_", s).strip("_")
    return s[:maxlen]

def exists_or_none(p: Path):
    try:
        return p if p.exists() else None
    except Exception:
        return None

def try_read_csv(p: Path) -> pd.DataFrame:
    if p and p.exists():
        try:
            return pd.read_csv(p)
        except Exception:
            pass
    return pd.DataFrame()

def safe_col(d: pd.DataFrame, name: str, default=np.nan):
    if name not in d.columns:
        d[name] = default
    return d

def coalesce(*vals, default=None):
    for v in vals:
        if v is not None and isinstance(v, float) and np.isfinite(v):
            return v
        if v not in (None, "", np.nan) and not (isinstance(v, float) and np.isnan(v)):
            return v
    return default

def fmtf(x):
    return "—" if not (isinstance(x, (int,float)) and np.isfinite(x)) else f"{x:.6f}"

def infer_source_path(dataset: str) -> Path | None:
    """
    Heuristic: the 'dataset' in lawbook is like
      artifacts__tables__genome3d__atlas__nodes_v1h_realhic__20251009-020445.parquet
    Try to map into CNT_Lab tree by splitting on '__' and joining.
    Also try features CSVs written earlier (features__*.csv.csv).
    """
    # 1) raw path heuristic
    parts = [p for p in dataset.split("__") if p]
    # Try under CNT_Lab (favor artifacts/notebooks roots)
    candidates = []
    if parts:
        # Artifacts/raw file
        p1 = ROOT.joinpath(*parts)  # e.g., C:\...\artifacts\tables\...
        candidates.append(p1)
        # Features CSV produced by earlier run
        feat_name = f"features__{dataset}.csv.csv".replace("..", ".")
        p2 = OUT_DIR / feat_name
        candidates.append(p2)
        # Also try features under cnt_five_pillars subfolders if present
        p3 = OUT_DIR / "features" / feat_name
        candidates.append(p3)

    for c in candidates:
        if exists_or_none(c):
            return c
    return None

# ----------------------------- Load Lawbook ----------------------------------
if not LAWBOOK.exists():
    raise FileNotFoundError(f"Lawbook not found: {LAWBOOK}")

law = pd.read_csv(LAWBOOK)
# Normalize essential columns
for col in ["dataset","kind","priority_rank","Composite","badges","driver"]:
    if col not in law.columns:
        # best-effort fallback
        if col == "kind":
            law[col] = np.where(law["dataset"].str.contains("sim|synth", case=False, na=False),"synth","real")
        elif col == "priority_rank":
            law[col] = np.arange(1, len(law)+1, dtype=float)
        else:
            law[col] = np.nan

# ----------------------------- Merge micro-scores (optional) -----------------
pill = pd.concat([try_read_csv(PILLAR_REAL), try_read_csv(PILLAR_SYNTH)], ignore_index=True)
if not pill.empty:
    # Keep only needed columns and deduplicate on dataset
    keep = ["dataset","E","I","C","G","O","Composite"]
    pill = pill[[c for c in keep if c in pill.columns]].drop_duplicates("dataset", keep="first")
    law = law.merge(pill, on="dataset", how="left", suffixes=("","_pill"))

# ----------------------------- Build Packets ---------------------------------
ensure_dir(PACKETS_DIR)

rows_index = []
for i, r in law.sort_values(["priority_rank","Composite"], ascending=[True,False]).iterrows():
    ds    = str(r["dataset"])
    kind  = str(r.get("kind",""))
    drv   = str(r.get("driver","")).strip()[:1].upper() if isinstance(r.get("driver",""), str) else ""
    score = float(r.get("Composite", np.nan))
    badges= str(r.get("badges",""))
    prio  = r.get("priority_rank", np.nan)

    # Find a source/feature file for reference
    src_path = None
    for cand_col in ["source","file","filepath"]:
        if cand_col in law.columns and pd.notna(r.get(cand_col, np.nan)):
            maybe = Path(str(r[cand_col]))
            if maybe.exists():
                src_path = maybe; break
    if src_path is None:
        src_path = infer_source_path(ds)

    # Packet folder name: rank_slug
    rank_str = ("p" + (f"{prio:.1f}".replace(".","_") if isinstance(prio,(int,float)) and np.isfinite(prio) else "X"))
    slug     = slugify(ds)
    pfolder  = ensure_dir(PACKETS_DIR / f"{rank_str}__{slug}")

    # Compose packet.md
    E = r.get("E", np.nan); I = r.get("I", np.nan); C = r.get("C", np.nan)
    G = r.get("G", np.nan); O = r.get("O", np.nan)

    # Driver actions
    actions = DRIVER_ACTIONS.get(drv, [])
    actions_md = "\n".join(f"- [ ] {a}" for a in actions) if actions else "- [ ] Define driver tasks."

    md = f"""# Evidence Packet — {ds}

**Kind:** {kind}  **Priority:** {fmtf(prio)}  **Composite:** {fmtf(score)}  **Badges:** {badges or "—"}  
**Driver:** {drv or "—"}  **Source:** {src_path if src_path else "n/a"}

## Pillar Micro-Scores
| E | I | C | G | O |
|---:|---:|---:|---:|---:|
| {fmtf(E)} | {fmtf(I)} | {fmtf(C)} | {fmtf(G)} | {fmtf(O)} |

## Next Actions (by driver {drv or "?"})
{actions_md}

## Notes
- Verify windowing & estimators match lab standard (WIN/STEP/ALPHA).
- Attach plots (RFI vs dH, curvature, invariants drift) when generated.
"""
    (pfolder / "packet.md").write_text(md, encoding="utf-8")

    # Write next_actions.md (standalone checklist)
    (pfolder / "next_actions.md").write_text(
        f"# Next Actions — {ds}\n\n{actions_md}\n", encoding="utf-8"
    )

    # Row for index
    rows_index.append(dict(
        dataset=ds, kind=kind, driver=drv, priority_rank=prio, Composite=score,
        badges=badges, packet=str(pfolder), source=str(src_path) if src_path else ""
    ))

# ----------------------------- Write Index & Shortlist -----------------------
idx = pd.DataFrame(rows_index).sort_values(["priority_rank","Composite"], ascending=[True,False])
idx.to_csv(SHORTLIST, index=False)

index_md = ["# CNT Evidence Packets (v3)",
            f"_root: {PACKETS_DIR}_",
            "",
            "| Rank | Dataset | Kind | Driver | Composite | Badges | Packet |",
            "|:----:|---|:---:|:---:|---:|:---:|---|"]
for _, r in idx.iterrows():
    index_md.append(f"| {fmtf(r['priority_rank'])} | `{r['dataset']}` | {r['kind']} | {r['driver']} | {fmtf(r['Composite'])} | {r['badges'] or '—'} | `{r['packet']}` |")
INDEX_MD.write_text("\n".join(index_md) + "\n", encoding="utf-8")

print("Built evidence packets:")
print(idx.head(12).to_string(index=False))
print("\nWrote:")
print(" -", INDEX_MD)
print(" -", SHORTLIST)
print(" -", PACKETS_DIR)


Built evidence packets:
                                                                       dataset  kind driver  priority_rank  Composite   badges                                                                                                                                       packet                                                                                                                                         source
artifacts__tables__genome3d__atlas__nodes_v1h_realhic__20251009-020445.parquet  real      E            1.0   0.451088    E★ G★ C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\p1_0__artifacts_tables_genome3d_atlas_nodes_v1h_realhic_20251009-020445_parquet C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\features__artifacts__tables__genome3d__atlas__nodes_v1h_realhic__20251009-020445.parquet.csv
         artifacts__tables__genome3d__atlas__genes_v1__20251008-214043.parquet  real      E            2.5   0.429022    E★ G★          C:\Users\caleb\CNT

In [17]:
# CNT packet plotter v3 — adds plots & blurbs into each evidence packet
# - Reads priority_shortlist_v3.csv
# - For each row, opens the source features CSV
# - Computes/recovers t, H, dH, C, RFI; fits alpha if desired
# - Saves PNGs inside each packet folder
# - Appends an "Auto Plots" section + quick evidence bullets to packet.md

import os, io, re, math, textwrap, json, warnings
from pathlib import Path

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

warnings.filterwarnings("ignore", category=UserWarning)

# ----------------------------- paths & params -----------------------------
ROOT         = Path(r"C:\Users\caleb\CNT_Lab")
OUT_DIR      = ROOT / r"artifacts\cnt_five_pillars"
SHORTLIST    = OUT_DIR / "priority_shortlist_v3.csv"
PACKETS_ROOT = OUT_DIR / "packets_v3"

# RFI alpha grid (for quick fit if RFI needs computing)
ALPHA_GRID = np.linspace(0.25, 2.0, 15)

# What columns we try to use
CAND_T  = ["t", "t0", "time", "idx"]
CAND_H  = ["H","entropy","H_total"]
CAND_dH = ["dH","dH_dt","H_dot","dH_abs"]   # we prefer signed if available
CAND_C  = ["C","coh","coherence","NMI","PLV"]
CAND_R  = ["RFI","RFI_alpha","RFI_calc"]

# ----------------------------- utils -----------------------------
def pick_col(df, names):
    for n in names:
        if n in df.columns: return n
    return None

def ensure_time(df):
    ct = pick_col(df, CAND_T)
    if ct is None:
        df["t"] = np.arange(len(df))
        return "t"
    return ct

def safe_series(df, name, default=np.nan):
    return df[name].to_numpy() if name in df.columns else np.full(len(df), default, dtype=float)

def finite_diff(v):
    v = np.asarray(v, float)
    if len(v) < 2: return np.zeros_like(v)
    out = np.zeros_like(v)
    out[1:] = np.diff(v)
    return out

def rfi_from(C, dH, alpha=1.0):
    C = np.asarray(C, float)
    dH = np.asarray(dH, float)
    return C * np.exp(-alpha * np.maximum(0.0, dH))

def fit_alpha(C, dH, t=None):
    # choose alpha maximizing negative Spearman corr with future-risk proxy (here penalize positive dH)
    # fallback: maximize corr(RFI, -dH)
    C = np.asarray(C, float); dH = np.asarray(dH, float)
    mask = np.isfinite(C) & np.isfinite(dH)
    if not mask.any(): return 1.0
    best = (1.0, -np.inf)
    for a in ALPHA_GRID:
        rfi = rfi_from(C, dH, alpha=a)
        m = np.isfinite(rfi) & mask
        if m.sum() < 5: 
            continue
        # use Pearson on z-scored for speed/robustness
        x = (rfi[m] - np.nanmean(rfi[m])) / (np.nanstd(rfi[m]) + 1e-9)
        y = (-dH[m] - np.nanmean(-dH[m])) / (np.nanstd(-dH[m]) + 1e-9)
        corr = float(np.nanmean(x*y))  # ~ Pearson
        if corr > best[1]:
            best = (a, corr)
    return best[0]

def motion(v):
    v = np.asarray(v, float)
    if v.size < 2: return np.nan
    g = np.gradient(v)
    g = g[np.isfinite(g)]
    return float(np.mean(np.abs(g))) if g.size else np.nan

def add_or_append(path: Path, header: str, body: str):
    """Append a section to packet.md; replace if header already present."""
    text = path.read_text(encoding="utf-8") if path.exists() else ""
    block = f"\n\n## {header}\n{body}\n"
    pat = re.compile(rf"\n## {re.escape(header)}\n.*?(?=\n## |\Z)", re.S)
    if pat.search(text):
        text = pat.sub(block, text)
    else:
        text = text.rstrip() + block
    path.write_text(text, encoding="utf-8")

def png(path: Path):
    path.parent.mkdir(parents=True, exist_ok=True)
    plt.tight_layout()
    plt.savefig(path, dpi=120, bbox_inches="tight")
    plt.close()

def fmt(x, nd=6):
    return "—" if not (isinstance(x, (float,int)) and np.isfinite(x)) else f"{x:.{nd}f}"

# ----------------------------- main loop -----------------------------
if not SHORTLIST.exists():
    raise FileNotFoundError(f"Missing shortlist: {SHORTLIST}")

sl = pd.read_csv(SHORTLIST)
req_cols = ["dataset","packet","source","priority_rank","Composite","driver","kind","badges"]
for c in req_cols:
    if c not in sl.columns: sl[c] = np.nan

report_rows = []

for _, r in sl.iterrows():
    ds   = str(r["dataset"])
    src  = r.get("source", "")
    pkt  = r.get("packet", "")

    pkt_dir = Path(pkt) if pkt else None
    src_path = Path(src) if src else None

    if not pkt_dir or not pkt_dir.exists():
        print("[skip] no packet dir for", ds); continue
    if not src_path or not src_path.exists():
        print("[skip] no source for", ds); continue

    df = pd.read_csv(src_path, low_memory=False)
    if df.empty or len(df) < 3:
        print("[skip] tiny/empty", ds); continue

    # time & signals
    t_col = ensure_time(df)
    H_col = pick_col(df, CAND_H)
    C_col = pick_col(df, CAND_C)
    dH_col= pick_col(df, CAND_dH)
    R_col = pick_col(df, CAND_R)

    t  = df[t_col].to_numpy()
    H  = safe_series(df, H_col) if H_col else np.full(len(df), np.nan)
    Cc = safe_series(df, C_col) if C_col else np.full(len(df), np.nan)
    dH = safe_series(df, dH_col) if dH_col else finite_diff(H)

    # recover/compute RFI
    if R_col:
        RFI = df[R_col].to_numpy()
        alpha_used = np.nan
    else:
        alpha_used = fit_alpha(Cc, dH, t)
        RFI = rfi_from(Cc, dH, alpha_used)

    # quick stats
    mC    = np.nanmean(Cc)
    mdH   = np.nanmean(np.abs(dH))
    rfi95 = np.nanpercentile(RFI[np.isfinite(RFI)], 95) if np.isfinite(RFI).any() else np.nan
    inv_motion = motion(df["I_beta0"]) + motion(df["I_beta1"]) if all(c in df.columns for c in ["I_beta0","I_beta1"]) else np.nan
    metr_motion= motion(Cc) + motion(H)
    drift_ratio = (inv_motion / (metr_motion + 1e-9)) if (np.isfinite(inv_motion) and np.isfinite(metr_motion) and metr_motion>0) else np.nan

    # ---------------- plots ----------------
    # 1) time series RFI / C / H / dH (normalized bands)
    fig = plt.figure(figsize=(10,4))
    ax = plt.gca()
    ax.plot(t, RFI, label="RFI")
    if np.isfinite(Cc).any():  ax.plot(t, Cc,  label="C")
    if np.isfinite(H).any():   ax.plot(t, (H - np.nanmin(H)) / (np.nanmax(H)-np.nanmin(H)+1e-9), label="H (norm)")
    if np.isfinite(dH).any():  ax.plot(t, (dH - np.nanmin(dH)) / (np.nanmax(dH)-np.nanmin(dH)+1e-9), label="dH (norm)")
    ax.set_title(f"{ds} — Timeseries")
    ax.set_xlabel("t"); ax.set_ylabel("value / norm")
    ax.legend(loc="best", ncols=4)
    png(pkt_dir / "plot_timeseries.png")

    # 2) scatter RFI vs dH (expect negative trend vs positive dH)
    fig = plt.figure(figsize=(5,4))
    ax = plt.gca()
    m = np.isfinite(RFI) & np.isfinite(dH)
    ax.scatter(dH[m], RFI[m], s=8)
    ax.set_xlabel("dH"); ax.set_ylabel("RFI")
    ax.set_title("RFI vs dH")
    png(pkt_dir / "plot_rfi_vs_dh.png")

    # 3) coherence vs entropy (phase-ish plane)
    fig = plt.figure(figsize=(5,4))
    ax = plt.gca()
    m2 = np.isfinite(Cc) & np.isfinite(H)
    ax.scatter(Cc[m2], H[m2], s=8)
    ax.set_xlabel("C"); ax.set_ylabel("H")
    ax.set_title("C vs H")
    png(pkt_dir / "plot_c_vs_h.png")

    # 4) curvature proxy across windows if Cov available; else rolling logdet
    G_proxy = np.full(len(df), np.nan)
    if all(col in df.columns for col in ["curv_logdet","curv"]):
        G_proxy = df["curv_logdet"].to_numpy()
    else:
        # rolling 4-var covariance logdet (H,C,dH,RFI) with small window
        K = 32 if len(df) >= 64 else max(8, len(df)//4)
        X = np.vstack([
            np.nan_to_num(H,0),
            np.nan_to_num(Cc,0),
            np.nan_to_num(dH,0),
            np.nan_to_num(RFI,0)
        ]).T
        for i in range(len(df)):
            a = max(0, i-K); b = min(len(df), i+1)
            chunk = X[a:b]
            if len(chunk) >= 8:
                Cov = np.cov(chunk.T)
                sign, logdet = np.linalg.slogdet(Cov)
                G_proxy[i] = logdet if np.isfinite(logdet) else np.nan

    fig = plt.figure(figsize=(10,3.8))
    ax = plt.gca()
    ax.plot(t, G_proxy, lw=1)
    ax.set_xlabel("t"); ax.set_ylabel("logdet(Cov)")
    ax.set_title("Curvature proxy (rolling logdet)")
    png(pkt_dir / "plot_curvature_proxy.png")

    # ---------------- write into packet ----------------
    packet_md = pkt_dir / "packet.md"
    bullets = [
        f"RFI p95 = **{fmt(rfi95,3)}**; mean|dH| = **{fmt(mdH,3)}**; mean C = **{fmt(mC,3)}**.",
        f"drift ratio (invariants/metrics) = **{fmt(drift_ratio,3)}**.",
        (f"fitted α = **{fmt(alpha_used,3)}** (used for RFI)." if isinstance(alpha_used,(int,float)) and np.isfinite(alpha_used) else "")
    ]
    plots_md = textwrap.dedent(f"""
    - {bullets[0]}
    - {bullets[1]}
    - {bullets[2]}

    **Figures**
    ![](plot_timeseries.png)
    ![](plot_rfi_vs_dh.png)
    ![](plot_c_vs_h.png)
    ![](plot_curvature_proxy.png)
    """).strip("\n")

    add_or_append(packet_md, "Auto Plots & Evidence (v3)", plots_md)

    report_rows.append(dict(
        dataset=ds, rfi_p95=rfi95, C_mean=mC, dH_mean_abs=mdH,
        drift_ratio=drift_ratio, alpha_used=alpha_used,
        packet=str(pkt_dir)
    ))

# ---------------- summary table ----------------
rep = pd.DataFrame(report_rows).sort_values("rfi_p95", ascending=False)
rep_path = PACKETS_ROOT / "packet_plots_summary.csv"
rep.to_csv(rep_path, index=False)
print("Added plots & blurbs to", len(rep), "packets.")
print("Summary saved ->", rep_path)
print(rep.head(12).to_string(index=False))


Added plots & blurbs to 22 packets.
Summary saved -> C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\packet_plots_summary.csv
                                                                       dataset  rfi_p95   C_mean  dH_mean_abs  drift_ratio  alpha_used                                                                                                                                       packet
                       artifacts__tables__migrated__gdf-snapshot__d8dc9743.csv 1.000000 0.846963     0.008161     9.179209         NaN                       C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\p2_5__artifacts_tables_migrated_gdf-snapshot_d8dc9743_csv
         artifacts__tables__genome3d__atlas__genes_v1__20251008-214043.parquet 0.939549 0.792935     0.011407     1.244647         NaN          C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\p2_5__artifacts_tables_genome3d_atlas_genes_v1_20251008-214043_parquet
artifacts__tables__genome3d__atla

In [18]:
# CNT packet one-pagers + gallery (v3)
# - Builds a one-page PDF in each packet dir from the four PNGs + evidence bullets
# - Creates a combined gallery PDF and an index CSV
# - Appends a small "Auto One-Pager (v3)" section to each packet.md with a link

import re, textwrap
from pathlib import Path
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from matplotlib.backends.backend_pdf import PdfPages

ROOT         = Path(r"C:\Users\caleb\CNT_Lab")
OUT_DIR      = ROOT / r"artifacts\cnt_five_pillars"
PACKETS_ROOT = OUT_DIR / "packets_v3"
SHORTLIST    = OUT_DIR / "priority_shortlist_v3.csv"
SUMMARY      = PACKETS_ROOT / "packet_plots_summary.csv"

# ---------- helpers ----------
def read_text(p: Path) -> str:
    try:
        return p.read_text(encoding="utf-8", errors="ignore")
    except Exception:
        return ""

def first_md_h1(md: str) -> str:
    m = re.search(r"^#\s+(.+)$", md, re.M)
    return m.group(1).strip() if m else ""

def imread(path: Path):
    try:
        return plt.imread(path)
    except Exception:
        return None

def fmtf(x, p=6):
    try:
        if x is None or (isinstance(x, float) and (np.isnan(x) or np.isinf(x))):
            return "—"
        return f"{float(x):.{p}f}"
    except Exception:
        return "—"

def add_or_replace_section(md_path: Path, header: str, body_md: str):
    block = f"\n\n## {header}\n{body_md}\n"
    txt = read_text(md_path)
    pat = re.compile(rf"\n## {re.escape(header)}\n.*?(?=\n## |\Z)", re.S)
    new = pat.sub(block, txt) if pat.search(txt) else (txt.rstrip() + block)
    md_path.write_text(new, encoding="utf-8", errors="ignore")

# ---------- load inputs ----------
if not SUMMARY.exists():
    raise FileNotFoundError(f"Missing summary: {SUMMARY}")
sumdf = pd.read_csv(SUMMARY)

sl = pd.read_csv(SHORTLIST) if SHORTLIST.exists() else pd.DataFrame()
for col in ["dataset","packet","priority_rank","driver","kind","badges","Composite"]:
    if col not in sl.columns:
        sl[col] = np.nan

df = pd.merge(
    sumdf,
    sl[["dataset","packet","priority_rank","driver","kind","badges","Composite"]],
    on="dataset",
    how="left"
)

GALLERY_PDF = PACKETS_ROOT / "packets_gallery_v3.pdf"
INDEX_CSV   = PACKETS_ROOT / "packets_onepager_index_v3.csv"

# ---------- build pages ----------
pages = 0
rows  = []

with PdfPages(GALLERY_PDF) as gallery:
    for _, r in df.iterrows():
        pkt_dir = Path(str(r.get("packet",""))) if pd.notna(r.get("packet")) else None
        if not pkt_dir or not pkt_dir.exists():
            continue

        # images expected from prior cell
        names = ["plot_timeseries.png","plot_rfi_vs_dh.png","plot_c_vs_h.png","plot_curvature_proxy.png"]
        imgs  = [imread(pkt_dir/n) for n in names]
        if not any(imgs):
            # nothing to render
            continue

        md_path = pkt_dir / "packet.md"
        md      = read_text(md_path)
        title   = first_md_h1(md) or str(r["dataset"])
        subtitle= " ".join(str(z) for z in [r.get("kind",""), r.get("badges","")] if pd.notna(z)).strip()

        # tiny evidence summary from Auto Plots section
        ev_match = re.search(r"## Auto Plots & Evidence \(v3\)\n(.+?)(?:\n## |\Z)", md, re.S)
        evidence = ""
        if ev_match:
            block = ev_match.group(1)
            bullets = [ln.strip(" -") for ln in block.splitlines() if ln.lstrip().startswith("-")]
            evidence = " • ".join(bullets[:3])

        # compose one-page figure
        fig = plt.figure(figsize=(11, 8.5))

        # Header
        axH = fig.add_axes([0.04, 0.865, 0.92, 0.11]); axH.axis("off")
        axH.text(0, 0.70, title, fontsize=16, weight="bold")
        meta = (
            f"prio {fmtf(r.get('priority_rank'),0)} • driver {r.get('driver','')} • "
            f"Composite {fmtf(r.get('Composite'))} • RFI p95 {fmtf(r.get('rfi_p95'))} • "
            f"C_mean {fmtf(r.get('C_mean'))} • |dH| {fmtf(r.get('dH_mean_abs'))} • "
            f"drift_ratio {fmtf(r.get('drift_ratio'),3)}"
        )
        axH.text(0, 0.28, meta, fontsize=9)
        if subtitle:
            axH.text(0, 0.06, subtitle, fontsize=10)

        # Evidence line
        axE = fig.add_axes([0.04, 0.825, 0.92, 0.03]); axE.axis("off")
        if evidence:
            axE.text(0, 0.0, "Evidence: " + evidence, fontsize=9)

        # Plots grid
        ax1 = fig.add_axes([0.04, 0.47, 0.58, 0.34]); ax1.axis("off")
        if imgs[0] is not None: ax1.imshow(imgs[0]); ax1.set_title("Timeseries", fontsize=10)

        ax2 = fig.add_axes([0.66, 0.61, 0.30, 0.21]); ax2.axis("off")
        if imgs[1] is not None: ax2.imshow(imgs[1]); ax2.set_title("RFI vs dH", fontsize=9)

        ax3 = fig.add_axes([0.66, 0.37, 0.30, 0.21]); ax3.axis("off")
        if imgs[2] is not None: ax3.imshow(imgs[2]); ax3.set_title("C vs H", fontsize=9)

        ax4 = fig.add_axes([0.04, 0.06, 0.92, 0.28]); ax4.axis("off")
        if imgs[3] is not None: ax4.imshow(imgs[3]); ax4.set_title("Curvature proxy (rolling logdet)", fontsize=9, loc="left")

        # save single and add to gallery
        onepager = pkt_dir / "packet_onepager_v3.pdf"
        fig.savefig(onepager, dpi=150, bbox_inches="tight")
        gallery.savefig(fig)
        plt.close(fig)

        # append link to packet.md
        link_md = "[Open one-pager (PDF)](packet_onepager_v3.pdf)"
        add_or_replace_section(md_path, "Auto One-Pager (v3)", link_md)

        pages += 1
        rows.append({
            "dataset": r["dataset"],
            "packet": str(pkt_dir),
            "onepager": str(onepager),
            "priority_rank": r.get("priority_rank",""),
            "Composite": r.get("Composite", np.nan),
            "rfi_p95": r.get("rfi_p95", np.nan),
            "C_mean": r.get("C_mean", np.nan),
            "dH_mean_abs": r.get("dH_mean_abs", np.nan),
            "drift_ratio": r.get("drift_ratio", np.nan),
            "driver": r.get("driver",""),
            "badges": r.get("badges","")
        })

# index + print preview
idx = pd.DataFrame(rows)
if not idx.empty:
    idx.sort_values(["priority_rank","Composite"], ascending=[True, False], inplace=True)
    idx.to_csv(INDEX_CSV, index=False)

print(f"Built {pages} one-pagers.")
print("Gallery PDF ->", GALLERY_PDF)
print("Index CSV   ->", INDEX_CSV)
if not idx.empty:
    print(idx.head(12).to_string(index=False))


Built 0 one-pagers.
Gallery PDF -> C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\packets_gallery_v3.pdf
Index CSV   -> C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\packets_onepager_index_v3.csv


In [19]:
# CNT packets → One-pager PDFs + Gallery (v3.1, adaptive)
# Uses packet_plots_summary.csv to find packet dirs, auto-detects images in each packet folder.

import re
from pathlib import Path
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from matplotlib.backends.backend_pdf import PdfPages

ROOT         = Path(r"C:\Users\caleb\CNT_Lab")
OUT_DIR      = ROOT / r"artifacts\cnt_five_pillars"
PACKETS_ROOT = OUT_DIR / "packets_v3"
SUMMARY      = PACKETS_ROOT / "packet_plots_summary.csv"  # you just wrote this

# ---------- tiny utils ----------
def read_text(p: Path) -> str:
    try: return p.read_text(encoding="utf-8", errors="ignore")
    except: return ""

def first_md_h1(md: str) -> str:
    m = re.search(r"^#\s+(.+)$", md, re.M)
    return m.group(1).strip() if m else ""

def add_or_replace_section(md_path: Path, header: str, body_md: str):
    txt = read_text(md_path)
    block = f"\n\n## {header}\n{body_md}\n"
    pat = re.compile(rf"\n## {re.escape(header)}\n.*?(?=\n## |\Z)", re.S)
    new = pat.sub(block, txt) if pat.search(txt) else (txt.rstrip() + block)
    md_path.write_text(new, encoding="utf-8", errors="ignore")

def imread_safe(p: Path):
    try: return plt.imread(p)
    except: return None

def pick_images(pkt_dir: Path):
    """Pick up to 4 images. Prefer semantic matches; otherwise grab newest PNGs."""
    pngs = sorted(pkt_dir.glob("*.png")) + sorted(pkt_dir.glob("*.jpg"))
    if not pngs: return [None, None, None, None]

    def first_match(keywords):
        for k in keywords:
            for img in pngs:
                name = img.name.lower()
                if all(part in name for part in k if isinstance(k, tuple)) or (isinstance(k, str) and k in name):
                    return img
        return None

    # prefer these buckets
    times   = first_match([("time","series"), "timeseries", "ts_", "timeline"])
    rfi_dh  = first_match([("rfi","dh"), "rfi_vs_dh", "rfi-dh", "rfi"])
    cvsh    = first_match([("c","h"), "c_vs_h", "c-vs-h", "coherence_entropy"])
    curv    = first_match(["curv", "curvature", "logdet", "geometry"])

    chosen = []
    for c in [times, rfi_dh, cvsh, curv]:
        if c and c not in chosen:
            chosen.append(c)

    # backfill with newest remaining
    remaining = [p for p in pngs if p not in chosen]
    remaining.sort(key=lambda p: p.stat().st_mtime, reverse=True)
    while len(chosen) < 4 and remaining:
        chosen.append(remaining.pop(0))

    # pad to exactly 4
    while len(chosen) < 4:
        chosen.append(None)
    return chosen[:4]

def fmt(x, n=6):
    try:
        if x is None or (isinstance(x, float) and (np.isnan(x) or np.isinf(x))):
            return "—"
        return f"{float(x):.{n}f}"
    except:
        return "—"

# ---------- load summary ----------
if not SUMMARY.exists():
    raise FileNotFoundError(f"Missing summary CSV: {SUMMARY}")
df = pd.read_csv(SUMMARY)
if "packet" not in df.columns:
    raise ValueError("Summary CSV must contain a 'packet' column with packet directories.")

GALLERY_PDF = PACKETS_ROOT / "packets_gallery_v3.pdf"
INDEX_CSV   = PACKETS_ROOT / "packets_onepager_index_v3.csv"

rows = []
built_pages = 0

with PdfPages(GALLERY_PDF) as gallery:
    for _, r in df.iterrows():
        pkt_dir = Path(str(r["packet"])) if pd.notna(r["packet"]) else None
        if not pkt_dir or not pkt_dir.exists():
            continue

        md_path = pkt_dir / "packet.md"
        title = first_md_h1(read_text(md_path)) or str(r.get("dataset","(unknown dataset)"))
        meta_line = (
            f"RFI p95 {fmt(r.get('rfi_p95'))} • "
            f"C_mean {fmt(r.get('C_mean'))} • "
            f"|dH| {fmt(r.get('dH_mean_abs'))} • "
            f"drift_ratio {fmt(r.get('drift_ratio'),3)}"
        )

        imgs = pick_images(pkt_dir)
        if not any(imgs):
            continue
        ims = [imread_safe(p) if p else None for p in imgs]
        if not any(ims):
            continue

        # Make one-pager
        fig = plt.figure(figsize=(11, 8.5))
        # header
        axH = fig.add_axes([0.04, 0.865, 0.92, 0.11]); axH.axis("off")
        axH.text(0, 0.70, title, fontsize=16, weight="bold")
        axH.text(0, 0.28, meta_line, fontsize=9)
        # grid
        ax1 = fig.add_axes([0.04, 0.47, 0.58, 0.34]); ax1.axis("off")
        if ims[0] is not None: ax1.imshow(ims[0]); ax1.set_title(imgs[0].name, fontsize=9, loc="left")

        ax2 = fig.add_axes([0.66, 0.61, 0.30, 0.21]); ax2.axis("off")
        if ims[1] is not None: ax2.imshow(ims[1]); ax2.set_title(imgs[1].name, fontsize=8, loc="left")

        ax3 = fig.add_axes([0.66, 0.37, 0.30, 0.21]); ax3.axis("off")
        if ims[2] is not None: ax3.imshow(ims[2]); ax3.set_title(imgs[2].name, fontsize=8, loc="left")

        ax4 = fig.add_axes([0.04, 0.06, 0.92, 0.28]); ax4.axis("off")
        if ims[3] is not None: ax4.imshow(ims[3]); ax4.set_title(imgs[3].name, fontsize=8, loc="left")

        # save
        onepager = pkt_dir / "packet_onepager_v3.pdf"
        fig.savefig(onepager, dpi=150, bbox_inches="tight")
        gallery.savefig(fig)
        plt.close(fig)

        # link into packet.md
        add_or_replace_section(md_path, "Auto One-Pager (v3)", "[Open one-pager (PDF)](packet_onepager_v3.pdf)")

        rows.append({
            "dataset": r.get("dataset",""),
            "packet": str(pkt_dir),
            "onepager": str(onepager),
            "rfi_p95": r.get("rfi_p95", np.nan),
            "C_mean": r.get("C_mean", np.nan),
            "dH_mean_abs": r.get("dH_mean_abs", np.nan),
            "drift_ratio": r.get("drift_ratio", np.nan),
        })
        built_pages += 1

# index
idx = pd.DataFrame(rows)
if not idx.empty:
    idx.to_csv(INDEX_CSV, index=False)

print(f"Built {built_pages} one-pagers")
print("Gallery:", GALLERY_PDF)
print("Index:  ", INDEX_CSV)
if not idx.empty:
    print(idx.head(min(12, len(idx))).to_string(index=False))


ValueError: The truth value of an array with more than one element is ambiguous. Use a.any() or a.all()

In [20]:
# === Build one-pagers (CORRECTED guards to avoid NumPy truthiness error) ===
import os, sys, math
from pathlib import Path
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from matplotlib.backends.backend_pdf import PdfPages

# --- Config (kept consistent with your run) ---
PACKETS_DIR = Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3")
INDEX_CSV   = PACKETS_DIR / "packets_onepager_index_v3.csv"
GALLERY_PDF = PACKETS_DIR / "packets_gallery_v3.pdf"

# --- Fallback helpers (used only if your originals aren't already defined) ---
try:
    imread_safe
except NameError:
    import imageio.v3 as iio
    def imread_safe(p):
        try:
            return iio.imread(p)
        except Exception:
            return None

try:
    pick_images
except NameError:
    def pick_images(pkt_dir: Path, limit=4):
        exts = {".png", ".jpg", ".jpeg", ".webp"}
        found = []
        for root, _, files in os.walk(pkt_dir):
            for f in files:
                if Path(f).suffix.lower() in exts:
                    found.append(str(Path(root) / f))
        # crude preference: sort by typical plot names
        order = ["overview", "rfi", "coh", "entropy", "drift", "summary"]
        found.sort(key=lambda s: min((s.lower().find(k), k) for k in order)[0])
        return found[:limit] or []

try:
    render_onepager
except NameError:
    # Minimal 2x2 grid renderer; swap out with your richer layout if defined elsewhere
    def render_onepager(meta_row: dict, ims: list):
        cols = 2
        imgs = [im for im in ims if (im is not None) and getattr(im, "size", 0) > 0]
        rows = math.ceil(len(imgs) / cols) or 1
        fig, axes = plt.subplots(rows, cols, figsize=(11, 8.5), dpi=150)
        axes = np.atleast_2d(axes)
        i = 0
        for r in range(rows):
            for c in range(cols):
                ax = axes[r, c]
                if i < len(imgs):
                    ax.imshow(imgs[i])
                    ax.axis("off")
                else:
                    ax.remove()
                i += 1
        title = str(meta_row.get("dataset", meta_row.get("packet", "Packet")))
        fig.suptitle(title, fontsize=12, y=0.99)
        fig.tight_layout(rect=[0, 0, 1, 0.97])
        return fig

# --- Load packet index (or discover packets if index is missing) ---
if INDEX_CSV.exists():
    idx = pd.read_csv(INDEX_CSV)
else:
    # Discover packets; build a minimal index on the fly
    pkt_dirs = [p for p in PACKETS_DIR.iterdir() if p.is_dir()]
    idx = pd.DataFrame({"packet": [str(p) for p in pkt_dirs], "dataset": [p.name for p in pkt_dirs]})

# --- Build one-pagers & gallery (with corrected image guards) ---
built_rows = []
with PdfPages(GALLERY_PDF) as gallery:
    for _, row in idx.iterrows():
        pkt_dir = Path(row.get("packet", "")) if "packet" in row else Path(row["dataset"])
        if not pkt_dir.exists():
            continue

        # find candidate image paths
        imgs = pick_images(pkt_dir)

        # GUARD #1 — any *paths* to try?
        if not any((p is not None) and Path(p).exists() for p in imgs):
            continue

        # read images (None on failure)
        ims = [imread_safe(p) if p else None for p in imgs]

        # GUARD #2 — any *arrays* actually loaded?
        if not any((im is not None) and getattr(im, "size", 0) > 0 for im in ims):
            continue

        # render page
        fig = render_onepager(row.to_dict(), ims)

        # save per-packet one-pager
        onepager_path = pkt_dir / "onepager_v3.pdf"
        fig.savefig(onepager_path, bbox_inches="tight")

        # add to gallery
        gallery.savefig(fig, bbox_inches="tight")
        plt.close(fig)

        built_rows.append({
            "dataset": row.get("dataset", pkt_dir.name),
            "packet": str(pkt_dir),
            "onepager": str(onepager_path)
        })

# update index with produced one-pagers
out_df = pd.DataFrame(built_rows)
if not out_df.empty:
    out_df.to_csv(INDEX_CSV, index=False)

print(f"Built {len(built_rows)} one-pagers.")
print(f"Gallery PDF -> {GALLERY_PDF}")
print(f"Index CSV   -> {INDEX_CSV}")


Built 22 one-pagers.
Gallery PDF -> C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\packets_gallery_v3.pdf
Index CSV   -> C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\packets_onepager_index_v3.csv


In [21]:
# CNT Five Pillars — Packet Bundle & Executive Brief (v3)
import os, json, zipfile
import pandas as pd
import numpy as np
from pathlib import Path
from datetime import datetime

# --- Paths (adjust if needed) ---
ART = Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars")
PK  = ART / "packets_v3"

MASTER = ART / "CNT_Master_Sheet_v3.csv"
SUMMARY = PK  / "packet_plots_summary.csv"
INDEX   = PK  / "packets_onepager_index_v3.csv"
GALLERY = PK  / "packets_gallery_v3.pdf"

BRIEF_MD = PK / "CNT_Executive_Brief_v3.md"
MANIFEST = PK / "packets_manifest_v3.json"
BUNDLE   = PK / "CNT_packets_bundle_v3.zip"

PK.mkdir(parents=True, exist_ok=True)

def read_csv_safe(p):
    try:
        df = pd.read_csv(p)
        print(f"[ok] {p.name}: {df.shape}")
        return df
    except Exception as e:
        print(f"[warn] {p}: {e}")
        return pd.DataFrame()

master = read_csv_safe(MASTER)
summ   = read_csv_safe(SUMMARY)
index_ = read_csv_safe(INDEX)

# Normalize expected columns if needed
# master: dataset, kind, priority_rank, Composite, badges, driver  (expected)
for col in ["dataset","kind","priority_rank","Composite","badges","driver"]:
    if col not in master.columns:
        master[col] = np.nan

# summary: dataset, rfi_p95, C_mean, dH_mean_abs, drift_ratio, alpha_used, packet  (packet may be absent here)
for col in ["dataset","rfi_p95","C_mean","dH_mean_abs","drift_ratio","alpha_used","packet"]:
    if col not in summ.columns:
        if col == "packet" and "packet" not in index_.columns:
            # derive packet path heuristically from dataset
            summ[col] = np.nan
        else:
            summ[col] = np.nan

# index: dataset, packet (minimal)
if "dataset" not in index_.columns:
    # try to find a reasonable column containing dataset names
    cand = [c for c in index_.columns if "dataset" in c.lower()]
    if cand: index_ = index_.rename(columns={cand[0]:"dataset"})
if "packet" not in index_.columns:
    # try to find a reasonable column containing packet paths
    cand = [c for c in index_.columns if "packet" in c.lower()]
    if cand: index_ = index_.rename(columns={cand[0]:"packet"})
if "packet" not in index_.columns:
    index_["packet"] = np.nan

# Merge all info
cols_summary = ["dataset","rfi_p95","C_mean","dH_mean_abs","drift_ratio","alpha_used"]
cols_index   = ["dataset","packet"]
enriched = (master
            .merge(summ[cols_summary + (["packet"] if "packet" in summ.columns else [])],
                   on="dataset", how="left", suffixes=("","_sum"))
            .merge(index_[cols_index], on="dataset", how="left", suffixes=("","_idx")))

# Prefer packet path from index if summary lacked it
if "packet_sum" in enriched.columns:
    enriched["packet_path"] = enriched["packet_sum"].fillna(enriched["packet"])
else:
    enriched["packet_path"] = enriched["packet"]

# Sort by priority then Composite (desc for composite when rank ties)
enriched["priority_rank"] = pd.to_numeric(enriched["priority_rank"], errors="coerce")
enriched["Composite"]     = pd.to_numeric(enriched["Composite"], errors="coerce")
enriched_sorted = enriched.sort_values(["priority_rank","Composite"],
                                       ascending=[True, False]).reset_index(drop=True)

# Build manifest
manifest = []
for _, r in enriched_sorted.iterrows():
    manifest.append({
        "dataset":   r.get("dataset"),
        "kind":      r.get("kind"),
        "driver":    r.get("driver"),
        "priority_rank": r.get("priority_rank"),
        "composite": r.get("Composite"),
        "badges":    r.get("badges"),
        "metrics": {
            "rfi_p95":  r.get("rfi_p95"),
            "C_mean":   r.get("C_mean"),
            "dH_mean":  r.get("dH_mean_abs"),
            "drift_ratio": r.get("drift_ratio"),
            "alpha_used":  r.get("alpha_used"),
        },
        "packet":    r.get("packet_path")
    })

with open(MANIFEST, "w", encoding="utf-8") as f:
    json.dump(manifest, f, indent=2)
print(f"[write] {MANIFEST}")

# ---- Executive Brief (Markdown) ----
ts = datetime.now().strftime("%Y-%m-%d %H:%M:%S")
lines = []
lines.append(f"# CNT Packets — Executive Brief v3\n")
lines.append(f"_Generated: {ts}_\n")
lines.append(f"- Source sheets: `{MASTER.name}`, `{SUMMARY.name}`, `{INDEX.name}`")
lines.append(f"- Gallery: `{GALLERY.name}`\n")

def mk_table(df, cols):
    df2 = df[cols].copy()
    # friendly rounding
    for c in ["Composite","rfi_p95","C_mean","dH_mean_abs","drift_ratio"]:
        if c in df2.columns:
            df2[c] = pd.to_numeric(df2[c], errors="coerce").round(6)
    return "|\n".join([
        "| " + " | ".join(cols) + " |",
        "| " + " | ".join(["---"]*len(cols)) + " |",
        *["| " + " | ".join("" if pd.isna(v) else str(v) for v in row) + " |"
          for row in df2.to_numpy()]
    ])

def section(title, df, n):
    lines.append(f"## {title}\n")
    cols = ["dataset","kind","priority_rank","Composite","badges","driver",
            "rfi_p95","drift_ratio","packet_path"]
    cols = [c for c in cols if c in df.columns]
    lines.append(mk_table(df.head(n), cols))
    lines.append("")

# Sections
section("Top-priority (All kinds)", enriched_sorted, 12)
section("Top-priority REAL", enriched_sorted[enriched_sorted["kind"]=="real"], 12)
section("Top-priority SYNTH", enriched_sorted[enriched_sorted["kind"]=="synth"], 6)

BRIEF_MD.write_text("\n".join(lines), encoding="utf-8")
print(f"[write] {BRIEF_MD}")

# ---- Zip bundle (gallery + sheets + brief + manifest) ----
to_zip = [p for p in [GALLERY, INDEX, MASTER, SUMMARY, BRIEF_MD, MANIFEST] if p.exists()]
with zipfile.ZipFile(BUNDLE, "w", compression=zipfile.ZIP_DEFLATED) as z:
    for p in to_zip:
        z.write(p, arcname=p.name)
print(f"[zip] {BUNDLE}  (+{len(to_zip)} files)")

# Tiny report
print("\n== Bundle contents ==")
for p in to_zip:
    print(" -", p.name)
print("\nDone.")


[ok] CNT_Master_Sheet_v3.csv: (22, 33)
[ok] packet_plots_summary.csv: (22, 7)
[ok] packets_onepager_index_v3.csv: (22, 3)
[write] C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\packets_manifest_v3.json
[write] C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\CNT_Executive_Brief_v3.md
[zip] C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\CNT_packets_bundle_v3.zip  (+6 files)

== Bundle contents ==
 - packets_gallery_v3.pdf
 - packets_onepager_index_v3.csv
 - CNT_Master_Sheet_v3.csv
 - packet_plots_summary.csv
 - CNT_Executive_Brief_v3.md
 - packets_manifest_v3.json

Done.


In [22]:
# CNT Packets — Run Cards & Lab Proof Checklists (v3)
import os, re, json
from pathlib import Path
from datetime import datetime
import pandas as pd
import numpy as np

# --- Roots ---
ART = Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars")
PK  = ART / "packets_v3"

MASTER  = ART / "CNT_Master_Sheet_v3.csv"
SUMMARY = PK  / "packet_plots_summary.csv"
INDEX   = PK  / "packets_onepager_index_v3.csv"
MANIFEST= PK  / "packets_manifest_v3.json"  # optional
GALLERY = PK  / "packets_gallery_v3.pdf"    # for reference

RUN_DIR = PK / "run_cards_v3"
RUNLIST = PK / "runlist_v3.csv"

RUN_DIR.mkdir(parents=True, exist_ok=True)

def read_csv_safe(p):
    try:
        df = pd.read_csv(p)
        print(f"[ok] {p.name}: {df.shape}")
        return df
    except Exception as e:
        print(f"[warn] {p.name}: {e}")
        return pd.DataFrame()

def read_json_safe(p):
    if p.exists():
        try:
            with open(p, "r", encoding="utf-8") as f:
                return json.load(f)
        except Exception as e:
            print(f"[warn] {p.name}: {e}")
    return None

master = read_csv_safe(MASTER)
summ   = read_csv_safe(SUMMARY)
index_ = read_csv_safe(INDEX)
mani   = read_json_safe(MANIFEST) or []

# Normalize master expected cols
for col in ["dataset","kind","priority_rank","Composite","badges","driver","source","packet"]:
    if col not in master.columns:
        master[col] = np.nan

# summary expected cols
for col in ["dataset","rfi_p95","C_mean","dH_mean_abs","drift_ratio","alpha_used"]:
    if col not in summ.columns:
        summ[col] = np.nan

# index expected cols
if "dataset" not in index_.columns:
    cand = [c for c in index_.columns if "dataset" in c.lower()]
    if cand: index_ = index_.rename(columns={cand[0]:"dataset"})
if "packet" not in index_.columns:
    cand = [c for c in index_.columns if "packet" in c.lower()]
    if cand: index_ = index_.rename(columns={cand[0]:"packet"})
if "packet" not in index_.columns:
    index_["packet"] = np.nan

# Merge
enriched = (master
    .merge(summ[["dataset","rfi_p95","C_mean","dH_mean_abs","drift_ratio","alpha_used"]], on="dataset", how="left")
    .merge(index_[["dataset","packet"]], on="dataset", how="left", suffixes=("","_idx")))

# Prefer explicit packet path in master, else index
enriched["packet_path"] = enriched["packet"].where(enriched["packet"].notna(), master["packet"])

# Helper: slug for filenames
def slug(s, n=72):
    s = re.sub(r"[^\w\-\.]+","_", str(s)).strip("_")
    return (s[:n]).rstrip("_") or "item"

# Compose checklist text
def checklist_md(r):
    ds   = r.get("dataset")
    kind = r.get("kind")
    drv  = r.get("driver")
    pr   = r.get("priority_rank")
    comp = r.get("Composite")
    bdg  = r.get("badges")

    rfi  = r.get("rfi_p95")
    Cmu  = r.get("C_mean")
    dH   = r.get("dH_mean_abs")
    dR   = r.get("drift_ratio")
    alp  = r.get("alpha_used")

    pkt  = r.get("packet_path")
    src  = r.get("source") or ""

    ts = datetime.now().strftime("%Y-%m-%d %H:%M:%S")

    def fmt(x, nd=6):
        try:
            return f"{float(x):.{nd}f}"
        except:
            return str(x) if pd.notna(x) else "NaN"

    # Header
    lines = []
    lines += [
        f"# RUN CARD — {ds}",
        "",
        f"_Generated: {ts}_",
        "",
        "## Overview",
        f"- **Kind**: `{kind}`   •   **Driver**: `{drv}`   •   **Priority rank**: `{pr}`   •   **Composite**: `{fmt(comp,6)}`",
        f"- **Badges**: `{bdg}`",
        f"- **Packet**: `{pkt}`",
        f"- **Source**: `{src}`",
        "",
        "## Metrics Snapshot",
        "",
        "| rfi_p95 | C_mean | dH_mean_abs | drift_ratio | alpha_used |",
        "|---:|---:|---:|---:|---:|",
        f"| {fmt(rfi)} | {fmt(Cmu)} | {fmt(dH)} | {fmt(dR)} | {fmt(alp)} |",
        "",
        "## Proof Gates (Five Pillars)",
        "",
        "### E — Entropy & Resonance",
        "- [ ] **E1**: Compute H(t), dH(t) (spectral/permutation); compute C(t) (PLV/NMI).",
        "- [ ] **E2**: Fit α for RFI to maximize lead-time concordance.",
        "- [ ] **E3**: Show RFI vs time-to-collapse curves; report AUC/Precision@Θ.",
        "",
        "### I — Information-Theoretic Core",
        "- [ ] **I1**: Estimate F_CNT = H − λC; verify glyph vs random ΔF with CI.",
        "- [ ] **I2**: Ablate λ and report sensitivity.",
        "",
        "### C — Invariants & Symmetry",
        "- [ ] **C1**: Construct glyph/symbol graph; compute invariant(s) (e.g., MI spectrum/Betti).",
        "- [ ] **C2**: Show invariant drift < metric drift across perturbations.",
        "",
        "### G — Information Geometry",
        "- [ ] **G1**: Estimate local Fisher metric; compute scalar curvature \\(\\mathcal{R}\\).",
        "- [ ] **G2**: Regress lead time Θ on \\(\\mathcal{R}^{-}\\) and RFI; test β₁<0.",
        "",
        "### O — Oracle Policy",
        "- [ ] **O1**: Train risk model; set thresholds τ (risk) and τ₂ (uplift).",
        "- [ ] **O2**: Closed-loop vs open-loop comparison under matched budget.",
        "",
        "## Data & Files",
        f"- Dataset: `{ds}`",
        f"- Packet: `{pkt}`",
        f"- Gallery PDF (global): `{GALLERY}`",
        "",
        "## Notes",
        "> Findings, anomalies, caveats, TODOs…",
        "",
        "---",
        ""
    ]
    return "\n".join(lines)

# Sort by priority then composite
enriched["priority_rank"] = pd.to_numeric(enriched["priority_rank"], errors="coerce")
enriched["Composite"]     = pd.to_numeric(enriched["Composite"], errors="coerce")
enriched_sorted = enriched.sort_values(["priority_rank","Composite"], ascending=[True, False]).reset_index(drop=True)

# Generate run cards
rows = []
for i, r in enriched_sorted.iterrows():
    row = r.to_dict()
    ds  = row.get("dataset")
    pkt = row.get("packet_path")
    # Target path
    base = RUN_DIR / f"{i:02d}__{slug(ds)}.md"
    try:
        md = checklist_md(row)
        base.write_text(md, encoding="utf-8")
        ok = True
    except Exception as e:
        print(f"[warn] failed run card for {ds}: {e}")
        ok = False
    rows.append({
        "rank": i+1,
        "dataset": ds,
        "kind": row.get("kind"),
        "driver": row.get("driver"),
        "priority_rank": row.get("priority_rank"),
        "Composite": row.get("Composite"),
        "packet": pkt,
        "run_card": str(base),
        "status": "ok" if ok else "error"
    })

runlist_df = pd.DataFrame(rows)
runlist_df.to_csv(RUNLIST, index=False)
print(f"[write] {RUNLIST}  ({len(runlist_df)} items)")

# Tiny report
ok_n = (runlist_df["status"]=="ok").sum()
print(f"\n== Run Cards ==")
print(f" ok: {ok_n}  /  total: {len(runlist_df)}")
print(f" dir: {RUN_DIR}")
print("\nSample:")
print(runlist_df.head(8).to_string(index=False))


[ok] CNT_Master_Sheet_v3.csv: (22, 33)
[ok] packet_plots_summary.csv: (22, 7)
[ok] packets_onepager_index_v3.csv: (22, 3)
[write] C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\runlist_v3.csv  (22 items)

== Run Cards ==
 ok: 22  /  total: 22
 dir: C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\run_cards_v3

Sample:
 rank                                                                        dataset kind driver  priority_rank  Composite  packet                                                                                                                                                  run_card status
    1 artifacts__tables__genome3d__atlas__nodes_v1h_realhic__20251009-020445.parquet real      E            1.0   0.343132     NaN C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\run_cards_v3\00__artifacts__tables__genome3d__atlas__nodes_v1h_realhic__20251009-020445.p.md     ok
    2          artifacts__tables__genome3d__atlas__genes_v1__20251008-

In [23]:
# CNT Ops — Execution Tracker + Brief + Appendix + Burndown (v3)
import os, io, json, zipfile, textwrap, math, re
from pathlib import Path
from datetime import datetime, timedelta
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

# --- Paths ---
ART = Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars")
PK  = ART / "packets_v3"
PK.mkdir(parents=True, exist_ok=True)

RUNLIST = PK / "runlist_v3.csv"
RUN_DIR = PK / "run_cards_v3"

TRACKER = PK / "execution_tracker_v3.csv"
BRIEF   = PK / "Daily_Brief_v3.md"
APPX    = PK / "LawSheet_Appendix_Runlist_v3.md"
XLSX    = PK / "CNT_Execution_Tracker_v3.xlsx"
BURN    = PK / "burndown_v3.png"
ZIPF    = PK / "CNT_ops_bundle_v3.zip"

GALLERY = PK / "packets_gallery_v3.pdf"  # reference if present

# --- Read runlist ---
def read_csv_safe(p):
    try:
        df = pd.read_csv(p)
        print(f"[ok] {p} {df.shape}")
        return df
    except Exception as e:
        print(f"[err] reading {p}: {e}")
        return pd.DataFrame()

runlist = read_csv_safe(RUNLIST)
if runlist.empty:
    raise SystemExit("runlist_v3.csv not found or empty")

# Normalize/ensure columns
need_cols = ["rank","dataset","kind","driver","priority_rank","Composite","packet","run_card","status"]
for c in need_cols:
    if c not in runlist.columns:
        runlist[c] = np.nan

# --- Build tracker (idempotent + merge if exists) ---
now = pd.Timestamp.now()
base_cols = [
    "rank","dataset","kind","driver","priority_rank","Composite","packet","run_card"
]
tracker_new = runlist[base_cols].copy()

# default metadata
tracker_new["owner"]   = ""
tracker_new["status"]  = "todo"   # todo, doing, review, done, hold
tracker_new["notes"]   = ""
tracker_new["created"] = now
tracker_new["updated"] = now

# pillar gates
for g in ["E","I","C","G","O"]:
    tracker_new[f"{g}_done"]  = False
    tracker_new[f"{g}_notes"] = ""

# due dates by priority (earlier rank/priority -> sooner)
# heuristic: top priority = today+1d, then +1d per priority step, capped min 1 day
def due_from_priority(pr):
    try:
        pr = float(pr)
    except:
        pr = np.nan
    step = 1 if pd.isna(pr) else max(1, int(math.ceil(pr)))
    return (now + pd.Timedelta(days=step)).normalize() + pd.Timedelta(hours=17)  # 5pm

tracker_new["due"] = tracker_new["priority_rank"].apply(due_from_priority)

# merge with existing tracker (preserve manual edits)
if TRACKER.exists():
    old = pd.read_csv(TRACKER, parse_dates=["created","updated","due"], keep_default_na=False)
    # outer join on dataset; prefer existing manual fields if present
    key = "dataset"
    merged = tracker_new.merge(old.drop_duplicates(key), on=key, how="left", suffixes=("","_old"))

    def pick(a,b):
        return a if pd.notna(a) and (a!="" or isinstance(a,bool)) else b

    keep_cols = []
    out = pd.DataFrame()
    for col in tracker_new.columns:
        oc = f"{col}_old"
        if oc in merged.columns:
            out[col] = [pick(a,b) for a,b in zip(merged[col], merged[oc])]
        else:
            out[col] = merged[col]
        keep_cols.append(col)
    tracker = out[keep_cols].copy()
else:
    tracker = tracker_new.copy()

# Fix types
bool_cols = [c for c in tracker.columns if c.endswith("_done")]
for c in bool_cols:
    tracker[c] = tracker[c].astype(bool)

for c in ["created","updated","due"]:
    if c in tracker.columns:
        tracker[c] = pd.to_datetime(tracker[c], errors="coerce")

# --- Progress KPI helpers ---
def gate_score(row):
    tot = sum(bool(row[f"{g}_done"]) for g in "EICGO")
    return tot / 5.0

tracker["proof_score"] = tracker.apply(gate_score, axis=1)

# --- Save tracker ---
tracker.sort_values(["priority_rank","Composite"], ascending=[True,False], inplace=True, na_position="last")
tracker.to_csv(TRACKER, index=False)
print(f"[write] {TRACKER}  ({len(tracker)} rows)")

# --- Burndown (naive): completed items / gates over ranks ---
# Compute daily remaining gates assuming 5 per item, mark done gates
def burndown_series(df):
    # simplistic snapshot: remaining gates by cumulative rank
    df = df.copy().sort_values("rank")
    total_gates = 5 * len(df)
    done_gates  = df[[f"{g}_done" for g in "EICGO"]].sum(axis=1).cumsum()
    remaining   = total_gates - done_gates
    return pd.DataFrame({"rank": df["rank"].values, "remaining_gates": remaining})

bd = burndown_series(tracker)
plt.figure(figsize=(8,4.5))
plt.plot(bd["rank"], bd["remaining_gates"], linewidth=2)
plt.title("CNT Five-Pillars — Burndown (remaining gates vs rank)")
plt.xlabel("Cumulative rank")
plt.ylabel("Remaining gates")
plt.grid(True, linestyle="--", alpha=0.4)
plt.tight_layout()
plt.savefig(BURN, dpi=150)
plt.close()
print(f"[write] {BURN}")

# --- Daily Brief (Markdown) ---
def brief_md(df: pd.DataFrame) -> str:
    df = df.copy()
    df["status"] = df["status"].fillna("todo")
    counts = df["status"].value_counts()
    kpi = {
        "total_items": int(len(df)),
        "done_items":  int((df["status"]=="done").sum()),
        "doing_items": int((df["status"]=="doing").sum()),
        "review_items":int((df["status"]=="review").sum()),
        "hold_items":  int((df["status"]=="hold").sum()),
        "avg_proof":   float(df["proof_score"].mean() if len(df) else 0),
    }
    # next up (top 5 todos/doing by priority, then composite)
    nxt = df[df["status"].isin(["todo","doing"])].sort_values(
        ["priority_rank","Composite"], ascending=[True,False]).head(5)

    lines = []
    lines += [f"# CNT Daily Brief — {pd.Timestamp.now():%Y-%m-%d %H:%M}"]
    lines += [""]
    lines += ["## Snapshot"]
    lines += [f"- Total items: **{kpi['total_items']}**  |  Done: **{kpi['done_items']}**  |  Doing: **{kpi['doing_items']}**  |  Review: **{kpi['review_items']}**  |  Hold: **{kpi['hold_items']}**"]
    lines += [f"- Mean proof-score (E/I/C/G/O): **{kpi['avg_proof']:.2f}**"]
    lines += [f"- Burndown: {BURN}"]
    lines += [""]
    lines += ["## Next Up (Top 5)"]
    lines += ["| rank | dataset | status | driver | priority | Composite | run_card |"]
    lines += ["|---:|---|---|:---:|---:|---:|---|"]
    for _,r in nxt.iterrows():
        lines += [f"| {int(r['rank'])} | {r['dataset']} | {r['status']} | {r.get('driver','')} | {r['priority_rank']} | {r['Composite']:.6f} | {r['run_card']} |"]
    lines += ["", "## Notes", "> Add callouts, blockers, and asks here."]
    return "\n".join(lines)

BRIEF.write_text(brief_md(tracker), encoding="utf-8")
print(f"[write] {BRIEF}")

# --- Law Sheet Appendix (Markdown) ---
def appendix_md(df: pd.DataFrame) -> str:
    df = df.copy()
    df["priority_rank"] = pd.to_numeric(df["priority_rank"], errors="coerce")
    df["Composite"]     = pd.to_numeric(df["Composite"], errors="coerce")
    df.sort_values(["priority_rank","Composite"], ascending=[True,False], inplace=True, na_position="last")
    lines = []
    lines += ["# Appendix A — CNT Master Runlist (v3)"]
    lines += [""]
    lines += ["| rank | dataset | kind | driver | priority | Composite | gates (E/I/C/G/O) | run_card |"]
    lines += ["|---:|---|:---:|:---:|---:|---:|:---:|---|"]
    for _,r in df.iterrows():
        gates = "".join("✓" if r[f"{g}_done"] else "·" for g in "EICGO")
        comp  = f"{r['Composite']:.6f}" if pd.notna(r['Composite']) else ""
        lines += [f"| {int(r['rank'])} | {r['dataset']} | {r.get('kind','')} | {r.get('driver','')} | {r['priority_rank']} | {comp} | {gates} | {r['run_card']} |"]
    return "\n".join(lines)

APPX.write_text(appendix_md(tracker), encoding="utf-8")
print(f"[write] {APPX}")

# --- Excel workbook ---
with pd.ExcelWriter(XLSX, engine="xlsxwriter") as xw:
    tracker.to_excel(xw, index=False, sheet_name="Tracker")
    runlist.to_excel(xw, index=False, sheet_name="Runlist")
    ws = xw.sheets["Tracker"]
    # simple conditional format for status
    last_row = len(tracker)+1
    ws.conditional_format(f"I2:I{last_row}", {"type":"text","criteria":"containing","value":"done","format": xw.book.add_format({"bg_color":"#C6EFCE"})})
    ws.conditional_format(f"I2:I{last_row}", {"type":"text","criteria":"containing","value":"doing","format": xw.book.add_format({"bg_color":"#FFEB9C"})})
    ws.conditional_format(f"I2:I{last_row}", {"type":"text","criteria":"containing","value":"hold","format": xw.book.add_format({"bg_color":"#F4CCCC"})})
print(f"[write] {XLSX}")

# --- Utility: lightweight update function (use in later cells) ---
def update_tracker(dataset, **fields):
    """Update one row in TRACKER by dataset, set fields, stamp updated time."""
    df = pd.read_csv(TRACKER, parse_dates=["created","updated","due"], keep_default_na=False)
    m = df["dataset"]==dataset
    if not m.any():
        raise ValueError(f"dataset not found: {dataset}")
    for k,v in fields.items():
        if k not in df.columns:
            print(f"[warn] adding new column: {k}")
            df[k] = np.nan
        df.loc[m, k] = v
    df.loc[m, "updated"] = pd.Timestamp.now()
    df.to_csv(TRACKER, index=False)
    print(f"[ok] updated '{dataset}': {list(fields.keys())}")

# Example (commented):
# update_tracker("artifacts__tables__genome3d__atlas__nodes_v1h_realhic__20251009-020445.parquet",
#                status="doing", owner="caleb", E_done=True)

# --- Zip bundle ---
with zipfile.ZipFile(ZIPF, "w", compression=zipfile.ZIP_DEFLATED) as z:
    for p in [TRACKER, BRIEF, APPX, XLSX, BURN, RUNLIST]:
        if Path(p).exists():
            z.write(p, arcname=Path(p).name)
    if GALLERY.exists():
        z.write(GALLERY, arcname=GALLERY.name)
print(f"[zip] {ZIPF}")

print("\n== Outputs ==")
for p in [TRACKER, BRIEF, APPX, XLSX, BURN, ZIPF]:
    print(" -", p)


[ok] C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\runlist_v3.csv (22, 9)
[write] C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\execution_tracker_v3.csv  (22 rows)
[write] C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\burndown_v3.png
[write] C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\Daily_Brief_v3.md
[write] C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\LawSheet_Appendix_Runlist_v3.md


ModuleNotFoundError: No module named 'xlsxwriter'

In [24]:
# Patch: write Excel with engine fallback + rebuild ops zip (v3)
import zipfile, importlib
from pathlib import Path
import pandas as pd

ART = Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars")
PK  = ART / "packets_v3"
PK.mkdir(parents=True, exist_ok=True)

RUNLIST = PK / "runlist_v3.csv"
TRACKER = PK / "execution_tracker_v3.csv"
BRIEF   = PK / "Daily_Brief_v3.md"
APPX    = PK / "LawSheet_Appendix_Runlist_v3.md"
BURN    = PK / "burndown_v3.png"
GALLERY = PK / "packets_gallery_v3.pdf"  # optional
XLSX    = PK / "CNT_Execution_Tracker_v3.xlsx"
ZIPF    = PK / "CNT_ops_bundle_v3.zip"

def pick_excel_engine():
    if importlib.util.find_spec("openpyxl") is not None:
        return "openpyxl"
    if importlib.util.find_spec("xlsxwriter") is not None:
        return "xlsxwriter"
    return None

# Load current CSVs
tracker = pd.read_csv(TRACKER, parse_dates=["created","updated","due"], keep_default_na=False)
runlist = pd.read_csv(RUNLIST)

eng = pick_excel_engine()
if eng is None:
    # Fallback: no Excel engine installed — ship CSVs and warn
    print("[warn] No Excel engine found (install 'openpyxl' or 'xlsxwriter'). Skipping XLSX.")
else:
    print(f"[ok] Using Excel engine: {eng}")
    with pd.ExcelWriter(XLSX, engine=eng) as xw:
        tracker.to_excel(xw, index=False, sheet_name="Tracker")
        runlist.to_excel(xw, index=False, sheet_name="Runlist")
        if eng == "xlsxwriter":
            # Apply simple status highlighting (xlsxwriter only)
            ws = xw.sheets["Tracker"]
            last_row = len(tracker) + 1
            fmt_done  = xw.book.add_format({"bg_color":"#C6EFCE"})
            fmt_doing = xw.book.add_format({"bg_color":"#FFEB9C"})
            fmt_hold  = xw.book.add_format({"bg_color":"#F4CCCC"})
            ws.conditional_format(f"I2:I{last_row}", {"type":"text","criteria":"containing","value":"done","format":fmt_done})
            ws.conditional_format(f"I2:I{last_row}", {"type":"text","criteria":"containing","value":"doing","format":fmt_doing})
            ws.conditional_format(f"I2:I{last_row}", {"type":"text","criteria":"containing","value":"hold","format":fmt_hold})
    if eng:
        print(f"[write] {XLSX}")

# Zip bundle (always rebuild)
with zipfile.ZipFile(ZIPF, "w") as z:
    for p in [TRACKER, BRIEF, APPX, RUNLIST, BURN]:
        if Path(p).exists(): z.write(p, Path(p).name)
    if eng and XLSX.exists(): z.write(XLSX, XLSX.name)
    if GALLERY.exists(): z.write(GALLERY, GALLERY.name)
print(f"[zip] {ZIPF}")

print("\n== Outputs ==")
for p in [TRACKER, BRIEF, APPX, RUNLIST, BURN, XLSX, ZIPF]:
    print(" -", p, ("(missing)" if not Path(p).exists() else ""))


[ok] Using Excel engine: openpyxl
[write] C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\CNT_Execution_Tracker_v3.xlsx
[zip] C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\CNT_ops_bundle_v3.zip

== Outputs ==
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\execution_tracker_v3.csv 
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\Daily_Brief_v3.md 
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\LawSheet_Appendix_Runlist_v3.md 
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\runlist_v3.csv 
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\burndown_v3.png 
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\CNT_Execution_Tracker_v3.xlsx 
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\CNT_ops_bundle_v3.zip 


In [25]:
# CNT Five-Pillar Proof — Single Mega Cell (v1)
inv_m = np.nansum([motion(I0), motion(I1)])
metr_m = np.nansum([motion(C), motion(H)])
Cscore = np.nan
if np.isfinite(inv_m) and np.isfinite(metr_m) and metr_m > 0:
Cscore = 1 - float(np.clip(inv_m / (metr_m + 1e-9), 0, 1))


# G — curvature proxy via logdet(Cov)
G = np.nan
if N >= 64:
X = np.vstack([np.nan_to_num(C,0), np.nan_to_num(H,0), np.nan_to_num(dH,0), np.nan_to_num(R,0)]).T
Cov = np.cov(X.T)
sign, logdet = np.linalg.slogdet(Cov)
G = 1.0 / (1.0 + max(0.0, -float(logdet)))


# O — policy budget sweet spot ~5%
pr = float(policy_rate) if np.isfinite(policy_rate) else np.nan
O = float(np.exp(-((pr - 0.05)**2)/(2*0.05**2))) if np.isfinite(pr) else np.nan


return dict(E=E, I=I, C=Cscore, G=G, O=O, n=N)


# Composite weighting
W = dict(E=0.30, I=0.25, C=0.20, G=0.15, O=0.10)


def wmean(row):
num = den = 0.0
for k, wk in W.items():
v = row.get(k, np.nan)
if np.isfinite(v):
num += wk * float(v); den += wk
return num/den if den else np.nan


# === 4) Drive pipeline ===
if RUNLIST.exists():
sheet = pd.read_csv(RUNLIST)
# Use 'source' if present (feature CSVs), else 'dataset'
src_col = "source" if "source" in sheet.columns else "dataset"
else:
base = pd.read_csv(MASTER)
sheet = base.copy()
src_col = "source" if "source" in base.columns else "dataset"


rows = []
for i, r in sheet.iterrows():
ds = r.get("dataset", r.get(src_col, ""))
src = r.get("source", ds)
pr = r.get("policy_rate", np.nan)
kind = r.get("kind", "")
try:
feat = load_features_or_compute(src)
ms = micro_scores_from_feats(feat, pr)
comp = wmean(ms)
rows.append(dict(dataset=ds, source=src, kind=kind, Composite=comp, **ms))
except Exception as e:
rows.append(dict(dataset=ds, source=src, kind=kind, Composite=np.nan, E=np.nan, I=np.nan, C=np.nan, G=np.nan, O=np.nan, n=0, error=str(e)))


res = pd.DataFrame(rows)
res.sort_values(["Composite"], ascending=[False], inplace=True)


# Save outputs
VERDICT = OUT / "mega_verdict_v1.csv"
SUMMARY = OUT / "mega_summary_v1.txt"
res.to_csv(VERDICT, index=False)


with open(SUMMARY, "w", encoding="utf-8") as f:
f.write("== CNT Five-Pillar Mega Verdict (v1) ==
")
f.write(f"n_items = {len(res)}


")
cols = ["dataset","kind","E","I","C","G","O","Composite","n"]
f.write(res[cols].head(20).to_string(index=False))
f.write("
")


print("[write]", VERDICT)
print("[write]", SUMMARY)
print("Top-10:
", res[["dataset","kind","Composite"]].head(10).to_string(index=False))

SyntaxError: unterminated string literal (detected at line 76) (925036443.py, line 76)

In [26]:
# == CNT Five-Pillar Mega Verdict (v1.1 — fixed strings & safe I/O) ==
import os, json, textwrap, datetime as dt
from pathlib import Path
import numpy as np
import pandas as pd

# --- Paths ---
ROOT = Path(r"C:\Users\caleb\CNT_Lab")
ART  = ROOT / r"artifacts\cnt_five_pillars"
PKT  = ART  / r"packets_v3"
OUT  = ART  / r"mega_v1"
OUT.mkdir(parents=True, exist_ok=True)

RUNLIST = PKT / "runlist_v3.csv"
MASTER  = ART / "CNT_Master_Sheet_v3.csv"

# --- Helpers ---
def read_csv_first(*paths, **kw):
    for p in paths:
        try:
            if p and Path(p).exists():
                return pd.read_csv(p, **kw)
        except Exception:
            pass
    return None

def coerce_numeric(df, cols):
    for c in cols:
        if c in df.columns:
            df[c] = pd.to_numeric(df[c], errors="coerce")
    return df

def soft_badges(row):
    b = []
    # If your upstream added badge columns, keep them; else derive lightly
    if "badges" in row and isinstance(row["badges"], str) and row["badges"].strip():
        return row["badges"]
    if "driver" in row:
        if row["driver"] == "E": b.append("E★")
        if row["driver"] == "I": b.append("I★")
        if row["driver"] == "C": b.append("C★")
    # Light G/O heuristics if signals present
    if "G" in row and pd.notna(row["G"]) and row["G"] > 0.03: b.append("G★")
    if "O" in row and pd.notna(row["O"]) and row["O"] > 0.6:  b.append("O★")
    return " ".join(b)

# --- Load inputs (runlist preferred, fallback to master sheet) ---
runlist = read_csv_first(RUNLIST, MASTER, low_memory=False)
if runlist is None or runlist.empty:
    raise RuntimeError("No runlist/master sheet found. Expected one of:\n - "
                       f"{RUNLIST}\n - {MASTER}")

# Normalize expected columns
expected = ["dataset","kind","driver","priority_rank","Composite","packet","G","O"]
for c in expected:
    if c not in runlist.columns:
        runlist[c] = np.nan

runlist = coerce_numeric(runlist, ["priority_rank","Composite","G","O"]).copy()

# Build a simple verdict table
verdict_cols = ["dataset","kind","driver","priority_rank","Composite","packet","G","O"]
verdict = runlist[verdict_cols].copy()
verdict["badges"] = verdict.apply(soft_badges, axis=1)

# Sort: (higher Composite first, then lower priority_rank)
verdict = verdict.sort_values(
    by=["Composite", "priority_rank"],
    ascending=[False, True],
    na_position="last"
).reset_index(drop=True)

# --- Save CSV ---
VERDICT_CSV = OUT / "mega_verdict_v1.csv"
verdict.to_csv(VERDICT_CSV, index=False)

# --- Human summary (FIXED: triple-quoted string, no unterminated literals) ---
now = dt.datetime.now().strftime("%Y-%m-%d %H:%M:%S")
top5 = verdict.head(5)[["dataset","Composite","priority_rank","badges"]]

summary_txt = textwrap.dedent(f"""\
    == CNT Five-Pillar Mega Verdict (v1) ==
    Timestamp : {now}
    Root      : {ROOT}
    Out       : {OUT}

    Datasets considered : {len(verdict)}
    Kinds present       : {runlist.get('kind','').dropna().unique().tolist() if 'kind' in runlist else []}
    Drivers present     : {runlist.get('driver','').dropna().unique().tolist() if 'driver' in runlist else []}

    -- Top 5 by Composite --
    {top5.to_string(index=False)}
""")

SUMMARY_TXT = OUT / "mega_summary_v1.txt"
with open(SUMMARY_TXT, "w", encoding="utf-8") as f:
    f.write(summary_txt)

# --- Also emit a tiny JSON manifest for downstream tools ---
manifest = {
    "generated_at": now,
    "root": str(ROOT),
    "out": str(OUT),
    "inputs": {
        "runlist": str(RUNLIST) if RUNLIST.exists() else None,
        "master":  str(MASTER)  if MASTER.exists()  else None
    },
    "outputs": {
        "verdict_csv": str(VERDICT_CSV),
        "summary_txt": str(SUMMARY_TXT)
    },
    "counts": {
        "rows": int(len(verdict)),
        "top5": int(min(5, len(verdict)))
    }
}
with open(OUT / "mega_manifest_v1.json", "w", encoding="utf-8") as f:
    json.dump(manifest, f, indent=2)

print("[ok] Mega v1.1 complete")
print(" -", VERDICT_CSV)
print(" -", SUMMARY_TXT)
print(" -", OUT / "mega_manifest_v1.json")


[ok] Mega v1.1 complete
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\mega_verdict_v1.csv
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\mega_summary_v1.txt
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\mega_manifest_v1.json


In [27]:
# == Phase-V mini-harness (Top-5 real + Top-2 synth) ==
import os, json, math, time, numpy as np, pandas as pd
from pathlib import Path

# --------- IO ----------
ROOT = Path(r"/mnt/data")  # change to your run root if needed
VERDICT = ROOT / "mega_verdict_v1.csv"
MANIFEST = ROOT / "mega_manifest_v1.json"
OUTDIR = ROOT / "phaseV_results"
OUTDIR.mkdir(exist_ok=True, parents=True)
OUTCSV = OUTDIR / "phaseV_results.csv"

def load_verdict():
    assert VERDICT.exists(), f"Missing {VERDICT}"
    df = pd.read_csv(VERDICT)
    if "priority_rank" not in df.columns:
        df["priority_rank"] = np.arange(1, len(df)+1)
    return df

def load_manifest():
    return json.load(open(MANIFEST)) if MANIFEST.exists() else {}

verdict = load_verdict()
manifest = load_manifest()

# Map dataset -> source (fallbacks)
def get_source_path(row):
    ds = row["dataset"]
    # prefer explicit "source" column if present
    if "source" in row and isinstance(row["source"], str) and row["source"]:
        return row["source"]
    # else try manifest
    m = manifest.get(ds, {}) if isinstance(manifest, dict) else {}
    if isinstance(m, dict) and "source" in m and m["source"]:
        return m["source"]
    # last resort: if dataset itself is a path
    return ds

# --------- helpers ----------
EPS = 1e-9

def ema(x, alpha=0.01):
    x = np.asarray(x, float)
    y = np.empty_like(x); y[:] = np.nan
    m = np.isfinite(x)
    if not m.any(): return y
    last = x[m][0]
    for i, xi in enumerate(x):
        if np.isfinite(xi):
            last = alpha*xi + (1-alpha)*last
        y[i] = last
    return y

def motion(v):
    v = np.asarray(v, float)
    if v.size < 2: return np.nan
    g = np.gradient(v)
    g = g[np.isfinite(g)]
    return float(np.mean(np.abs(g))) if g.size else np.nan

def safe_col(df, name, default=np.nan):
    return df[name].to_numpy() if name in df.columns else np.full(len(df), default, dtype=float)

def e_test(rfi, dH):
    # resonance with non-increasing entropy
    m = np.isfinite(rfi) & np.isfinite(dH)
    if not m.any(): return np.nan
    return float(np.mean((rfi[m] > 0.85) & (dH[m] <= 0)))

def i_score(H, C):
    # free energy proxy: H - λC
    Cmed = np.nanmedian(C)
    lam = (np.nanmedian(H)/max(Cmed,1e-9)) if np.isfinite(Cmed) else 1.0
    F = H - lam*C
    Fz = (F - np.nanmedian(F)) / (np.nanstd(F)+1e-9)
    mu = np.nanmean(Fz)
    if not np.isfinite(mu): return np.nan
    return 1.0 / (1.0 + math.exp(mu))

def c_test(C, H, I0=None, I1=None, n_perm=500, seed=123):
    # invariants drift slower than metrics?
    rng = np.random.default_rng(seed)
    C = np.asarray(C, float); H = np.asarray(H, float)
    if I0 is None: I0 = ema(C, alpha=0.01)
    if I1 is None: I1 = ema(H, alpha=0.01)
    inv_m = np.nansum([motion(I0), motion(I1)])
    metr_m = np.nansum([motion(C),  motion(H)])
    ratio = np.nan
    if np.isfinite(inv_m) and np.isfinite(metr_m) and metr_m > 0:
        ratio = inv_m / (metr_m + EPS)
    # one-sided permutation test: T = metr_m - inv_m; want large positive T
    T_obs = (metr_m - inv_m) if (np.isfinite(inv_m) and np.isfinite(metr_m)) else np.nan
    if not np.isfinite(T_obs): 
        return dict(ratio=np.nan, T=np.nan, p=np.nan)
    # shuffle invariant series (preserves metric)
    def perm_once(v):
        v = np.asarray(v, float).copy()
        finite = np.isfinite(v)
        shuf = v[finite].copy()
        rng.shuffle(shuf)
        v[finite] = shuf
        return v
    ge = 0
    for _ in range(n_perm):
        I0p = perm_once(I0)
        I1p = perm_once(I1)
        inv_mp = np.nansum([motion(I0p), motion(I1p)])
        Tp = metr_m - inv_mp
        if Tp >= T_obs - 1e-12:
            ge += 1
    p = (ge + 1) / (n_perm + 1)
    return dict(ratio=ratio, T=T_obs, p=p)

def o_score(policy_rate):
    if not np.isfinite(policy_rate): return np.nan
    pr = float(policy_rate)
    # Gaussian sweet spot around 5% with sigma=5%
    return math.exp(-((pr - 0.05)**2)/(2*0.05**2))

def best_o():
    choices = [0.01, 0.03, 0.05, 0.10]
    sc = [(p, o_score(p)) for p in choices]
    sc.sort(key=lambda x: x[1], reverse=True)
    return sc[0]  # (p, score)

def synth_ablation(df):
    # Try a phase/row shuffle to see signal drop; report ΔRFI_mean
    rfi = safe_col(df, "RFI")
    if np.isfinite(rfi).sum() < 10:
        return dict(delta_RFI_mean=np.nan)
    base = float(np.nanmean(rfi))
    # Prefer shuffling a "phase" column if it exists; else row-shuffle rfi
    if "phase" in df.columns:
        ph = df["phase"].to_numpy()
        idx = np.arange(len(ph))
        np.random.default_rng(0).shuffle(idx)
        rfi_shuf = rfi[idx]
    else:
        rfi_shuf = rfi.copy()
        np.random.default_rng(0).shuffle(rfi_shuf)
    shuf_mean = float(np.nanmean(rfi_shuf))
    return dict(delta_RFI_mean=base - shuf_mean)

# --------- selection ----------
real = verdict[verdict["kind"]=="real"].copy() if "kind" in verdict.columns else verdict.copy()
real = real.sort_values(["priority_rank","Composite"], ascending=[True, False]).head(5)

synth = verdict[verdict["kind"]=="synth"].copy() if "kind" in verdict.columns else verdict.iloc[0:0].copy()
synth = synth.sort_values("Composite", ascending=False).head(2)

sel = pd.concat([real, synth], ignore_index=True)
print(f"[select] {len(real)} real + {len(synth)} synth -> {len(sel)} total")

# --------- run ----------
rows = []
for i, r in sel.iterrows():
    ds = r["dataset"]
    src = get_source_path(r)
    kind = r.get("kind","")
    driver = r.get("driver","")
    comp = r.get("Composite", np.nan)
    prio = r.get("priority_rank", np.nan)
    badges = r.get("badges","")
    print(f" -> [{i+1}/{len(sel)}] {ds} ({kind})")
    if not src or not os.path.exists(src):
        print("    [skip] source missing:", src)
        rows.append(dict(dataset=ds, kind=kind, driver=driver, priority_rank=prio,
                         Composite=comp, badges=badges, source=src,
                         E=np.nan, I=np.nan, C_ratio=np.nan, C_T=np.nan, C_p=np.nan,
                         O=np.nan, O_best=np.nan, O_best_p=np.nan,
                         synth_delta_RFI_mean=np.nan, status="missing"))
        continue
    try:
        df = pd.read_csv(src, low_memory=False)
    except Exception as e:
        print("    [skip] read error:", e)
        rows.append(dict(dataset=ds, kind=kind, driver=driver, priority_rank=prio,
                         Composite=comp, badges=badges, source=src,
                         E=np.nan, I=np.nan, C_ratio=np.nan, C_T=np.nan, C_p=np.nan,
                         O=np.nan, O_best=np.nan, O_best_p=np.nan,
                         synth_delta_RFI_mean=np.nan, status=f"read_error:{e}"))
        continue

    # columns
    RFI = safe_col(df, "RFI")
    dH  = safe_col(df, "dH")
    C   = safe_col(df, "C")
    H   = safe_col(df, "H")
    I0  = df["I_beta0"].to_numpy() if "I_beta0" in df.columns else None
    I1  = df["I_beta1"].to_numpy() if "I_beta1" in df.columns else None

    # tests
    Et = e_test(RFI, dH)
    It = i_score(H, C)
    Ct = c_test(C, H, I0, I1, n_perm=500, seed=42)

    # O fill
    O_val = r.get("O", np.nan)
    O_sc = o_score(O_val) if isinstance(O_val, (float,int)) else np.nan
    if not np.isfinite(O_sc):
        p_best, O_best = best_o()
    else:
        p_best, O_best = (float(O_val), float(O_sc))

    # synth ablation if synth
    ab = synth_ablation(df) if str(kind)=="synth" else dict(delta_RFI_mean=np.nan)

    rows.append(dict(dataset=ds, kind=kind, driver=driver, priority_rank=prio,
                     Composite=comp, badges=badges, source=src,
                     E=Et, I=It,
                     C_ratio=Ct["ratio"], C_T=Ct["T"], C_p=Ct["p"],
                     O=O_sc, O_best=O_best, O_best_p=p_best,
                     synth_delta_RFI_mean=ab["delta_RFI_mean"],
                     status="ok"))

res = pd.DataFrame(rows)
res = res.sort_values(["kind","priority_rank","Composite"], ascending=[True,True,False])

res.to_csv(OUTCSV, index=False)
print("\n[write]", OUTCSV, f"({res.shape[0]} rows)")

# also dump per-dataset JSON for quick diffs
PJSON = OUTDIR / "per_dataset"
PJSON.mkdir(exist_ok=True)
for _, rr in res.iterrows():
    slug = rr["dataset"].replace(os.sep,"__").replace(" ","_").replace(":","")
    with open(PJSON / f"{slug}.json", "w") as f:
        json.dump({k:(None if (isinstance(v,float) and not np.isfinite(v)) else v) for k,v in rr.items()}, f, indent=2)

print("[ok] Phase-V complete.")


AssertionError: Missing \mnt\data\mega_verdict_v1.csv

In [28]:
# == Phase-V mini-harness (auto-locate + robust paths) ==
import os, json, math, time, numpy as np, pandas as pd
from pathlib import Path

# -------- user-tweak knobs --------
USE_ALL = False        # set True to run all rows in the verdict
N_REAL  = 5            # top-N real by priority_rank (then Composite)
N_SYNTH = 2            # top-N synth by Composite
N_PERM  = 500          # permutations for C-test
SEED    = 42

# Optional manual overrides (paste full paths if auto-locate fails)
OVERRIDE_VERDICT  = None  # e.g., r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\mega_verdict_v1.csv"
OVERRIDE_MANIFEST = None  # e.g., r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\mega_manifest_v1.json"

# -------- likely roots to search --------
LIKELY_ROOTS = [
    Path("/mnt/data"),
    Path.cwd(),
    Path.cwd() / "packets_v3",
    Path.home(),
    Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars"),
    Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3"),
]

def _first_existing(paths):
    for p in paths:
        try:
            if p and Path(p).exists():
                return Path(p)
        except Exception:
            pass
    return None

def locate(name, extra_roots=()):
    # direct hits
    candidates = []
    for R in list(extra_roots) + LIKELY_ROOTS:
        candidates += [
            Path(R) / name,
            Path(R) / "packets_v3" / name,
            Path(R) / "cnt_five_pillars" / name,
        ]
    hit = _first_existing(candidates)
    if hit:
        return hit
    # bounded rglob under modest roots
    for R in list(extra_roots) + LIKELY_ROOTS:
        R = Path(R)
        if R.exists() and R.is_dir():
            try:
                # limit breadth by immediate subdirs
                for sub in [R] + [p for p in R.iterdir() if p.is_dir()]:
                    hits = list(sub.rglob(name))
                    if hits:
                        return hits[0]
            except Exception:
                continue
    return None

# -------- IO locate --------
VERDICT = Path(OVERRIDE_VERDICT) if OVERRIDE_VERDICT else locate("mega_verdict_v1.csv")
MANIFEST= Path(OVERRIDE_MANIFEST) if OVERRIDE_MANIFEST else locate("mega_manifest_v1.json")

if not VERDICT or not VERDICT.exists():
    raise FileNotFoundError(
        "Could not locate 'mega_verdict_v1.csv'. "
        "Set OVERRIDE_VERDICT to its full path."
    )

if not MANIFEST or not MANIFEST.exists():
    print("[warn] mega_manifest_v1.json not found; proceeding without it.")
    MANIFEST = None

OUTDIR = (VERDICT.parent / "phaseV_results")
OUTDIR.mkdir(exist_ok=True, parents=True)
OUTCSV = OUTDIR / "phaseV_results.csv"

def load_verdict(fp):
    df = pd.read_csv(fp)
    if "priority_rank" not in df.columns:
        df["priority_rank"] = np.arange(1, len(df)+1)
    # normalize types
    for col in ("Composite","priority_rank"):
        if col in df.columns:
            df[col] = pd.to_numeric(df[col], errors="coerce")
    return df

def load_manifest(fp):
    if not fp: return {}
    try:
        return json.load(open(fp, "r"))
    except Exception:
        return {}

verdict = load_verdict(VERDICT)
manifest = load_manifest(MANIFEST)

# Map dataset -> source path
def get_source_path(row):
    ds = row.get("dataset","")
    # prefer explicit 'source' column
    src = row.get("source", "")
    if isinstance(src, str) and src.strip():
        return src
    # else manifest
    m = manifest.get(ds, {}) if isinstance(manifest, dict) else {}
    if isinstance(m, dict):
        src2 = m.get("source","") or m.get("file","")
        if isinstance(src2, str) and src2.strip():
            return src2
    # last resort: dataset field itself (sometimes a pathy string)
    return ds

# -------- helpers --------
EPS = 1e-9

def ema(x, alpha=0.01):
    x = np.asarray(x, float)
    y = np.empty_like(x); y[:] = np.nan
    m = np.isfinite(x)
    if not m.any(): return y
    last = x[m][0]
    for i, xi in enumerate(x):
        if np.isfinite(xi):
            last = alpha*xi + (1-alpha)*last
        y[i] = last
    return y

def motion(v):
    v = np.asarray(v, float)
    if v.size < 2: return np.nan
    g = np.gradient(v)
    g = g[np.isfinite(g)]
    return float(np.mean(np.abs(g))) if g.size else np.nan

def safe_col(df, name, default=np.nan):
    return df[name].to_numpy() if name in df.columns else np.full(len(df), default, dtype=float)

def e_test(rfi, dH):
    m = np.isfinite(rfi) & np.isfinite(dH)
    if not m.any(): return np.nan
    return float(np.mean((rfi[m] > 0.85) & (dH[m] <= 0)))

def i_score(H, C):
    Cmed = np.nanmedian(C)
    lam = (np.nanmedian(H)/max(Cmed,1e-9)) if np.isfinite(Cmed) else 1.0
    F = H - lam*C
    Fz = (F - np.nanmedian(F)) / (np.nanstd(F)+1e-9)
    mu = np.nanmean(Fz)
    return 1.0 / (1.0 + math.exp(mu)) if np.isfinite(mu) else np.nan

def c_test(C, H, I0=None, I1=None, n_perm=N_PERM, seed=SEED):
    rng = np.random.default_rng(seed)
    C = np.asarray(C, float); H = np.asarray(H, float)
    if I0 is None: I0 = ema(C, alpha=0.01)
    if I1 is None: I1 = ema(H, alpha=0.01)
    inv_m = np.nansum([motion(I0), motion(I1)])
    metr_m = np.nansum([motion(C),  motion(H)])
    ratio = np.nan
    if np.isfinite(inv_m) and np.isfinite(metr_m) and metr_m > 0:
        ratio = inv_m / (metr_m + EPS)
    T_obs = (metr_m - inv_m) if (np.isfinite(inv_m) and np.isfinite(metr_m)) else np.nan
    if not np.isfinite(T_obs):
        return dict(ratio=np.nan, T=np.nan, p=np.nan)
    def perm_once(v):
        v = np.asarray(v, float).copy()
        finite = np.isfinite(v)
        shuf = v[finite].copy()
        rng.shuffle(shuf)
        v[finite] = shuf
        return v
    ge = 0
    for _ in range(n_perm):
        I0p = perm_once(I0)
        I1p = perm_once(I1)
        inv_mp = np.nansum([motion(I0p), motion(I1p)])
        Tp = metr_m - inv_mp
        if Tp >= T_obs - 1e-12:
            ge += 1
    p = (ge + 1) / (n_perm + 1)
    return dict(ratio=ratio, T=T_obs, p=p)

def o_score(policy_rate):
    if not np.isfinite(policy_rate): return np.nan
    pr = float(policy_rate)
    return math.exp(-((pr - 0.05)**2)/(2*0.05**2))

def best_o():
    choices = [0.01, 0.03, 0.05, 0.10]
    sc = [(p, o_score(p)) for p in choices]
    sc.sort(key=lambda x: x[1], reverse=True)
    return sc[0]  # (p, score)

def synth_ablation(df):
    rfi = safe_col(df, "RFI")
    if np.isfinite(rfi).sum() < 10:
        return dict(delta_RFI_mean=np.nan)
    base = float(np.nanmean(rfi))
    if "phase" in df.columns:
        ph = df["phase"].to_numpy()
        idx = np.arange(len(ph))
        np.random.default_rng(0).shuffle(idx)
        rfi_shuf = rfi[idx]
    else:
        rfi_shuf = rfi.copy()
        np.random.default_rng(0).shuffle(rfi_shuf)
    shuf_mean = float(np.nanmean(rfi_shuf))
    return dict(delta_RFI_mean=base - shuf_mean)

# -------- selection --------
dfv = verdict.copy()
if USE_ALL:
    sel = dfv.copy()
else:
    real  = dfv[dfv.get("kind","real").eq("real")].sort_values(
        ["priority_rank","Composite"], ascending=[True, False]).head(N_REAL)
    synth = dfv[dfv.get("kind","").eq("synth")].sort_values(
        "Composite", ascending=False).head(N_SYNTH)
    sel = pd.concat([real, synth], ignore_index=True)

print(f"[select] real={sum(sel.get('kind','').eq('real'))} synth={sum(sel.get('kind','').eq('synth'))} total={len(sel)}")

# -------- run --------
rows = []
for i, r in sel.iterrows():
    ds = r.get("dataset","")
    src = get_source_path(r)
    kind = r.get("kind","")
    driver = r.get("driver","")
    comp = r.get("Composite", np.nan)
    prio = r.get("priority_rank", np.nan)
    badges = r.get("badges","")
    print(f" -> [{i+1}/{len(sel)}] {ds} ({kind})")
    if not src or not os.path.exists(src):
        print("    [skip] source missing:", src)
        rows.append(dict(dataset=ds, kind=kind, driver=driver, priority_rank=prio,
                         Composite=comp, badges=badges, source=src,
                         E=np.nan, I=np.nan, C_ratio=np.nan, C_T=np.nan, C_p=np.nan,
                         O=np.nan, O_best=np.nan, O_best_p=np.nan,
                         synth_delta_RFI_mean=np.nan, status="missing"))
        continue
    try:
        df = pd.read_csv(src, low_memory=False)
    except Exception as e:
        print("    [skip] read error:", e)
        rows.append(dict(dataset=ds, kind=kind, driver=driver, priority_rank=prio,
                         Composite=comp, badges=badges, source=src,
                         E=np.nan, I=np.nan, C_ratio=np.nan, C_T=np.nan, C_p=np.nan,
                         O=np.nan, O_best=np.nan, O_best_p=np.nan,
                         synth_delta_RFI_mean=np.nan, status=f"read_error:{e}"))
        continue

    RFI = safe_col(df, "RFI")
    dH  = safe_col(df, "dH")
    C   = safe_col(df, "C")
    H   = safe_col(df, "H")
    I0  = df["I_beta0"].to_numpy() if "I_beta0" in df.columns else None
    I1  = df["I_beta1"].to_numpy() if "I_beta1" in df.columns else None

    Et = e_test(RFI, dH)
    It = i_score(H, C)
    Ct = c_test(C, H, I0, I1, n_perm=N_PERM, seed=SEED)

    O_val = r.get("O", np.nan)
    O_sc = o_score(O_val) if isinstance(O_val, (float, int)) else np.nan
    if not np.isfinite(O_sc):
        p_best, O_best = best_o()
    else:
        p_best, O_best = (float(O_val), float(O_sc))

    ab = synth_ablation(df) if str(kind)=="synth" else dict(delta_RFI_mean=np.nan)

    rows.append(dict(dataset=ds, kind=kind, driver=driver, priority_rank=float(prio) if pd.notna(prio) else np.nan,
                     Composite=float(comp) if pd.notna(comp) else np.nan, badges=badges, source=src,
                     E=Et, I=It,
                     C_ratio=Ct["ratio"], C_T=Ct["T"], C_p=Ct["p"],
                     O=O_sc, O_best=O_best, O_best_p=p_best,
                     synth_delta_RFI_mean=ab["delta_RFI_mean"],
                     status="ok"))

res = pd.DataFrame(rows)
res = res.sort_values(["kind","priority_rank","Composite"], ascending=[True, True, False])

# -------- write outputs --------
res.to_csv(OUTCSV, index=False)
print("\n[write]", OUTCSV, f"({res.shape[0]} rows)")

PJSON = OUTDIR / "per_dataset"
PJSON.mkdir(exist_ok=True)
for _, rr in res.iterrows():
    slug = str(rr["dataset"]).replace("\\","__").replace("/","__").replace(" ","_").replace(":","")
    with open(PJSON / f"{slug}.json", "w") as f:
        json.dump({k:(None if (isinstance(v,float) and not np.isfinite(v)) else v) for k,v in rr.items()}, f, indent=2)

print("[ok] Phase-V complete.")


[select] real=5 synth=2 total=7
 -> [1/7] artifacts__tables__genome3d__atlas__nodes_v1h_realhic__20251009-020445.parquet (real)
    [skip] source missing: artifacts__tables__genome3d__atlas__nodes_v1h_realhic__20251009-020445.parquet
 -> [2/7] artifacts__tables__genome3d__atlas__genes_v1__20251008-214043.parquet (real)
    [skip] source missing: artifacts__tables__genome3d__atlas__genes_v1__20251008-214043.parquet
 -> [3/7] artifacts__tables__migrated__gdf-snapshot__d8dc9743.csv (real)
    [skip] source missing: artifacts__tables__migrated__gdf-snapshot__d8dc9743.csv
 -> [4/7] artifacts__tables__genome3d__atlas__nodes_v1h__20251008-215623.parquet (real)
    [skip] source missing: artifacts__tables__genome3d__atlas__nodes_v1h__20251008-215623.parquet
 -> [5/7] artifacts__tables__genome3d__atlas__nodes_v0c__20251008-213724.parquet (real)
    [skip] source missing: artifacts__tables__genome3d__atlas__nodes_v0c__20251008-213724.parquet
 -> [6/7] artifacts__tables__migrated__sim-theta__fc53

In [29]:
# == Phase-V++ : robust source resolver + run ==
import os, json, math, time, numpy as np, pandas as pd
from pathlib import Path

# -------- knobs you may tweak --------
USE_ALL = False        # True => run all rows in the verdict
N_REAL  = 5            # top-N real by priority_rank (then Composite)
N_SYNTH = 2            # top-N synth by Composite
N_PERM  = 500          # permutations for C-test
SEED    = 42

# Optional explicit paths if auto-locate fails
OVERRIDE_VERDICT  = None  # e.g., r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\mega_verdict_v1.csv"
OVERRIDE_MANIFEST = None  # e.g., r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3\mega_manifest_v1.json"

# -------- likely roots to search --------
LIKELY_ROOTS = [
    Path("/mnt/data"),
    Path.cwd(),
    Path.cwd() / "packets_v3",
    Path.home(),
    Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars"),
    Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3"),
]

def _first_existing(paths):
    for p in paths:
        try:
            if p and Path(p).exists():
                return Path(p)
        except Exception:
            pass
    return None

def locate(name, extra_roots=()):
    cands = []
    for R in list(extra_roots) + LIKELY_ROOTS:
        R = Path(R)
        cands += [R/name, R/"packets_v3"/name, R/"cnt_five_pillars"/name]
    hit = _first_existing(cands)
    if hit: return hit
    # shallow rglob
    for R in list(extra_roots) + LIKELY_ROOTS:
        R = Path(R)
        if R.exists() and R.is_dir():
            try:
                for sub in [R] + [p for p in R.iterdir() if p.is_dir()]:
                    hits = list(sub.rglob(name))
                    if hits: return hits[0]
            except Exception:
                continue
    return None

VERDICT  = Path(OVERRIDE_VERDICT)  if OVERRIDE_VERDICT  else locate("mega_verdict_v1.csv")
MANIFEST = Path(OVERRIDE_MANIFEST) if OVERRIDE_MANIFEST else locate("mega_manifest_v1.json")

if not VERDICT or not VERDICT.exists():
    raise FileNotFoundError("Could not locate 'mega_verdict_v1.csv'. Set OVERRIDE_VERDICT to its full path.")

if not MANIFEST or not MANIFEST.exists():
    print("[warn] mega_manifest_v1.json not found; proceeding without it.")
    MANIFEST = None

OUTDIR = (VERDICT.parent / "phaseV_results")
OUTDIR.mkdir(exist_ok=True, parents=True)
OUTCSV = OUTDIR / "phaseV_results.csv"

# ---------- load verdict / manifest ----------
def load_verdict(fp):
    df = pd.read_csv(fp)
    if "priority_rank" not in df.columns:
        df["priority_rank"] = np.arange(1, len(df)+1)
    for col in ("Composite","priority_rank"):
        if col in df.columns:
            df[col] = pd.to_numeric(df[col], errors="coerce")
    return df

def _flatten_json_to_pairs(obj, out):
    # collect (dataset, source) pairs from arbitrary JSON shapes
    if isinstance(obj, dict):
        keys = {k.lower(): k for k in obj.keys()}
        # try common field names
        ds_key = next((keys[k] for k in ["dataset","name","id","key"] if k in keys), None)
        src_key= next((keys[k] for k in ["source","file","path","features","input"] if k in keys), None)
        if ds_key and src_key and isinstance(obj[ds_key], str) and isinstance(obj[src_key], str):
            out.append((obj[ds_key], obj[src_key]))
        for v in obj.values():
            _flatten_json_to_pairs(v, out)
    elif isinstance(obj, list):
        for v in obj:
            _flatten_json_to_pairs(v, out)

def load_manifest_map(fp):
    if not fp: return {}
    try:
        data = json.load(open(fp, "r", encoding="utf-8"))
    except Exception:
        return {}
    pairs = []
    if isinstance(data, dict) and all(isinstance(v, dict) for v in data.values()):
        # dict keyed by dataset -> {source: ...}
        for k,v in data.items():
            src = v.get("source") or v.get("file") or v.get("path") or v.get("features")
            if isinstance(src, str) and src.strip():
                pairs.append((k, src))
    else:
        _flatten_json_to_pairs(data, pairs)
    # normalize to map (exact + slug)
    m = {}
    for ds, src in pairs:
        ds = str(ds)
        m[ds] = src
        m[ds.replace("\\","/")] = src
        m[ds.replace("/","\\")] = src
        m[ds.strip()] = src
        m[ds.strip().replace("\\","__").replace("/","__")] = src
    return m

verdict  = load_verdict(VERDICT)
mani_map = load_manifest_map(MANIFEST)

# ---------- path heuristics for features__ mirrors ----------
def slugify_dataset(ds: str) -> str:
    return str(ds).strip().replace("\\","__").replace("/","__")

def candidate_feature_paths(ds: str):
    slug = slugify_dataset(ds)
    names = [
        f"features__{slug}.csv",
        f"features__{slug}.csv.csv",
        f"features__{slug}.parquet.csv",
    ]
    roots = []
    # prioritize next to verdict and common lab dirs
    roots += [VERDICT.parent, VERDICT.parent.parent]
    roots += [Path(r) for r in [
        r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars",
        r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\packets_v3",
        r"C:\Users\caleb\CNT_Lab\artifacts",
    ] if os.path.exists(r)]
    roots += LIKELY_ROOTS
    # include 'features__' subfolder style
    paths = []
    for R in roots:
        for nm in names:
            paths += [Path(R)/nm, Path(R)/"features__"/nm]
    return paths

def resolve_source_for_dataset(ds: str, row_source: str = "") -> str:
    # 1) explicit row source
    if isinstance(row_source, str) and row_source.strip() and os.path.exists(row_source):
        return row_source
    # 2) manifest direct
    cand = mani_map.get(ds) or mani_map.get(ds.replace("\\","/")) or mani_map.get(slugify_dataset(ds))
    if isinstance(cand, str) and os.path.exists(cand):
        return cand
    # 3) heuristic features__ mirrors
    for p in candidate_feature_paths(ds):
        if os.path.exists(p):
            return str(p)
    # 4) shallow rglob for a close match
    slug = slugify_dataset(ds)
    for R in LIKELY_ROOTS:
        if R.exists():
            try:
                hits = list(R.glob(f"**/*{slug}*.csv"))
                hits = [h for h in hits if "features__" in str(h)]
                if hits:
                    return str(hits[0])
            except Exception:
                pass
    # last resort: give back the dataset (likely non-existent)
    return ds

# ---------- scoring helpers (same as before) ----------
EPS = 1e-9
def ema(x, alpha=0.01):
    x = np.asarray(x, float)
    y = np.empty_like(x); y[:] = np.nan
    m = np.isfinite(x)
    if not m.any(): return y
    last = x[m][0]
    for i, xi in enumerate(x):
        if np.isfinite(xi): last = alpha*xi + (1-alpha)*last
        y[i] = last
    return y

def motion(v):
    v = np.asarray(v, float)
    if v.size < 2: return np.nan
    g = np.gradient(v)
    g = g[np.isfinite(g)]
    return float(np.mean(np.abs(g))) if g.size else np.nan

def safe_col(df, name, default=np.nan):
    return df[name].to_numpy() if name in df.columns else np.full(len(df), default, dtype=float)

def e_test(rfi, dH):
    m = np.isfinite(rfi) & np.isfinite(dH)
    if not m.any(): return np.nan
    return float(np.mean((rfi[m] > 0.85) & (dH[m] <= 0)))

def i_score(H, C):
    Cmed = np.nanmedian(C)
    lam = (np.nanmedian(H)/max(Cmed,1e-9)) if np.isfinite(Cmed) else 1.0
    F = H - lam*C
    Fz = (F - np.nanmedian(F)) / (np.nanstd(F)+1e-9)
    mu = np.nanmean(Fz)
    return 1.0 / (1.0 + math.exp(mu)) if np.isfinite(mu) else np.nan

def c_test(C, H, I0=None, I1=None, n_perm=N_PERM, seed=SEED):
    rng = np.random.default_rng(seed)
    C = np.asarray(C, float); H = np.asarray(H, float)
    if I0 is None: I0 = ema(C, alpha=0.01)
    if I1 is None: I1 = ema(H, alpha=0.01)
    inv_m = np.nansum([motion(I0), motion(I1)])
    metr_m = np.nansum([motion(C),  motion(H)])
    ratio = np.nan
    if np.isfinite(inv_m) and np.isfinite(metr_m) and metr_m > 0:
        ratio = inv_m / (metr_m + EPS)
    T_obs = (metr_m - inv_m) if (np.isfinite(inv_m) and np.isfinite(metr_m)) else np.nan
    if not np.isfinite(T_obs):
        return dict(ratio=np.nan, T=np.nan, p=np.nan)
    def perm_once(v):
        v = np.asarray(v, float).copy()
        finite = np.isfinite(v)
        shuf = v[finite].copy()
        rng.shuffle(shuf)
        v[finite] = shuf
        return v
    ge = 0
    for _ in range(n_perm):
        I0p = perm_once(I0)
        I1p = perm_once(I1)
        inv_mp = np.nansum([motion(I0p), motion(I1p)])
        Tp = metr_m - inv_mp
        if Tp >= T_obs - 1e-12:
            ge += 1
    p = (ge + 1) / (n_perm + 1)
    return dict(ratio=ratio, T=T_obs, p=p)

def o_score(policy_rate):
    if not np.isfinite(policy_rate): return np.nan
    pr = float(policy_rate)
    return math.exp(-((pr - 0.05)**2)/(2*0.05**2))

def best_o():
    choices = [0.01, 0.03, 0.05, 0.10]
    sc = [(p, o_score(p)) for p in choices]
    sc.sort(key=lambda x: x[1], reverse=True)
    return sc[0]  # (p, score)

def synth_ablation(df):
    rfi = safe_col(df, "RFI")
    if np.isfinite(rfi).sum() < 10:
        return dict(delta_RFI_mean=np.nan)
    base = float(np.nanmean(rfi))
    if "phase" in df.columns:
        ph = df["phase"].to_numpy()
        idx = np.arange(len(ph))
        np.random.default_rng(0).shuffle(idx)
        rfi_shuf = rfi[idx]
    else:
        rfi_shuf = rfi.copy()
        np.random.default_rng(0).shuffle(rfi_shuf)
    shuf_mean = float(np.nanmean(rfi_shuf))
    return dict(delta_RFI_mean=base - shuf_mean)

# ---------- select subset ----------
dfv = verdict.copy()

# Pre-resolve sources into a column so we can inspect what matched
resolved_sources = []
for _, r in dfv.iterrows():
    resolved_sources.append(
        resolve_source_for_dataset(
            r.get("dataset",""),
            r.get("source","") if "source" in dfv.columns else ""
        )
    )
dfv["source_resolved"] = resolved_sources

# Show a quick match summary
matched = sum(os.path.exists(s) for s in dfv["source_resolved"])
print(f"[resolve] matched sources: {matched} / {len(dfv)}")

if USE_ALL:
    sel = dfv.copy()
else:
    real  = dfv[dfv.get("kind","real").eq("real")].sort_values(
        ["priority_rank","Composite"], ascending=[True, False]).head(N_REAL)
    synth = dfv[dfv.get("kind","").eq("synth")].sort_values(
        "Composite", ascending=False).head(N_SYNTH)
    sel = pd.concat([real, synth], ignore_index=True)

print(f"[select] real={sum(sel.get('kind','').eq('real'))} synth={sum(sel.get('kind','').eq('synth'))} total={len(sel)}")

# ---------- run ----------
rows = []
for i, r in sel.iterrows():
    ds = r.get("dataset","")
    src = r.get("source_resolved","") or r.get("source","") or ds
    kind = r.get("kind","")
    driver = r.get("driver","")
    comp = r.get("Composite", np.nan)
    prio = r.get("priority_rank", np.nan)
    badges = r.get("badges","")
    print(f" -> [{i+1}/{len(sel)}] {ds} ({kind})")
    if not src or not os.path.exists(src):
        print("    [skip] source missing:", src)
        rows.append(dict(dataset=ds, kind=kind, driver=driver, priority_rank=prio,
                         Composite=comp, badges=badges, source=src,
                         E=np.nan, I=np.nan, C_ratio=np.nan, C_T=np.nan, C_p=np.nan,
                         O=np.nan, O_best=np.nan, O_best_p=np.nan,
                         synth_delta_RFI_mean=np.nan, status="missing"))
        continue
    try:
        df = pd.read_csv(src, low_memory=False)
    except Exception as e:
        print("    [skip] read error:", e)
        rows.append(dict(dataset=ds, kind=kind, driver=driver, priority_rank=prio,
                         Composite=comp, badges=badges, source=src,
                         E=np.nan, I=np.nan, C_ratio=np.nan, C_T=np.nan, C_p=np.nan,
                         O=np.nan, O_best=np.nan, O_best_p=np.nan,
                         synth_delta_RFI_mean=np.nan, status=f"read_error:{e}"))
        continue

    RFI = safe_col(df, "RFI")
    dH  = safe_col(df, "dH")
    C   = safe_col(df, "C")
    H   = safe_col(df, "H")
    I0  = df["I_beta0"].to_numpy() if "I_beta0" in df.columns else None
    I1  = df["I_beta1"].to_numpy() if "I_beta1" in df.columns else None

    Et = e_test(RFI, dH)
    It = i_score(H, C)
    Ct = c_test(C, H, I0, I1, n_perm=N_PERM, seed=SEED)

    O_val = r.get("O", np.nan)
    O_sc = o_score(O_val) if isinstance(O_val, (float, int)) else np.nan
    if not np.isfinite(O_sc):
        p_best, O_best = best_o()
    else:
        p_best, O_best = (float(O_val), float(O_sc))

    ab = synth_ablation(df) if str(kind)=="synth" else dict(delta_RFI_mean=np.nan)

    rows.append(dict(dataset=ds, kind=kind, driver=driver, priority_rank=float(prio) if pd.notna(prio) else np.nan,
                     Composite=float(comp) if pd.notna(comp) else np.nan, badges=badges, source=src,
                     E=Et, I=It,
                     C_ratio=Ct["ratio"], C_T=Ct["T"], C_p=Ct["p"],
                     O=O_sc, O_best=O_best, O_best_p=p_best,
                     synth_delta_RFI_mean=ab["delta_RFI_mean"],
                     status="ok"))

res = pd.DataFrame(rows).sort_values(["kind","priority_rank","Composite"], ascending=[True, True, False])

# ---------- write outputs ----------
res.to_csv(OUTCSV, index=False)
print("\n[write]", OUTCSV, f"({res.shape[0]} rows)")
PJSON = OUTDIR / "per_dataset"
PJSON.mkdir(exist_ok=True)
for _, rr in res.iterrows():
    slug = str(rr["dataset"]).replace("\\","__").replace("/","__").replace(" ","_").replace(":","")
    with open(PJSON / f"{slug}.json", "w", encoding="utf-8") as f:
        json.dump({k:(None if (isinstance(v,float) and not np.isfinite(v)) else v) for k,v in rr.items()}, f, indent=2)

print("[ok] Phase-V complete.")


[resolve] matched sources: 22 / 22
[select] real=5 synth=2 total=7
 -> [1/7] artifacts__tables__genome3d__atlas__nodes_v1h_realhic__20251009-020445.parquet (real)
 -> [2/7] artifacts__tables__genome3d__atlas__genes_v1__20251008-214043.parquet (real)
 -> [3/7] artifacts__tables__migrated__gdf-snapshot__d8dc9743.csv (real)
 -> [4/7] artifacts__tables__genome3d__atlas__nodes_v1h__20251008-215623.parquet (real)
 -> [5/7] artifacts__tables__genome3d__atlas__nodes_v0c__20251008-213724.parquet (real)
 -> [6/7] artifacts__tables__migrated__sim-theta__fc536f2f.csv (synth)
 -> [7/7] artifacts__tables__migrated__sim-alpha__f44f6f05.csv (synth)

[write] C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\phaseV_results.csv (7 rows)
[ok] Phase-V complete.


In [30]:
# == Phase-V Report Card (v1) ==
# Loads phaseV_results.csv, computes flags, emits a clean summary + picks.
import os, math, json, numpy as np, pandas as pd
from pathlib import Path

# --- knobs ---
CSV_HINT = r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\phaseV_results.csv"
THRESH = {
    "E_pass": 0.40,     # resonance with non-increasing entropy
    "I_pass": 0.50,     # free-energy score
    "C_sig":  0.05,     # permutation p-value for invariants steadiness (smaller=better)
    "C_strong_ratio": 0.80,  # invariants motion / metric motion (smaller=steadier invariants)
    "O_good": 0.80,     # O_best score (policy sweet spot proximity)
}

# --- locate results ---
def locate_phase_csv():
    cand = Path(CSV_HINT)
    if cand.exists(): return cand
    roots = [
        Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results"),
        Path.cwd(), Path.cwd()/ "phaseV_results",
    ]
    for R in roots:
        p = R/"phaseV_results.csv"
        if p.exists(): return p
    # breadth-first-ish scan (shallow)
    for R in roots:
        if R.exists():
            hits = list(R.rglob("phaseV_results.csv"))
            if hits: return hits[0]
    raise FileNotFoundError("phaseV_results.csv not found; update CSV_HINT if needed.")

CSV = locate_phase_csv()
df = pd.read_csv(CSV)

# --- tidy & flags ---
num = lambda s: pd.to_numeric(df.get(s, np.nan), errors="coerce")

df["priority_rank"] = num("priority_rank")
df["Composite"]     = num("Composite")
df["E"]             = num("E")
df["I"]             = num("I")
df["C_p"]           = num("C_p")
df["C_ratio"]       = num("C_ratio")
df["O"]             = num("O")
df["O_best"]        = num("O_best")
df["O_best_p"]      = num("O_best_p")

df["E_pass"]    = df["E"] >= THRESH["E_pass"]
df["I_pass"]    = df["I"] >= THRESH["I_pass"]
df["C_sig"]     = df["C_p"] <= THRESH["C_sig"]
df["C_strong"]  = df["C_ratio"] < THRESH["C_strong_ratio"]
df["O_sweet"]   = df["O_best"] >= THRESH["O_good"]

def tag_row(r):
    tags = []
    if r.get("E_pass"):   tags.append("E★")
    if r.get("I_pass"):   tags.append("I★")
    if r.get("C_sig"):    tags.append("C(p≤{:.2g})".format(THRESH["C_sig"]))
    if r.get("C_strong"): tags.append("Cratio<{:.2f}".format(THRESH["C_strong_ratio"]))
    if r.get("O_sweet"):  tags.append("O★")
    return " ".join(tags)

df["phaseV_tags"] = df.apply(tag_row, axis=1)

# Define a simple go/no-go for “real” items:
#   GO if (C_sig & C_strong) OR (E_pass & C_sig)
def go_flag(r):
    return bool( (r["C_sig"] and r["C_strong"]) or (r["E_pass"] and r["C_sig"]) )
df["GO"] = df.apply(go_flag, axis=1)

# --- pretty scorecard (sorted: real first, then by rank/Composite) ---
score_cols = [
    "dataset","kind","driver","priority_rank","Composite",
    "E","I","C_ratio","C_p","O_best","O_best_p","phaseV_tags","GO","status","source"
]
score = df.sort_values(
    by=["kind","priority_rank","Composite"],
    ascending=[True, True, False]
)[score_cols]

# --- Picks ---
real_picks  = score[(score["kind"]=="real")  & (score["GO"]==True)].copy()
synth_picks = score[(score["kind"]=="synth") & (score["C_sig"]==True)].copy()  # for synth prefer strict C

# --- write outputs next to the CSV ---
OUTDIR = Path(CSV).parent
REPORT_MD  = OUTDIR / "phaseV_report_v1.md"
REPORT_CSV = OUTDIR / "phaseV_report_v1.csv"
PICKS_CSV  = OUTDIR / "phaseV_picks_v1.csv"

score.to_csv(REPORT_CSV, index=False)
pd.concat(
    [real_picks.assign(bucket="real_pick"), synth_picks.assign(bucket="synth_pick")],
    ignore_index=True
).to_csv(PICKS_CSV, index=False)

with open(REPORT_MD, "w", encoding="utf-8") as f:
    f.write("# Phase-V Report (v1)\n\n")
    f.write(f"- Source: `{CSV}`\n")
    f.write(f"- Rows: {len(df)}\n")
    f.write(f"- Real GO picks: {len(real_picks)} | Synth C-sig picks: {len(synth_picks)}\n")
    f.write("\n## Thresholds\n")
    for k,v in THRESH.items():
        f.write(f"- {k} = {v}\n")
    f.write("\n## Real — GO Picks\n")
    if len(real_picks)==0:
        f.write("_(none)_\n")
    else:
        for _,r in real_picks.iterrows():
            f.write(f"- **{r['dataset']}**  rank={r['priority_rank']:.2f}  "
                    f"E={r['E']:.3f}  I={r['I']:.3f}  "
                    f"C_ratio={r['C_ratio']:.3f} (p={r['C_p']:.3g})  "
                    f"O*=({r['O_best_p']:.2%},{r['O_best']:.3f})  "
                    f"{r['phaseV_tags']}\n")
    f.write("\n## Synth — C-significant\n")
    if len(synth_picks)==0:
        f.write("_(none)_\n")
    else:
        for _,r in synth_picks.iterrows():
            f.write(f"- **{r['dataset']}**  E={r['E']:.3f}  I={r['I']:.3f}  "
                    f"C_ratio={r['C_ratio']:.3f} (p={r['C_p']:.3g})  {r['phaseV_tags']}\n")

print("[ok] Report:", REPORT_MD)
print("[ok] Scorecard CSV:", REPORT_CSV)
print("[ok] Picks CSV:", PICKS_CSV)

# Show top few rows inline for a quick glance
print("\n== Phase-V Scorecard (head) ==")
print(score.head(10).to_string(index=False))


KeyError: 'C_sig'

In [31]:
# == Phase-V Report Card (v1.1, fixed 'C_sig' selection) ==
import os, numpy as np, pandas as pd
from pathlib import Path

# --- knobs ---
CSV_HINT = r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\phaseV_results.csv"
THRESH = {
    "E_pass": 0.40,
    "I_pass": 0.50,
    "C_sig":  0.05,
    "C_strong_ratio": 0.80,
    "O_good": 0.80,
}

def locate_phase_csv():
    p = Path(CSV_HINT)
    if p.exists():
        return p
    roots = [
        Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results"),
        Path.cwd(), Path.cwd()/ "phaseV_results",
    ]
    for R in roots:
        q = R / "phaseV_results.csv"
        if q.exists(): return q
    for R in roots:
        if R.exists():
            hits = list(R.rglob("phaseV_results.csv"))
            if hits: return hits[0]
    raise FileNotFoundError("phaseV_results.csv not found; update CSV_HINT if needed.")

CSV = locate_phase_csv()
df = pd.read_csv(CSV)

# --- helpers ---
to_num = lambda s: pd.to_numeric(df.get(s, np.nan), errors="coerce")

# normalize columns
for col in ["priority_rank","Composite","E","I","C_p","C_ratio","O","O_best","O_best_p"]:
    df[col] = to_num(col)

# ensure optional text cols exist
if "status" not in df.columns: df["status"] = ""
if "source" not in df.columns: df["source"] = ""

# --- flags ---
df["E_pass"]    = df["E"] >= THRESH["E_pass"]
df["I_pass"]    = df["I"] >= THRESH["I_pass"]
df["C_sig"]     = df["C_p"] <= THRESH["C_sig"]
df["C_strong"]  = df["C_ratio"] < THRESH["C_strong_ratio"]
df["O_sweet"]   = df["O_best"] >= THRESH["O_good"]

def tag_row(r):
    tags = []
    if r["E_pass"]:    tags.append("E★")
    if r["I_pass"]:    tags.append("I★")
    if r["C_sig"]:     tags.append(f"C(p≤{THRESH['C_sig']:.2g})")
    if r["C_strong"]:  tags.append(f"Cratio<{THRESH['C_strong_ratio']:.2f}")
    if r["O_sweet"]:   tags.append("O★")
    return " ".join(tags)

df["phaseV_tags"] = df.apply(tag_row, axis=1)

# GO if (C_sig & C_strong) OR (E_pass & C_sig)
df["GO"] = (df["C_sig"] & df["C_strong"]) | (df["E_pass"] & df["C_sig"])

# --- scorecard (include C_sig/C_strong so later masks never KeyError) ---
score_cols = [
    "dataset","kind","driver","priority_rank","Composite",
    "E","I","C_ratio","C_p","C_sig","C_strong",
    "O_best","O_best_p","phaseV_tags","GO","status","source"
]
have = [c for c in score_cols if c in df.columns]  # guard against weird inputs

score = df.sort_values(
    by=["kind","priority_rank","Composite"],
    ascending=[True, True, False]
)[have]

# --- picks ---
real_picks  = score[(score["kind"]=="real")  & (score["GO"])].copy()
synth_picks = score[(score["kind"]=="synth") & (score["C_sig"])].copy()  # strict on C for synth

# --- write outputs ---
OUTDIR = Path(CSV).parent
REPORT_MD  = OUTDIR / "phaseV_report_v1.md"
REPORT_CSV = OUTDIR / "phaseV_report_v1.csv"
PICKS_CSV  = OUTDIR / "phaseV_picks_v1.csv"

score.to_csv(REPORT_CSV, index=False)
pd.concat(
    [real_picks.assign(bucket="real_pick"), synth_picks.assign(bucket="synth_pick")],
    ignore_index=True
).to_csv(PICKS_CSV, index=False)

def fmt(x, f): 
    return f.format(x) if pd.notna(x) else "NaN"

with open(REPORT_MD, "w", encoding="utf-8") as f:
    f.write("# Phase-V Report (v1.1)\n\n")
    f.write(f"- Source: `{CSV}`\n")
    f.write(f"- Rows: {len(df)}\n")
    f.write(f"- Real GO picks: {len(real_picks)} | Synth C-sig picks: {len(synth_picks)}\n")
    f.write("\n## Thresholds\n")
    for k,v in THRESH.items():
        f.write(f"- {k} = {v}\n")
    f.write("\n## Real — GO Picks\n")
    if real_picks.empty:
        f.write("_(none)_\n")
    else:
        for _,r in real_picks.iterrows():
            f.write(
                f"- **{r['dataset']}**  rank={fmt(r['priority_rank'],'{:.2f}')}  "
                f"E={fmt(r['E'],'{:.3f}')}  I={fmt(r['I'],'{:.3f}')}  "
                f"C_ratio={fmt(r['C_ratio'],'{:.3f}')} (p={fmt(r['C_p'],'{:.3g}')})  "
                f"O* p={fmt(r['O_best_p'],'{:.2%}')}, best={fmt(r['O_best'],'{:.3f}')}  "
                f"{r['phaseV_tags']}\n"
            )
    f.write("\n## Synth — C-significant\n")
    if synth_picks.empty:
        f.write("_(none)_\n")
    else:
        for _,r in synth_picks.iterrows():
            f.write(
                f"- **{r['dataset']}**  E={fmt(r['E'],'{:.3f}')}  I={fmt(r['I'],'{:.3f}')}  "
                f"C_ratio={fmt(r['C_ratio'],'{:.3f}')} (p={fmt(r['C_p'],'{:.3g}')})  "
                f"{r['phaseV_tags']}\n"
            )

print("[ok] Report:", REPORT_MD)
print("[ok] Scorecard CSV:", REPORT_CSV)
print("[ok] Picks CSV:", PICKS_CSV)
print("\n== Phase-V Scorecard (head) ==")
print(score.head(10).to_string(index=False))


[ok] Report: C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\phaseV_report_v1.md
[ok] Scorecard CSV: C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\phaseV_report_v1.csv
[ok] Picks CSV: C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\phaseV_picks_v1.csv

== Phase-V Scorecard (head) ==
                                                                       dataset  kind driver  priority_rank  Composite        E        I  C_ratio      C_p  C_sig  C_strong  O_best  O_best_p       phaseV_tags    GO status                                                                                                                                         source
artifacts__tables__genome3d__atlas__nodes_v1h_realhic__20251009-020445.parquet  real      E            1.0   0.343132 0.416036 0.419484 0.895404 1.000000  False     False     1.0      0.05             E★ O★ False     ok C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\featur

In [32]:
# === CNT Five-Pillar — Phase-V “Single Mega Cell” (strict picks + ratio sanity check) ===
# Robust, one-shot post-processing with optional re-computation of C_ratio using slower invariant EMA.
# Outputs (placed next to phaseV_report_v1.csv):
#  - phaseV_real_GO_strict.csv
#  - phaseV_real_GO_lenient.csv
#  - phaseV_synth_Csig.csv
#  - phaseV_scorebook_v2.xlsx  (Score + Picks sheets)
#  - phaseV_summary_strict.md  (human-readable recap)
#
# Safe to re-run: idempotent, fills missing columns, and gracefully skips missing sources.

import os, json, math, traceback
from pathlib import Path
import numpy as np
import pandas as pd

# ---------- Config ----------
BASE    = Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results")
REPORT  = BASE / "phaseV_report_v1.csv"     # must exist from your previous step
SCOREBK = BASE / "phaseV_scorebook_v2.xlsx"
MD      = BASE / "phaseV_summary_strict.md"

# Strict thresholds (tune here)
P_THRESH         = 0.05   # p-value for C_sig
CRATIO_STRICT    = 0.80   # invariants must drift slower than metrics
E_PASS_THRESH    = 0.40   # useful for "lenient" bucket
I_PASS_THRESH    = 0.50   # useful for "lenient" bucket

# Optional: re-compute an alternate/stabilized C_ratio using slower EMA on invariants
RECALC_C_RATIO          = True
EMA_ALPHA_INV_SLOW      = 0.005  # slower EMA for invariants (stabilize I0/I1)
PRINT_PER_ROW_DIAGNOSTIC= False  # set True to see per-row recompute logs


# ---------- Helpers ----------
def ema(x, alpha=0.01):
    x = np.asarray(x, float)
    y = np.empty_like(x)
    m = np.isfinite(x)
    if not m.any():
        return np.full_like(x, np.nan)
    y[:] = np.nan
    last = x[m][0]
    for i, xi in enumerate(x):
        if np.isfinite(xi):
            last = alpha * xi + (1 - alpha) * last
        y[i] = last
    return y

def _motion(v):
    """Mean abs(gradient) ignoring NaNs; returns np.nan if too short."""
    v = np.asarray(v, float)
    if v.size < 2:
        return np.nan
    g = np.gradient(v)
    g = g[np.isfinite(g)]
    return float(np.mean(np.abs(g))) if g.size else np.nan

def recompute_c_ratio_from_source(src_path, alpha_inv=EMA_ALPHA_INV_SLOW):
    """
    Recompute C_ratio = inv_motion / metr_motion from a source CSV.
    Uses I_beta0/I_beta1 if present, else EMA proxies from C and H.
    Returns np.nan on any hard failure (file missing, etc.).
    """
    try:
        df = pd.read_csv(src_path, low_memory=False)
    except Exception:
        return np.nan

    # Pull columns with safe fallbacks
    N = len(df)
    C = df.get("C", pd.Series([np.nan]*N)).to_numpy(dtype=float)
    H = df.get("H", pd.Series([np.nan]*N)).to_numpy(dtype=float)

    # Prefer provided invariants, else build slow EMA proxies from C & H
    if "I_beta0" in df.columns:
        I0 = df["I_beta0"].to_numpy(dtype=float)
    else:
        I0 = ema(C, alpha=alpha_inv)

    if "I_beta1" in df.columns:
        I1 = df["I_beta1"].to_numpy(dtype=float)
    else:
        I1 = ema(H, alpha=alpha_inv)

    inv_m  = np.nansum([_motion(I0), _motion(I1)])
    metr_m = np.nansum([_motion(C),  _motion(H)])

    if not (np.isfinite(inv_m) and np.isfinite(metr_m) and metr_m > 0):
        return np.nan
    return float(inv_m / (metr_m + 1e-12))


def nmin_ignore_nan(*vals):
    """Numeric min ignoring NaNs; returns NaN if all are NaN."""
    arr = np.array(vals, dtype=float)
    arr = arr[np.isfinite(arr)]
    return float(arr.min()) if arr.size else np.nan


# ---------- Load & normalize ----------
assert REPORT.exists(), f"Missing report CSV: {REPORT}"
score = pd.read_csv(REPORT)

# Ensure core columns exist (create with NaNs or sensible defaults if missing)
for col, default in [
    ("kind", np.nan),
    ("driver", np.nan),
    ("priority_rank", np.nan),
    ("Composite", np.nan),
    ("E", np.nan),
    ("I", np.nan),
    ("C_ratio", np.nan),
    ("C_p", np.nan),
    ("O_best", np.nan),
    ("O_best_p", np.nan),
    ("source", np.nan),
]:
    if col not in score.columns:
        score[col] = default

# Recreate derived flags (never fail on KeyError now)
score["C_sig"]    = score["C_p"] <= P_THRESH
score["E_pass"]   = score["E"] >= E_PASS_THRESH
score["I_pass"]   = score["I"] >= I_PASS_THRESH

# ---------- Optional: re-compute a stabilized C_ratio (slow EMA invariants) ----------
C_ratio_slow = []
if RECALC_C_RATIO:
    for idx, row in score.iterrows():
        src = str(row.get("source", "") or "")
        val = np.nan
        if src and Path(src).exists():
            try:
                val = recompute_c_ratio_from_source(src, alpha_inv=EMA_ALPHA_INV_SLOW)
            except Exception as e:
                if PRINT_PER_ROW_DIAGNOSTIC:
                    print(f"[recalc] {row.get('dataset','?')}: error {e}")
        else:
            if PRINT_PER_ROW_DIAGNOSTIC:
                print(f"[recalc] Missing/invalid source for row {idx}: {src}")
        C_ratio_slow.append(val)
else:
    C_ratio_slow = [np.nan]*len(score)

score["C_ratio_slow"] = C_ratio_slow
score["C_ratio_best"] = [
    nmin_ignore_nan(a, b) for a, b in zip(score["C_ratio"].to_numpy(), score["C_ratio_slow"].to_numpy())
]
score["C_strong"]      = score["C_ratio_best"] < CRATIO_STRICT

# ---------- Picks ----------
# Strict GO: must be C_sig AND C_strong (ratio test). E/I not required here.
GO_strict = (score["C_sig"] & score["C_strong"])

# A lenient bucket: either strict OR (E strong AND C_sig)
GO_lenient = (GO_strict | (score["E_pass"] & score["C_sig"]))

real_GO_strict  = score[(score["kind"]=="real")  & GO_strict].copy()
real_GO_lenient = score[(score["kind"]=="real")  & GO_lenient].copy()
synth_C_sig     = score[(score["kind"]=="synth") & score["C_sig"]].copy()

# ---------- Save picks & workbook ----------
OUT1 = BASE / "phaseV_real_GO_strict.csv"
OUT2 = BASE / "phaseV_real_GO_lenient.csv"
OUT3 = BASE / "phaseV_synth_Csig.csv"
real_GO_strict.to_csv(OUT1, index=False)
real_GO_lenient.to_csv(OUT2, index=False)
synth_C_sig.to_csv(OUT3, index=False)

# Excel scorebook with 4 sheets
try:
    with pd.ExcelWriter(SCOREBK, engine="openpyxl") as xw:
        score.to_excel(xw, index=False, sheet_name="Score")
        real_GO_strict.to_excel(xw, index=False, sheet_name="Real_GO_strict")
        real_GO_lenient.to_excel(xw, index=False, sheet_name="Real_GO_lenient")
        synth_C_sig.to_excel(xw, index=False, sheet_name="Synth_Csig")
except Exception as e:
    print(f"[warn] Excel write failed ({e}). Skipping workbook.")

# ---------- Write human summary ----------
lines = []
lines.append("== Phase-V Strict Picks Summary ==\n")
lines.append(f"- Input: {REPORT}")
lines.append(f"- n(rows): {len(score)}")
lines.append(f"- Strict thresholds: p≤{P_THRESH}, C_ratio<{CRATIO_STRICT}, E_pass≥{E_PASS_THRESH}, I_pass≥{I_PASS_THRESH}")
lines.append(f"- Recomputed C_ratio_slow (alpha_inv={EMA_ALPHA_INV_SLOW}): {'ON' if RECALC_C_RATIO else 'OFF'}\n")

lines.append(f"**Strict Real GO:** {len(real_GO_strict)}")
if len(real_GO_strict):
    cols = ["dataset","driver","priority_rank","Composite","E","I","C_ratio","C_ratio_slow","C_ratio_best","C_p"]
    lines.append(pd.DataFrame(real_GO_strict, columns=[c for c in cols if c in real_GO_strict.columns]).head(10).to_string(index=False))
else:
    lines.append("(none)")

lines.append("\n**Lenient Real GO (strict OR E&Csig):** " + str(len(real_GO_lenient)))
if len(real_GO_lenient):
    cols = ["dataset","driver","priority_rank","Composite","E","I","C_ratio_best","C_p"]
    lines.append(pd.DataFrame(real_GO_lenient, columns=[c for c in cols if c in real_GO_lenient.columns]).head(10).to_string(index=False))

lines.append("\n**Synth C-sig:** " + str(len(synth_C_sig)))
if len(synth_C_sig):
    cols = ["dataset","driver","priority_rank","Composite","E","I","C_ratio_best","C_p"]
    lines.append(pd.DataFrame(synth_C_sig, columns=[c for c in cols if c in synth_C_sig.columns]).head(10).to_string(index=False))

# Quick callouts for “real results”
real_csig = score[(score["kind"]=="real") & (score["C_sig"])].copy()
lines.append("\n**Real C-significant (any ratio):** " + str(len(real_csig)))
if len(real_csig):
    cols = ["dataset","E","I","C_ratio","C_ratio_slow","C_ratio_best","C_p"]
    lines.append(pd.DataFrame(real_csig, columns=[c for c in cols if c in real_csig.columns]).sort_values("C_p").head(10).to_string(index=False))

# Save & print
MD.write_text("\n".join(lines), encoding="utf-8")

print("[ok] Strict picks saved:")
print(" -", OUT1)
print(" -", OUT2)
print(" -", OUT3)
if SCOREBK.exists():
    print(" -", SCOREBK)
print(" -", MD)

print("\n== Head (Score with recomputed ratios) ==")
show_cols = [c for c in ["dataset","kind","driver","priority_rank","Composite","E","I","C_ratio","C_ratio_slow","C_ratio_best","C_sig","C_strong"] if c in score.columns]
print(score[show_cols].head(10).to_string(index=False))


[ok] Strict picks saved:
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\phaseV_real_GO_strict.csv
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\phaseV_real_GO_lenient.csv
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\phaseV_synth_Csig.csv
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\phaseV_scorebook_v2.xlsx
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\phaseV_summary_strict.md

== Head (Score with recomputed ratios) ==
                                                                       dataset  kind driver  priority_rank  Composite        E        I  C_ratio  C_ratio_slow  C_ratio_best  C_sig  C_strong
artifacts__tables__genome3d__atlas__nodes_v1h_realhic__20251009-020445.parquet  real      E            1.0   0.343132 0.416036 0.419484 0.895404      0.895404      0.895404  False     False
         artifacts__tables__genome3d__atlas__ge

In [33]:
# === Phase-V sensitivity sweep (v1.1) — relax ratio & E thresholds ===
from pathlib import Path
import numpy as np, pandas as pd

BASE = Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results")
CSV  = BASE / "phaseV_report_v1.csv"
df   = pd.read_csv(CSV)

# ensure columns exist
for c in ["kind","E","I","C_ratio","C_p"]: 
    if c not in df.columns: df[c] = np.nan

# thresholds (relaxed)
P_THRESH       = 0.05
CRATIO_STRICT  = 0.95
E_PASS_THRESH  = 0.30

df["C_sig"]   = df["C_p"] <= P_THRESH
df["C_strong"]= df["C_ratio"] < CRATIO_STRICT
df["E_pass"]  = df["E"] >= E_PASS_THRESH

GO_strict   = (df["C_sig"] & df["C_strong"])
GO_lenient  = (GO_strict | (df["E_pass"] & df["C_sig"]))

real_GO_strict_v11  = df[(df["kind"]=="real")  & GO_strict].copy()
real_GO_lenient_v11 = df[(df["kind"]=="real")  & GO_lenient].copy()
synth_Csig_v11      = df[(df["kind"]=="synth") & df["C_sig"]].copy()

# write side-by-side
real_GO_strict_v11.to_csv(BASE/"phaseV_real_GO_strict_v1p1.csv", index=False)
real_GO_lenient_v11.to_csv(BASE/"phaseV_real_GO_lenient_v1p1.csv", index=False)
synth_Csig_v11.to_csv(BASE/"phaseV_synth_Csig_v1p1.csv", index=False)

print("[v1.1] strict_real:", len(real_GO_strict_v11),
      "| lenient_real:", len(real_GO_lenient_v11),
      "| synth_Csig:", len(synth_Csig_v11))
print("Files:")
print(" -", BASE/"phaseV_real_GO_strict_v1p1.csv")
print(" -", BASE/"phaseV_real_GO_lenient_v1p1.csv")
print(" -", BASE/"phaseV_synth_Csig_v1p1.csv")


[v1.1] strict_real: 0 | lenient_real: 2 | synth_Csig: 0
Files:
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\phaseV_real_GO_strict_v1p1.csv
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\phaseV_real_GO_lenient_v1p1.csv
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\phaseV_synth_Csig_v1p1.csv


In [34]:
# === Phase-V v1.2 — robust ratio + bootstrap CI + refreshed picks (single cell) ===
import numpy as np, pandas as pd, os, json
from pathlib import Path

# -----------------------------
# Config & IO
# -----------------------------
BASE = Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results")
IN_CSV  = BASE / "phaseV_report_v1.csv"               # your existing scorecard
OUT_CSV = BASE / "phaseV_report_v1p2.csv"             # updated scorecard with robust fields
OUT_MD  = BASE / "phaseV_report_v1p2.md"

OUT_REAL_STRICT   = BASE / "phaseV_real_GO_strict_v1p2.csv"
OUT_REAL_LENIENT  = BASE / "phaseV_real_GO_lenient_v1p2.csv"
OUT_SYNTH_CSIG    = BASE / "phaseV_synth_Csig_v1p2.csv"

# Thresholds (keep strict at 0.80, E at 0.40 to match your original)
P_THRESH       = 0.05
CRATIO_STRICT  = 0.80
E_PASS_THRESH  = 0.40

# Bootstrap settings (kept light; tune up if you want)
N_BOOT   = 120
SUB_FRAC = 0.70
RNG      = np.random.default_rng(1234)

# -----------------------------
# Helpers
# -----------------------------
def ema(x, alpha=0.01):
    x = np.asarray(x, float)
    y = np.empty_like(x); y[:] = np.nan
    m = np.isfinite(x)
    if not m.any(): return y
    last = x[m][0]
    for i, xi in enumerate(x):
        if np.isfinite(xi): last = alpha*xi + (1-alpha)*last
        y[i] = last
    return y

def robust_motion(v):
    """Median |first difference|; NaN if <2 finite points."""
    a = np.asarray(v, float)
    m = np.isfinite(a)
    if m.sum() < 2: return np.nan
    d = np.diff(a[m])
    d = d[np.isfinite(d)]
    return float(np.median(np.abs(d))) if d.size else np.nan

def compute_robust_ratio_from_source(src_path):
    """
    Read a source CSV, derive invariants (I_beta0/I_beta1 or EMA proxies),
    metrics (C,H), and compute robust ratio = (motion(I0)+motion(I1)) / (motion(C)+motion(H)).
    Returns (ratio, ratio_ci_lo, ratio_ci_hi).
    """
    if not src_path or (not os.path.exists(src_path)):
        return (np.nan, np.nan, np.nan)
    try:
        df = pd.read_csv(src_path, low_memory=False)
    except Exception:
        return (np.nan, np.nan, np.nan)

    # Pull columns with fallbacks
    C = df.get("C", pd.Series([np.nan]*len(df))).to_numpy(float)
    H = df.get("H", pd.Series([np.nan]*len(df))).to_numpy(float)

    # Invariants: if present use them; else slow EMA proxies of metrics
    I0 = df["I_beta0"].to_numpy(float) if "I_beta0" in df.columns else ema(C, alpha=0.01)
    I1 = df["I_beta1"].to_numpy(float) if "I_beta1" in df.columns else ema(H, alpha=0.01)

    def ratio_on_index(idx):
        # subset by index list (for bootstrap subsampling)
        C_sub  = C[idx]
        H_sub  = H[idx]
        I0_sub = I0[idx]
        I1_sub = I1[idx]
        inv_m  = np.nansum([robust_motion(I0_sub), robust_motion(I1_sub)])
        metr_m = np.nansum([robust_motion(C_sub),  robust_motion(H_sub)])
        if not np.isfinite(inv_m) or not np.isfinite(metr_m) or metr_m <= 0:
            return np.nan
        return float(inv_m / (metr_m + 1e-12))

    # Full-series robust ratio
    n = len(C)
    idx_full = np.arange(n)
    ratio = ratio_on_index(idx_full)

    # Bootstrap CI on subsampled windows
    boots = []
    if n >= 10:  # need at least a bit of data
        k = max(5, int(np.floor(SUB_FRAC * n)))
        for _ in range(N_BOOT):
            idx = np.sort(RNG.choice(n, size=k, replace=False))
            r = ratio_on_index(idx)
            if np.isfinite(r):
                boots.append(r)
    if boots:
        lo, hi = np.nanpercentile(boots, [5, 95])
    else:
        lo = hi = np.nan

    return (ratio, lo, hi)

# -----------------------------
# Load, compute, update
# -----------------------------
score = pd.read_csv(IN_CSV)
for need in ["dataset","kind","E","I","C_ratio","C_p","source"]:
    if need not in score.columns:
        score[need] = np.nan

# Compute robust ratios per row using 'source'
rob_vals = []
print("Computing robust ratios (median |Δ|) ...")
for i, r in score.iterrows():
    src = r.get("source", "")
    ratio, lo, hi = compute_robust_ratio_from_source(src)
    rob_vals.append((ratio, lo, hi))
    tag = f"{r.get('dataset','?')}"
    print(f" - [{i+1}/{len(score)}] {tag}  ->  C_ratio_robust={ratio:.4g}  CI[5,95%]=({lo:.4g}, {hi:.4g})" if np.isfinite(ratio) else
          f" - [{i+1}/{len(score)}] {tag}  ->  C_ratio_robust=NaN")

score["C_ratio_robust"]    = [v[0] for v in rob_vals]
score["C_ratio_robust_lo"] = [v[1] for v in rob_vals]
score["C_ratio_robust_hi"] = [v[2] for v in rob_vals]

# Primary flags
score["C_sig"]    = score["C_p"] <= P_THRESH
score["E_pass"]   = score["E"]   >= E_PASS_THRESH
score["C_strict_robust"] = score["C_ratio_robust"] < CRATIO_STRICT

# Decisions (v1.2 uses robust ratio for strict; lenient = E_pass & C_sig)
GO_strict_v12  = (score["C_sig"] & score["C_strict_robust"])
GO_lenient_v12 = (GO_strict_v12 | (score["E_pass"] & score["C_sig"]))

# -----------------------------
# Write updated reports & picks
# -----------------------------
score.to_csv(OUT_CSV, index=False)

real_strict  = score[(score["kind"]=="real")  & GO_strict_v12].copy()
real_lenient = score[(score["kind"]=="real")  & GO_lenient_v12].copy()
synth_csig   = score[(score["kind"]=="synth") & score["C_sig"]].copy()

real_strict.to_csv(OUT_REAL_STRICT, index=False)
real_lenient.to_csv(OUT_REAL_LENIENT, index=False)
synth_csig.to_csv(OUT_SYNTH_CSIG, index=False)

with open(OUT_MD, "w", encoding="utf-8") as f:
    f.write("# Phase-V v1.2 — Robust Ratio Update\n\n")
    f.write(f"- Input:  {IN_CSV}\n")
    f.write(f"- Output: {OUT_CSV}\n\n")
    f.write(f"**Thresholds:** p≤{P_THRESH}, robust C_ratio<{CRATIO_STRICT}, E≥{E_PASS_THRESH}\n\n")
    f.write(f"**Counts:** strict_real={len(real_strict)} | lenient_real={len(real_lenient)} | synth_Csig={len(synth_csig)}\n\n")
    f.write("## Top rows (real, sorted by Composite)\n\n")
    cols = ["dataset","Composite","E","I","C_ratio","C_ratio_robust","C_ratio_robust_lo","C_ratio_robust_hi","C_p","C_sig","C_strict_robust"]
    f.write(score[score["kind"]=="real"][cols].sort_values("Composite", ascending=False).head(10).to_string(index=False))
    f.write("\n")

print("\n== v1.2 Summary ==")
print(" strict_real:", len(real_strict),
      "| lenient_real:", len(real_lenient),
      "| synth_Csig:", len(synth_csig))
print("Wrote:")
print(" -", OUT_CSV)
print(" -", OUT_MD)
print(" -", OUT_REAL_STRICT)
print(" -", OUT_REAL_LENIENT)
print(" -", OUT_SYNTH_CSIG)


Computing robust ratios (median |Δ|) ...
 - [1/7] artifacts__tables__genome3d__atlas__nodes_v1h_realhic__20251009-020445.parquet  ->  C_ratio_robust=0  CI[5,95%]=(0, 0)
 - [2/7] artifacts__tables__genome3d__atlas__genes_v1__20251008-214043.parquet  ->  C_ratio_robust=0  CI[5,95%]=(0, 0)
 - [3/7] artifacts__tables__migrated__gdf-snapshot__d8dc9743.csv  ->  C_ratio_robust=NaN
 - [4/7] artifacts__tables__genome3d__atlas__nodes_v1h__20251008-215623.parquet  ->  C_ratio_robust=0  CI[5,95%]=(0, 0)
 - [5/7] artifacts__tables__genome3d__atlas__nodes_v0c__20251008-213724.parquet  ->  C_ratio_robust=0  CI[5,95%]=(0, 0)
 - [6/7] artifacts__tables__migrated__sim-theta__fc536f2f.csv  ->  C_ratio_robust=0  CI[5,95%]=(0, 0)
 - [7/7] artifacts__tables__migrated__sim-alpha__f44f6f05.csv  ->  C_ratio_robust=0  CI[5,95%]=(0, 0)

== v1.2 Summary ==
 strict_real: 2 | lenient_real: 3 | synth_Csig: 0
Wrote:
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\phaseV_report_v1p2.csv
 - 

In [35]:
# === Phase-V v1.3 — p90-diff robust ratio + eps smoothing + inconclusive guard ===
import numpy as np, pandas as pd, os
from pathlib import Path

# --- IO ---
BASE = Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results")
IN_CSV  = BASE / "phaseV_report_v1.csv"
OUT_CSV = BASE / "phaseV_report_v1p3.csv"
OUT_MD  = BASE / "phaseV_report_v1p3.md"
OUT_REAL_STRICT   = BASE / "phaseV_real_GO_strict_v1p3.csv"
OUT_REAL_LENIENT  = BASE / "phaseV_real_GO_lenient_v1p3.csv"
OUT_SYNTH_CSIG    = BASE / "phaseV_synth_Csig_v1p3.csv"

# --- thresholds (unchanged logic, stricter ratio via p90) ---
P_THRESH       = 0.05
CRATIO_STRICT  = 0.80
E_PASS_THRESH  = 0.40
EPS            = 1e-6  # smooth both motions

def ema(x, alpha=0.01):
    x = np.asarray(x, float)
    y = np.full_like(x, np.nan, dtype=float)
    m = np.isfinite(x)
    if not m.any(): return y
    last = x[m][0]
    for i, xi in enumerate(x):
        if np.isfinite(xi): last = alpha*xi + (1-alpha)*last
        y[i] = last
    return y

def motion_p90(v):
    """p90(|Δ|); robust against flat/stepwise series but not zeroed by single flats."""
    a = np.asarray(v, float)
    m = np.isfinite(a)
    if m.sum() < 2: return np.nan
    d = np.diff(a[m])
    d = d[np.isfinite(d)]
    return float(np.nanpercentile(np.abs(d), 90)) if d.size else np.nan

def compute_ratio_p90(src_path):
    """Return (ratio, lo, hi) using p90(|Δ|) and eps smoothing; NaN if both motions ~0."""
    if not src_path or not os.path.exists(src_path): return (np.nan, np.nan, np.nan)
    try:
        df = pd.read_csv(src_path, low_memory=False)
    except Exception:
        return (np.nan, np.nan, np.nan)

    C = df.get("C",  pd.Series([np.nan]*len(df))).to_numpy(float)
    H = df.get("H",  pd.Series([np.nan]*len(df))).to_numpy(float)
    I0 = (df["I_beta0"].to_numpy(float) if "I_beta0" in df.columns else ema(C, 0.01))
    I1 = (df["I_beta1"].to_numpy(float) if "I_beta1" in df.columns else ema(H, 0.01))

    inv_m  = np.nansum([motion_p90(I0), motion_p90(I1)])
    metr_m = np.nansum([motion_p90(C),  motion_p90(H)])

    # if both are essentially flat, mark inconclusive
    if (not np.isfinite(inv_m)) or (not np.isfinite(metr_m)):
        return (np.nan, np.nan, np.nan)
    if (inv_m < EPS) and (metr_m < EPS):
        return (np.nan, np.nan, np.nan)

    ratio = (inv_m + EPS) / (metr_m + EPS)

    # simple bootstrap over indices for CI (lightweight)
    n = len(C)
    boots = []
    if n >= 12:
        rng = np.random.default_rng(2025)
        k = max(6, int(0.7*n))
        idx = np.arange(n)
        for _ in range(120):
            sub = np.sort(rng.choice(idx, size=k, replace=False))
            inv_b = np.nansum([motion_p90(I0[sub]), motion_p90(I1[sub])])
            metr_b= np.nansum([motion_p90(C[sub]),  motion_p90(H[sub])])
            if np.isfinite(inv_b) and np.isfinite(metr_b):
                if (inv_b < EPS) and (metr_b < EPS):
                    continue
                boots.append((inv_b+EPS)/(metr_b+EPS))
    lo, hi = (np.nan, np.nan)
    if boots:
        lo, hi = np.nanpercentile(boots, [5, 95])
    return (float(ratio), float(lo), float(hi))

# --- load & augment ---
score = pd.read_csv(IN_CSV)
for col in ["dataset","kind","E","I","C_ratio","C_p","source"]:
    if col not in score.columns: score[col] = np.nan

print("Recomputing C_ratio_robust (p90) ...")
rows=[]
for i, r in score.iterrows():
    ratio, lo, hi = compute_ratio_p90(r.get("source", ""))
    rows.append((ratio, lo, hi))
    name = r.get("dataset","?")
    if np.isfinite(ratio):
        print(f" - [{i+1}/{len(score)}] {name} -> robust={ratio:.4g} CI=({lo:.4g},{hi:.4g})")
    else:
        print(f" - [{i+1}/{len(score)}] {name} -> robust=NaN")

score["C_ratio_robust"]    = [x[0] for x in rows]
score["C_ratio_robust_lo"] = [x[1] for x in rows]
score["C_ratio_robust_hi"] = [x[2] for x in rows]

# flags
score["C_sig"]  = score["C_p"] <= P_THRESH
score["E_pass"] = score["E"]   >= E_PASS_THRESH
score["C_strict_robust"] = score["C_ratio_robust"] < CRATIO_STRICT

# decisions
GO_strict  = (score["C_sig"] & score["C_strict_robust"])
GO_lenient = (GO_strict | (score["E_pass"] & score["C_sig"]))

# outputs
score.to_csv(OUT_CSV, index=False)
real_strict  = score[(score["kind"]=="real")  & GO_strict].copy()
real_lenient = score[(score["kind"]=="real")  & GO_lenient].copy()
synth_csig   = score[(score["kind"]=="synth") & score["C_sig"]].copy()

real_strict.to_csv(OUT_REAL_STRICT, index=False)
real_lenient.to_csv(OUT_REAL_LENIENT, index=False)
synth_csig.to_csv(OUT_SYNTH_CSIG, index=False)

with open(OUT_MD, "w", encoding="utf-8") as f:
    f.write("# Phase-V v1.3 — p90 robust ratio\n\n")
    f.write(f"- Input:  {IN_CSV}\n- Output: {OUT_CSV}\n\n")
    f.write(f"**Thresh:** p≤{P_THRESH}, robust C_ratio<{CRATIO_STRICT}, E≥{E_PASS_THRESH}\n\n")
    f.write(f"**Counts:** strict_real={len(real_strict)} | lenient_real={len(real_lenient)} | synth_Csig={len(synth_csig)}\n\n")
    cols = ["dataset","Composite","E","I","C_ratio","C_ratio_robust","C_ratio_robust_lo","C_ratio_robust_hi","C_p","C_sig","C_strict_robust"]
    f.write(score[score['kind']=='real'][cols].sort_values('Composite', ascending=False).head(10).to_string(index=False))
    f.write("\n")

print("\n== v1.3 Summary ==")
print(" strict_real:", len(real_strict),
      "| lenient_real:", len(real_lenient),
      "| synth_Csig:", len(synth_csig))
print("Wrote:")
print(" -", OUT_CSV)
print(" -", OUT_MD)
print(" -", OUT_REAL_STRICT)
print(" -", OUT_REAL_LENIENT)
print(" -", OUT_SYNTH_CSIG)


Recomputing C_ratio_robust (p90) ...
 - [1/7] artifacts__tables__genome3d__atlas__nodes_v1h_realhic__20251009-020445.parquet -> robust=1.559e-05 CI=(1.079e-05,1.285e-05)
 - [2/7] artifacts__tables__genome3d__atlas__genes_v1__20251008-214043.parquet -> robust=1.427e-05 CI=(9.01e-06,1.133e-05)
 - [3/7] artifacts__tables__migrated__gdf-snapshot__d8dc9743.csv -> robust=37.34 CI=(18.51,28.34)
 - [4/7] artifacts__tables__genome3d__atlas__nodes_v1h__20251008-215623.parquet -> robust=1.538e-05 CI=(1.08e-05,1.281e-05)
 - [5/7] artifacts__tables__genome3d__atlas__nodes_v0c__20251008-213724.parquet -> robust=2.308 CI=(1.989,4.437)
 - [6/7] artifacts__tables__migrated__sim-theta__fc536f2f.csv -> robust=0.0001625 CI=(0.0001475,0.0001668)
 - [7/7] artifacts__tables__migrated__sim-alpha__f44f6f05.csv -> robust=0.0001708 CI=(0.0001571,0.000172)

== v1.3 Summary ==
 strict_real: 1 | lenient_real: 2 | synth_Csig: 0
Wrote:
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\phaseV

In [36]:
# === Phase-V v1.3 — Decision pack (strict/lenient) ===
import pandas as pd, numpy as np, os, json, zipfile, textwrap
from pathlib import Path
from datetime import datetime

BASE   = Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars")
PVR    = BASE / "mega_v1" / "phaseV_results"

# Inputs (v1.3)
REPORT_CSV = PVR / "phaseV_report_v1p3.csv"
REPORT_MD  = PVR / "phaseV_report_v1p3.md"
REAL_STRICT= PVR / "phaseV_real_GO_strict_v1p3.csv"
REAL_LEN   = PVR / "phaseV_real_GO_lenient_v1p3.csv"
SYN_CSIG   = PVR / "phaseV_synth_Csig_v1p3.csv"

# Optional extras for bundle
PACKETS_DIR = BASE / "packets_v3"
GALLERY_PDF = PACKETS_DIR / "packets_gallery_v3.pdf"
ONEPAGER_CSV= PACKETS_DIR / "packets_onepager_index_v3.csv"
MASTER_SHEET= BASE / "CNT_Master_Sheet_v3.csv"

# Outputs
DECISION_MD   = PVR / "PhaseV_Decision_v1p3.md"
DECISION_CSV  = PVR / "PhaseV_Decision_v1p3.csv"
DECISION_JSON = PVR / "PhaseV_Decision_v1p3.json"
BUNDLE_ZIP    = PVR / "PhaseV_decision_bundle_v1p3.zip"

# Thresholds used in v1.3
P_THRESH      = 0.05
CRATIO_STRICT = 0.80
E_PASS_THRESH = 0.40

assert REPORT_CSV.exists(), f"Missing {REPORT_CSV}"
df = pd.read_csv(REPORT_CSV)

# Ensure columns exist
for c in ["dataset","kind","E","I","Composite","C_p","C_ratio_robust","C_ratio_robust_lo","C_ratio_robust_hi"]:
    if c not in df.columns: df[c] = np.nan

df["C_sig"]           = df["C_p"] <= P_THRESH
df["E_pass"]          = df["E"]   >= E_PASS_THRESH
df["C_strict_robust"] = df["C_ratio_robust"] < CRATIO_STRICT

# Decisions
df["decision"] = "reject"
df.loc[(df["kind"]=="real") & (df["C_sig"] & df["C_strict_robust"]), "decision"] = "strict_real"
df.loc[(df["kind"]=="real") & ((df["C_sig"] & df["E_pass"]) | (df["decision"]=="strict_real")), "decision"] = df.loc[(df["kind"]=="real") & ((df["C_sig"] & df["E_pass"]) | (df["decision"]=="strict_real")), "decision"].replace("strict_real","strict_real").fillna("lenient_real")
# Note: strict stays "strict_real"; others with E_pass∧C_sig become "lenient_real"
df.loc[(df["kind"]=="synth") & (df["C_sig"]), "decision"] = "synth_csig"

# Keep only the useful columns for the decision CSV
keep_cols = [
    "dataset","kind","Composite","E","I","C_p","C_sig",
    "C_ratio_robust","C_ratio_robust_lo","C_ratio_robust_hi",
    "C_strict_robust","E_pass","decision","source"
]
dec = df[keep_cols].copy().sort_values(["decision","kind","Composite"], ascending=[True, True, False])
dec.to_csv(DECISION_CSV, index=False)

# JSON manifest for programmatic consumption
payload = {
    "timestamp": datetime.now().isoformat(timespec="seconds"),
    "criteria": {
        "p_value_max": P_THRESH,
        "robust_ratio_max": CRATIO_STRICT,
        "E_pass_min": E_PASS_THRESH
    },
    "counts": {
        "strict_real": int((dec["decision"]=="strict_real").sum()),
        "lenient_real": int((dec["decision"]=="lenient_real").sum()),
        "synth_csig": int((dec["decision"]=="synth_csig").sum()),
        "total": int(len(dec))
    },
    "strict_real": dec.loc[dec["decision"]=="strict_real","dataset"].tolist(),
    "lenient_real": dec.loc[dec["decision"]=="lenient_real","dataset"].tolist(),
    "synth_csig": dec.loc[dec["decision"]=="synth_csig","dataset"].tolist(),
}
json.dump(payload, open(DECISION_JSON, "w"), indent=2)

# Markdown decision note (short & exec-friendly)
def tbl(sub):
    if sub.empty: return "_(none)_"
    cols = ["dataset","Composite","E","C_p","C_ratio_robust","C_ratio_robust_lo","C_ratio_robust_hi"]
    cols = [c for c in cols if c in sub.columns]
    return sub[cols].to_string(index=False)

strict_tbl  = tbl(dec[dec["decision"]=="strict_real"])
lenient_tbl = tbl(dec[dec["decision"]=="lenient_real"])
synth_tbl   = tbl(dec[dec["decision"]=="synth_csig"])

with open(DECISION_MD, "w", encoding="utf-8") as f:
    f.write("# Phase-V Decision — v1.3 (p90 robust ratio)\n\n")
    f.write(f"- Input report: `{REPORT_CSV.name}`\n")
    f.write(f"- Criteria: p≤{P_THRESH}, robust C_ratio<{CRATIO_STRICT}, E≥{E_PASS_THRESH} (for lenient)\n\n")
    f.write(f"**Counts** — strict_real: {payload['counts']['strict_real']} | lenient_real: {payload['counts']['lenient_real']} | synth_Csig: {payload['counts']['synth_csig']}\n\n")

    f.write("## Strict (real)\n")
    f.write(strict_tbl + "\n\n")

    f.write("## Lenient (real)\n")
    f.write(lenient_tbl + "\n\n")

    f.write("## Synth (C_sig)\n")
    f.write(synth_tbl + "\n\n")

    f.write("### Notes\n")
    f.write("- *Robust C_ratio* uses p90(|Δ|) with ε-smoothing; extremely flat series no longer collapse to exact 0.\n")
    f.write("- Treat *lenient* as provisional: passes E & p-value but fails robust ratio.\n")

# Build a compact handoff bundle
with zipfile.ZipFile(BUNDLE_ZIP, "w", zipfile.ZIP_DEFLATED) as z:
    for p in [REPORT_CSV, REPORT_MD, DECISION_CSV, DECISION_MD, DECISION_JSON,
              REAL_STRICT, REAL_LEN, SYN_CSIG]:
        if p and Path(p).exists():
            z.write(p, arcname=p.name)
    # Optional extras
    for p in [GALLERY_PDF, ONEPAGER_CSV, MASTER_SHEET]:
        if p and Path(p).exists():
            z.write(p, arcname=p.name)

print("== Phase-V v1.3 Decision Pack ==")
print(" strict_real:", payload["counts"]["strict_real"])
print(" lenient_real:", payload["counts"]["lenient_real"])
print(" synth_Csig:", payload["counts"]["synth_csig"])
print("Wrote:")
print(" -", DECISION_CSV)
print(" -", DECISION_MD)
print(" -", DECISION_JSON)
print(" -", BUNDLE_ZIP)


== Phase-V v1.3 Decision Pack ==
 strict_real: 1
 lenient_real: 0
 synth_Csig: 0
Wrote:
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\PhaseV_Decision_v1p3.csv
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\PhaseV_Decision_v1p3.md
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\PhaseV_Decision_v1p3.json
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\PhaseV_decision_bundle_v1p3.zip


In [37]:
# === Phase-V v1.3r1 — Correct decision labeling & bundle ===
import pandas as pd, numpy as np, json, zipfile
from pathlib import Path
from datetime import datetime

BASE   = Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars")
PVR    = BASE / "mega_v1" / "phaseV_results"

# Inputs
REPORT_CSV = PVR / "phaseV_report_v1p3.csv"
REPORT_MD  = PVR / "phaseV_report_v1p3.md"

# Outputs (revision r1)
DECISION_CSV  = PVR / "PhaseV_Decision_v1p3r1.csv"
DECISION_MD   = PVR / "PhaseV_Decision_v1p3r1.md"
DECISION_JSON = PVR / "PhaseV_Decision_v1p3r1.json"
BUNDLE_ZIP    = PVR / "PhaseV_decision_bundle_v1p3r1.zip"

# Optional extras for bundle
PACKETS_DIR = BASE / "packets_v3"
GALLERY_PDF = PACKETS_DIR / "packets_gallery_v3.pdf"
ONEPAGER_CSV= PACKETS_DIR / "packets_onepager_index_v3.csv"
MASTER_SHEET= BASE / "CNT_Master_Sheet_v3.csv"

# Criteria
P_THRESH      = 0.05
CRATIO_STRICT = 0.80
E_PASS_THRESH = 0.40

assert REPORT_CSV.exists(), f"Missing {REPORT_CSV}"
df = pd.read_csv(REPORT_CSV)

# Ensure needed columns exist
need = ["dataset","kind","E","I","Composite","C_p","C_ratio_robust",
        "C_ratio_robust_lo","C_ratio_robust_hi","source"]
for c in need:
    if c not in df.columns: df[c] = np.nan

# Derived gates
df["C_sig"]           = df["C_p"] <= P_THRESH
df["E_pass"]          = df["E"]   >= E_PASS_THRESH
df["C_strict_robust"] = df["C_ratio_robust"] < CRATIO_STRICT

# Explicit masks (no in-place overwrite bugs)
is_real  = df["kind"] == "real"
is_synth = df["kind"] == "synth"

m_strict  = is_real  & df["C_sig"] & df["C_strict_robust"]
m_lenient = is_real  & df["C_sig"] & df["E_pass"] & (~m_strict)
m_synth   = is_synth & df["C_sig"]

df["decision"] = "reject"
df.loc[m_strict,  "decision"] = "strict_real"
df.loc[m_lenient, "decision"] = "lenient_real"
df.loc[m_synth,   "decision"] = "synth_csig"

# Save compact decision table
keep = ["dataset","kind","Composite","E","I","C_p","C_sig",
        "C_ratio_robust","C_ratio_robust_lo","C_ratio_robust_hi",
        "C_strict_robust","E_pass","decision","source"]
dec = df[keep].copy().sort_values(
    ["decision","kind","Composite"], ascending=[True, True, False]
)
dec.to_csv(DECISION_CSV, index=False)

# Build JSON summary
payload = {
    "timestamp": datetime.now().isoformat(timespec="seconds"),
    "criteria": {
        "p_value_max": P_THRESH,
        "robust_ratio_max": CRATIO_STRICT,
        "E_pass_min": E_PASS_THRESH
    },
    "counts": {
        "strict_real": int(m_strict.sum()),
        "lenient_real": int(m_lenient.sum()),
        "synth_csig": int(m_synth.sum()),
        "total": int(len(df)),
    },
    "strict_real": df.loc[m_strict, "dataset"].tolist(),
    "lenient_real": df.loc[m_lenient, "dataset"].tolist(),
    "synth_csig":  df.loc[m_synth,  "dataset"].tolist(),
}
json.dump(payload, open(DECISION_JSON, "w"), indent=2)

# Markdown summary
def table(sub):
    if sub.empty: return "_(none)_"
    cols = ["dataset","Composite","E","C_p","C_ratio_robust","C_ratio_robust_lo","C_ratio_robust_hi"]
    cols = [c for c in cols if c in sub.columns]
    return sub[cols].to_string(index=False)

strict_tbl  = table(dec[dec["decision"]=="strict_real"])
lenient_tbl = table(dec[dec["decision"]=="lenient_real"])
synth_tbl   = table(dec[dec["decision"]=="synth_csig"])

with open(DECISION_MD, "w", encoding="utf-8") as f:
    f.write("# Phase-V Decision — v1.3r1 (corrected gating)\n\n")
    f.write(f"- Input: `{REPORT_CSV.name}`\n")
    f.write(f"- Criteria: p≤{P_THRESH}, robust C_ratio<{CRATIO_STRICT} (strict); lenient requires E≥{E_PASS_THRESH} & p≤{P_THRESH}\n\n")
    f.write(f"**Counts** — strict_real: {payload['counts']['strict_real']} | lenient_real: {payload['counts']['lenient_real']} | synth_Csig: {payload['counts']['synth_csig']}\n\n")
    f.write("## Strict (real)\n" + strict_tbl + "\n\n")
    f.write("## Lenient (real)\n" + lenient_tbl + "\n\n")
    f.write("## Synth (C_sig)\n" + synth_tbl + "\n\n")
    f.write("### Note\n- This revision fixes a labeling bug where rows meeting (E_pass ∧ C_sig) were left as `reject` if not already `strict`.\n")

# Bundle
with zipfile.ZipFile(BUNDLE_ZIP, "w", zipfile.ZIP_DEFLATED) as z:
    for p in [REPORT_CSV, REPORT_MD, DECISION_CSV, DECISION_MD, DECISION_JSON]:
        if Path(p).exists(): z.write(p, arcname=Path(p).name)
    for p in [GALLERY_PDF, ONEPAGER_CSV, MASTER_SHEET]:
        if Path(p).exists(): z.write(p, arcname=Path(p).name)

print("== Phase-V v1.3r1 Decision Pack ==")
print(" strict_real:", payload["counts"]["strict_real"])
print(" lenient_real:", payload["counts"]["lenient_real"])
print(" synth_Csig:", payload["counts"]["synth_csig"])
print("Wrote:")
print(" -", DECISION_CSV)
print(" -", DECISION_MD)
print(" -", DECISION_JSON)
print(" -", BUNDLE_ZIP)


== Phase-V v1.3r1 Decision Pack ==
 strict_real: 1
 lenient_real: 1
 synth_Csig: 0
Wrote:
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\PhaseV_Decision_v1p3r1.csv
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\PhaseV_Decision_v1p3r1.md
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\PhaseV_Decision_v1p3r1.json
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\PhaseV_decision_bundle_v1p3r1.zip


In [38]:
# === Phase-V v1.3r1 — Correct decision labeling & bundle ===
import pandas as pd, numpy as np, json, zipfile
from pathlib import Path
from datetime import datetime

BASE   = Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars")
PVR    = BASE / "mega_v1" / "phaseV_results"

# Inputs
REPORT_CSV = PVR / "phaseV_report_v1p3.csv"
REPORT_MD  = PVR / "phaseV_report_v1p3.md"

# Outputs (revision r1)
DECISION_CSV  = PVR / "PhaseV_Decision_v1p3r1.csv"
DECISION_MD   = PVR / "PhaseV_Decision_v1p3r1.md"
DECISION_JSON = PVR / "PhaseV_Decision_v1p3r1.json"
BUNDLE_ZIP    = PVR / "PhaseV_decision_bundle_v1p3r1.zip"

# Optional extras for bundle
PACKETS_DIR = BASE / "packets_v3"
GALLERY_PDF = PACKETS_DIR / "packets_gallery_v3.pdf"
ONEPAGER_CSV= PACKETS_DIR / "packets_onepager_index_v3.csv"
MASTER_SHEET= BASE / "CNT_Master_Sheet_v3.csv"

# Criteria
P_THRESH      = 0.05
CRATIO_STRICT = 0.80
E_PASS_THRESH = 0.40

assert REPORT_CSV.exists(), f"Missing {REPORT_CSV}"
df = pd.read_csv(REPORT_CSV)

# Ensure needed columns exist
need = ["dataset","kind","E","I","Composite","C_p","C_ratio_robust",
        "C_ratio_robust_lo","C_ratio_robust_hi","source"]
for c in need:
    if c not in df.columns: df[c] = np.nan

# Derived gates
df["C_sig"]           = df["C_p"] <= P_THRESH
df["E_pass"]          = df["E"]   >= E_PASS_THRESH
df["C_strict_robust"] = df["C_ratio_robust"] < CRATIO_STRICT

# Explicit masks (no in-place overwrite bugs)
is_real  = df["kind"] == "real"
is_synth = df["kind"] == "synth"

m_strict  = is_real  & df["C_sig"] & df["C_strict_robust"]
m_lenient = is_real  & df["C_sig"] & df["E_pass"] & (~m_strict)
m_synth   = is_synth & df["C_sig"]

df["decision"] = "reject"
df.loc[m_strict,  "decision"] = "strict_real"
df.loc[m_lenient, "decision"] = "lenient_real"
df.loc[m_synth,   "decision"] = "synth_csig"

# Save compact decision table
keep = ["dataset","kind","Composite","E","I","C_p","C_sig",
        "C_ratio_robust","C_ratio_robust_lo","C_ratio_robust_hi",
        "C_strict_robust","E_pass","decision","source"]
dec = df[keep].copy().sort_values(
    ["decision","kind","Composite"], ascending=[True, True, False]
)
dec.to_csv(DECISION_CSV, index=False)

# Build JSON summary
payload = {
    "timestamp": datetime.now().isoformat(timespec="seconds"),
    "criteria": {
        "p_value_max": P_THRESH,
        "robust_ratio_max": CRATIO_STRICT,
        "E_pass_min": E_PASS_THRESH
    },
    "counts": {
        "strict_real": int(m_strict.sum()),
        "lenient_real": int(m_lenient.sum()),
        "synth_csig": int(m_synth.sum()),
        "total": int(len(df)),
    },
    "strict_real": df.loc[m_strict, "dataset"].tolist(),
    "lenient_real": df.loc[m_lenient, "dataset"].tolist(),
    "synth_csig":  df.loc[m_synth,  "dataset"].tolist(),
}
json.dump(payload, open(DECISION_JSON, "w"), indent=2)

# Markdown summary
def table(sub):
    if sub.empty: return "_(none)_"
    cols = ["dataset","Composite","E","C_p","C_ratio_robust","C_ratio_robust_lo","C_ratio_robust_hi"]
    cols = [c for c in cols if c in sub.columns]
    return sub[cols].to_string(index=False)

strict_tbl  = table(dec[dec["decision"]=="strict_real"])
lenient_tbl = table(dec[dec["decision"]=="lenient_real"])
synth_tbl   = table(dec[dec["decision"]=="synth_csig"])

with open(DECISION_MD, "w", encoding="utf-8") as f:
    f.write("# Phase-V Decision — v1.3r1 (corrected gating)\n\n")
    f.write(f"- Input: `{REPORT_CSV.name}`\n")
    f.write(f"- Criteria: p≤{P_THRESH}, robust C_ratio<{CRATIO_STRICT} (strict); lenient requires E≥{E_PASS_THRESH} & p≤{P_THRESH}\n\n")
    f.write(f"**Counts** — strict_real: {payload['counts']['strict_real']} | lenient_real: {payload['counts']['lenient_real']} | synth_Csig: {payload['counts']['synth_csig']}\n\n")
    f.write("## Strict (real)\n" + strict_tbl + "\n\n")
    f.write("## Lenient (real)\n" + lenient_tbl + "\n\n")
    f.write("## Synth (C_sig)\n" + synth_tbl + "\n\n")
    f.write("### Note\n- This revision fixes a labeling bug where rows meeting (E_pass ∧ C_sig) were left as `reject` if not already `strict`.\n")

# Bundle
with zipfile.ZipFile(BUNDLE_ZIP, "w", zipfile.ZIP_DEFLATED) as z:
    for p in [REPORT_CSV, REPORT_MD, DECISION_CSV, DECISION_MD, DECISION_JSON]:
        if Path(p).exists(): z.write(p, arcname=Path(p).name)
    for p in [GALLERY_PDF, ONEPAGER_CSV, MASTER_SHEET]:
        if Path(p).exists(): z.write(p, arcname=Path(p).name)

print("== Phase-V v1.3r1 Decision Pack ==")
print(" strict_real:", payload["counts"]["strict_real"])
print(" lenient_real:", payload["counts"]["lenient_real"])
print(" synth_Csig:", payload["counts"]["synth_csig"])
print("Wrote:")
print(" -", DECISION_CSV)
print(" -", DECISION_MD)
print(" -", DECISION_JSON)
print(" -", BUNDLE_ZIP)


== Phase-V v1.3r1 Decision Pack ==
 strict_real: 1
 lenient_real: 1
 synth_Csig: 0
Wrote:
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\PhaseV_Decision_v1p3r1.csv
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\PhaseV_Decision_v1p3r1.md
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\PhaseV_Decision_v1p3r1.json
 - C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars\mega_v1\phaseV_results\PhaseV_decision_bundle_v1p3r1.zip


In [39]:
# === Phase-V v1.3r1 → Ops Kit (action sheet, TODO, mini-runlist, zip bundle) ===
import pandas as pd, numpy as np, json, zipfile
from pathlib import Path
from datetime import datetime

BASE   = Path(r"C:\Users\caleb\CNT_Lab\artifacts\cnt_five_pillars")
PVR    = BASE / "mega_v1" / "phaseV_results"
PACK   = BASE / "packets_v3"

# Inputs
DECISION_CSV  = PVR / "PhaseV_Decision_v1p3r1.csv"
REPORT_CSV    = PVR / "phaseV_report_v1p3.csv"           # metrics table (v1p3)
MANIFEST_JSON = PACK / "packets_manifest_v3.json"        # dataset -> packet info (optional)
ONEPAGER_CSV  = PACK / "packets_onepager_index_v3.csv"   # optional
GALLERY_PDF   = PACK / "packets_gallery_v3.pdf"          # optional
MASTER_SHEET  = BASE / "CNT_Master_Sheet_v3.csv"         # optional

# Outputs
ACTION_SHEET  = PVR / "PhaseV_Action_Sheet_v1p3r1.csv"
TODO_MD       = PVR / "PhaseV_TODO_v1p3r1.md"
RUNLIST_MINI  = PVR / "runlist_phaseV_v1p3r1.csv"
BUNDLE_ZIP    = PVR / "PhaseV_ops_bundle_v1p3r1.zip"

assert DECISION_CSV.exists(), f"Missing {DECISION_CSV}"
assert REPORT_CSV.exists(),   f"Missing {REPORT_CSV}"

dec = pd.read_csv(DECISION_CSV)
rep = pd.read_csv(REPORT_CSV)

# Bring in packet paths if we have a manifest
manifest = {}
if MANIFEST_JSON.exists():
    with open(MANIFEST_JSON, "r", encoding="utf-8") as f:
        try:
            manifest = json.load(f)
        except Exception:
            manifest = {}

def packet_for(dataset):
    # Manifest may be {dataset: {...}} or a list of dicts—handle both
    if isinstance(manifest, dict):
        entry = manifest.get(dataset, {})
        if isinstance(entry, dict):
            return entry.get("packet") or entry.get("packet_path") or entry.get("packet_dir")
        # fallback: if manifest is mapping to string
        if isinstance(entry, str):
            return entry
    elif isinstance(manifest, list):
        for e in manifest:
            if isinstance(e, dict) and e.get("dataset") == dataset:
                return e.get("packet") or e.get("packet_path") or e.get("packet_dir")
    return np.nan

# Merge decisions with report to grab priority_rank, kind, source, etc.
cols_to_pull = [
    "dataset","kind","driver","priority_rank","Composite","E","I",
    "C_p","C_ratio","C_ratio_slow","C_ratio_best","C_ratio_robust",
    "C_ratio_robust_lo","C_ratio_robust_hi","source","phaseV_tags"
]
for c in cols_to_pull:
    if c not in rep.columns:
        rep[c] = np.nan
rep_slim = rep[cols_to_pull].copy()

df = dec.merge(rep_slim, on="dataset", how="left", suffixes=("",""))
df["packet"] = df["dataset"].map(packet_for)

# Keep only the actual picks (strict_real + lenient_real)
picks = df[df["decision"].isin(["strict_real","lenient_real"])].copy()

# Column order for action sheet
ordered_cols = [
    "dataset","decision","kind","driver","priority_rank","Composite",
    "E","I","C_p","C_sig","C_ratio_robust","C_ratio_robust_lo","C_ratio_robust_hi",
    "E_pass","C_strict_robust","phaseV_tags","source","packet"
]
for c in ordered_cols:
    if c not in picks.columns:
        picks[c] = np.nan
picks = picks[ordered_cols].sort_values(["decision","priority_rank","Composite"], ascending=[True, True, False])

# Save action sheet
picks.to_csv(ACTION_SHEET, index=False)

# Mini runlist for these picks only
runlist_cols = [
    "rank","dataset","kind","driver","priority_rank","Composite","packet","status","notes"
]
mini = pd.DataFrame({
    "rank": range(1, len(picks)+1),
    "dataset": picks["dataset"].values,
    "kind": picks["kind"].values,
    "driver": picks["driver"].values,
    "priority_rank": picks["priority_rank"].values,
    "Composite": picks["Composite"].values,
    "packet": picks["packet"].values,
    "status": ["queued"]*len(picks),
    "notes": [f"Phase-V v1.3r1 → {d}" for d in picks["decision"].values]
})
mini.to_csv(RUNLIST_MINI, index=False)

# Human-friendly TODO
stamp = datetime.now().strftime("%Y-%m-%d %H:%M")
with open(TODO_MD, "w", encoding="utf-8") as f:
    f.write("# Phase-V v1.3r1 — Execution TODO\n\n")
    f.write(f"_Generated: {stamp}_\n\n")
    f.write("## Picks\n")
    if picks.empty:
        f.write("- (none)\n\n")
    else:
        for _,r in picks.iterrows():
            f.write(f"- **{r['dataset']}** — `{r['decision']}`"
                    f" | E={r['E']:.3f} | p={r['C_p']:.3g} | robust={r['C_ratio_robust']}"
                    f" [{r['C_ratio_robust_lo']}, {r['C_ratio_robust_hi']}]"
                    f" | packet: {r['packet'] if pd.notna(r['packet']) else '(none)'}\n")
        f.write("\n")
    f.write("## Next steps\n")
    f.write("1) Confirm source tables and packet assets load cleanly.\n")
    f.write("2) Run replication script for strict; run lightweight confirmatory checks for lenient.\n")
    f.write("3) Update run tracker with outcomes, attach plots, and bump status.\n")
    f.write("4) Roll results into Daily Brief + Executive Brief if effect survives.\n")

# Bundle
with zipfile.ZipFile(BUNDLE_ZIP, "w", zipfile.ZIP_DEFLATED) as z:
    for p in [DECISION_CSV, REPORT_CSV, ACTION_SHEET, TODO_MD, RUNLIST_MINI]:
        if p.exists(): z.write(p, arcname=p.name)
    for p in [ONEPAGER_CSV, GALLERY_PDF, MASTER_SHEET]:
        if p.exists(): z.write(p, arcname=p.name)

print("== Phase-V v1.3r1 Ops Kit ==")
print("Action sheet:", ACTION_SHEET)
print("Mini runlist:", RUNLIST_MINI)
print("TODO:",        TODO_MD)
print("Bundle:",      BUNDLE_ZIP)
print("\nPicks:")
print(picks[["dataset","decision","E","C_p","C_ratio_robust","C_ratio_robust_lo","C_ratio_robust_hi","packet"]].to_string(index=False))


ValueError: columns overlap but no suffix specified: Index(['kind', 'Composite', 'E', 'I', 'C_p', 'C_ratio_robust',
       'C_ratio_robust_lo', 'C_ratio_robust_hi', 'source'],
      dtype='object')